# How I did the analysis

This is just a jupyter notebook containing all the python code I used to do my analysis.

I won't be uploading all the raw data I used, so you won't be able to reproduce the analysis
fully (sorry, but it's not my data to redistribute). But I will upload the final dataset I used
for my analysis, the list i got from Bookmyshow and some other stuff.

Pretty certain no one will go through the whole notebook, so will just summarise everything I 
did:</br>
<br />
* Found out which movies were released in the US from 2013 to August 2018, movies which had at least one American production company involved<br>
<br />
* Total number of releases in that period came up to 5,628.<br>
<br />
* Scraped the data from the-numbers.com, chose them because imdb 
    doesn't have the release dates for all movies for some reason.
    If I remember correctly, boxofficemojo does have the release
    dates, but in a less scraping-friendly format. So decided to go with the-numbers.com. Did use boxofficemojo.com and imdb.com for other things though.<br>
<br />
* Took out movies which earned less than USD 500K at the US box office in that period, keeps the focus of the analysis on mainstream Hollywood output as well as bigger independent movies made outside the Hollywood system.<br>
<br />
* BookMyShow very generously gave me a list of all the English-language movies that were released from 2013 to 2018. This will help us figure out which Hollywood movies were released here or not. There were a few errors in the list (for example, some movies that weren't released like the fifty shades movies were still given release dates of December XX, 2018 or December XX, 2017) but I think I've managed to deal with most of the errors. Used google, critics reviews and news reports of the time to cross-check some of the bookmyshow data. <br>
<br />
* Then I just matched movies from one list (movies that made more than USD 500K at US box office and had at least one American production company involved) to the Bookmyshow list (all English-language movies released in India) to figure out which movies were released or not. <br>
<br />
* Now if you look through the code I try to come up with my own way of matching titles. A colleague told me later I could have used some fuzzy match library to do it instead. Some of my code later uses the fuzzywuzzy library.<br>
<br />
* There was some manual intervention needed when titles couldn't be matched. If movie titles can't be matched, you can't use the bookmyshow list. For example, 'Pirates Of The Carribean: Dead Men Tell No Tales' was the title in the US, 'Pirates Of The Carribean: Salazar’s Revenge' was the title in India, so things like that needed to be accounted for.<br>
<br />
* After the matching was done, wanted to find the genres. First went with imdb's data dump at https://datasets.imdbws.com/ . Later realised that they just have 3 genres listed for each movie and those data dumps are limited in other ways too. Some movies could have as many as 5-6 genres on the main IMDB website. Used the IMDBpy library to get the data I needed from the site.<br>
<br />
* Deleted some movies that were not made primarily in the English language. Used IMDBpy to figure out which movies didn't have English listed as a language. Did some cross-checking here too.<br>
<br />
* Removed documentaries, short films, standup performances, promotional releases etc.<br>
<br />
* Got various production companies for each movie from the-numbers.com , did some online research to figure out which companies are part of the various movie studios and conglomerates. For example, there are three distributors associated with Lionsgate -- "Focus Features","Universal" and "Gramercy". Had to read up a bit to figure out things like that.<br />
<br />
* After all this, just did some basic number crunching to figure out what percentages of movies in terms of genre, US distributor etc. weren't released in India. <br>



In [7]:
#the urls and titles were taken from pages on the-numbers.com
#for example, this was the page for movies produced or co-produced by US companies and released in 2018
    # https://www.the-numbers.com/United-States/movies/year/2018

#will be using the urls later on to scrape pages from the-numbers.com 
    
import csv
from lxml import html

labels = ['number','title','url','year']

with open("data/titles_urls.csv", "w") as filex:   
    wr = csv.writer(filex, delimiter = ',' , quotechar = '"' )
    wr.writerow(labels)
    
file_open_location = 'data/us_movies_2013_2018.html'

with open(file_open_location) as filex:
    sourcex = filex.read()
    treex = html.document_fromstring(sourcex)

    rows = treex.xpath("/html/body/table//tr")
    
    number = 0
    
    for row in rows[1:]:
        number += 1
        title = row.xpath("td[1]/font/a/text()")[0]
        url = row.xpath("td[1]/font/a/@href")[0]
        year = row.xpath("td[7]/text()")[0]
        
        new_row = [number,title,url,year]

        with open("data/titles_urls.csv", "a") as filez:
            wr = csv.writer(filez, delimiter = ',' , quotechar = '"' )
            wr.writerow(new_row)
    
print('DONE AND DONE')

DONE AND DONE


In [ ]:
#domestic release schedules for the US were taken from pages on the-numbers.com
    #For example, this is the 2018 release schedule for movies in the US 
    #https://www.the-numbers.com/movies/release-schedule/2018


In [31]:
#in the cell blocks below, i'll be taking out the 2018 movies from the titles_urls csv 
    #the ones that were released after july 31, 2018
    #The thinking being that if a movie was released after that, it might take some time to come to India
    #Don't think things work like that anymore but just wanted to allow for that possibility
    #That if a movie was released after July 31 in the US but hasn't come to India by Sept, there is still
    # a possibility that it could be released in October
    #So july 31 is kind of a cut-off

   #Note - changed the cutoff later from july 31 to august 31, covers the whole summer period then
    
import pandas as pd

title_url_df = pd.read_csv("data/titles_urls.csv")

title_url_df.head()

number                                title  \
0       1                               Frozen   
1       2                           Iron Man 3   
2       3                      Despicable Me 2   
3       4  The Hobbit: The Desolation of Smaug   
4       5      The Hunger Games: Catching Fire   

                                                 url  year  
0  https://www.the-numbers.com/movie/Frozen-(2013...  2013  
1  https://www.the-numbers.com/movie/Iron-Man-3#t...  2013  
2  https://www.the-numbers.com/movie/Despicable-M...  2013  
3  https://www.the-numbers.com/movie/Hobbit-The-D...  2013  
4  https://www.the-numbers.com/movie/Hunger-Games...  2013

In [32]:
title_url_df.dtypes

number     int64
title     object
url       object
year       int64
dtype: object

In [33]:
title_url_df_2018 = title_url_df[title_url_df['year'] == 2018 ]

title_url_df_not_2018 = title_url_df[title_url_df['year'] != 2018 ]

In [34]:
title_url_df_2018.shape

(989, 4)

In [35]:
title_url_df_2018.head()

number                           title  \
5061    5062          Avengers: Infinity War   
5062    5063                   Black Panther   
5063    5064  Jurassic World: Fallen Kingdom   
5064    5065                   Incredibles 2   
5065    5066     Mission: Impossible—Fallout   

                                                    url  year  
5061  https://www.the-numbers.com/movie/Avengers-Inf...  2018  
5062  https://www.the-numbers.com/movie/Black-Panthe...  2018  
5063  https://www.the-numbers.com/movie/Jurassic-Wor...  2018  
5064  https://www.the-numbers.com/movie/Incredibles-...  2018  
5065  https://www.the-numbers.com/movie/Mission-Impo...  2018

In [36]:
num_lines = sum(1 for line in open('data/2018_titles_released_US_b4_july_31.txt'))
num_lines

655

In [37]:
with open("data/2018_titles_released_US_b4_july_31.txt", "r", encoding='utf-8') as ins:
    released_b4_july_31_list = []
    for line in ins:
        line = line.replace(u'\xa0', u' ')
        line = line.strip()
        released_b4_july_31_list.append(line)
        
released_b4_july_31_list[3:10]

['Blame',
 'Bob le flambeur',
 'Day of the Dead: Bloodline',
 "Devil's Gate",
 'Django',
 'Goldbuster',
 'Hanson and the Beast']

In [38]:
title_url_df_2018_b4_jul_31 = title_url_df_2018[title_url_df_2018['title']\
                                                .isin(released_b4_july_31_list)]
title_url_df_2018_b4_jul_31.shape

(350, 4)

In [30]:
pd.set_option('display.height', 500)
pd.set_option('display.max_rows', 500)

height has been deprecated.



In [41]:
title_url_df_2018_after_jul_31 = title_url_df_2018[~title_url_df_2018['title']\
                                                .isin(released_b4_july_31_list)]
title_url_df_2018_after_jul_31['title']

5069                                              The Meg
5082                                              The Nun
5083                                    Crazy Rich Asians
5086                                    Christopher Robin
5098                                      Xie Bu Ya Zheng
5099                                                Alpha
5104                                       BlacKkKlansman
5107                                The Spy Who Dumped Me
5110                                         The Predator
5113                                              Mile 22
5116                                          Slender Man
5119                                            Searching
5124                                    The Darkest Minds
5127                                           Peppermint
5129                                The Happytime Murders
5130                                       A Simple Favor
5138    The Guernsey Literary and Potato Peel Pie Society
5140          

In [42]:
title_url_df_shorter = pd.concat([title_url_df_not_2018, title_url_df_2018_b4_jul_31])

In [43]:
title_url_df_shorter.shape

(5411, 4)

In [44]:
title_url_df_shorter.head()

number                                title  \
0       1                               Frozen   
1       2                           Iron Man 3   
2       3                      Despicable Me 2   
3       4  The Hobbit: The Desolation of Smaug   
4       5      The Hunger Games: Catching Fire   

                                                 url  year  
0  https://www.the-numbers.com/movie/Frozen-(2013...  2013  
1  https://www.the-numbers.com/movie/Iron-Man-3#t...  2013  
2  https://www.the-numbers.com/movie/Despicable-M...  2013  
3  https://www.the-numbers.com/movie/Hobbit-The-D...  2013  
4  https://www.the-numbers.com/movie/Hunger-Games...  2013

In [45]:
title_url_df_shorter.to_csv('data/titles_urls_shorter.csv', index=False)

In [ ]:
#DO IT ALL OVER AGAIN, WE'RE AT LEAST 150 titles short, there should be at least 500, 
    #we only have 350 2018 titles

In [1]:
import pandas as pd

titles_urls_df = pd.read_csv('data/titles_urls_final.csv',encoding='iso-8859-1', converters={'number': str})
titles_urls_df.head()

number                                title  \
0   0001                               Frozen   
1   0002                           Iron Man 3   
2   0003                      Despicable Me 2   
3   0004  The Hobbit: The Desolation of Smaug   
4   0005      The Hunger Games: Catching Fire   

                                                 url  year  
0  https://www.the-numbers.com/movie/Frozen-(2013...  2013  
1  https://www.the-numbers.com/movie/Iron-Man-3#t...  2013  
2  https://www.the-numbers.com/movie/Despicable-M...  2013  
3  https://www.the-numbers.com/movie/Hobbit-The-D...  2013  
4  https://www.the-numbers.com/movie/Hunger-Games...  2013

In [2]:
titles_urls_df.shape

(5566, 4)

In [3]:
import os
os.mkdir('movie_pages')

In [5]:
import requests
import csv
from lxml import html
import re
from random import randint
import time
from datetime import datetime,date

headersx = {
"accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8",
"accept-encoding": "gzip, deflate, br",
"accept-language": "en-US,en;q=0.9,en-GB;q=0.8",
"cache-control": "no-cache",
"cookie": "IN_HASH=tab%3Dyear; gsScrollPos-236254187=; IN_HASH=tab%3Dyear; gsScrollPos-236254186=; gsScrollPos-236249552=0; gsScrollPos-236252306=0",
"pragma": "no-cache",
"upgrade-insecure-requests": "1",
"user-agent": "Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/69.0.3497.81 Safari/537.36"
}

for index,row in titles_urls_df.iterrows():
    url = row['url']
    number = row['number']
    year = row['year']
    
    try:
        responsex = requests.get(url, headers = headersx, timeout = 5)
        
    except requests.ConnectionError:
        print("OOPS!! Connection Error for title_number {}".format(number))
        print('this is the url: {}'.format(url))
        continue
    except requests.Timeout:
        print("OOPS!! Timeout Error for title_number {}".format(number))
        print('this is the url: {}'.format(url))
        continue
    except requests.RequestException:
        print("OOPS!! General Error for title_number {}".format(number))
        print('this is the url: {}'.format(url))
        continue
    except requests.HTTPError:
        print("OOPS!! HTTP Error for title_number {}".format(number))
        print('this is the url: {}'.format(url))
        continue
        
    else:
        delay = randint(5,9)

        time.sleep(delay)
        
        file_save_locationz =\
        'movie_pages/'+ number + '_' + str(year) + '.html'

        with open(file_save_locationz, 'wb') as f:
            f.write(responsex.content)

        print("done {}".format(file_save_locationz))
                    
print('done and done')

done movie_pages/0001_2013.html
done movie_pages/0002_2013.html
done movie_pages/0003_2013.html
done movie_pages/0004_2013.html
done movie_pages/0005_2013.html
done movie_pages/0006_2013.html
done movie_pages/0007_2013.html
done movie_pages/0008_2013.html
done movie_pages/0009_2013.html
done movie_pages/0010_2013.html
done movie_pages/0011_2013.html
done movie_pages/0012_2013.html
done movie_pages/0013_2013.html
done movie_pages/0014_2013.html
done movie_pages/0015_2013.html
done movie_pages/0016_2013.html
done movie_pages/0017_2013.html
done movie_pages/0018_2013.html
done movie_pages/0019_2013.html
done movie_pages/0020_2013.html
done movie_pages/0021_2013.html
done movie_pages/0022_2013.html
done movie_pages/0023_2013.html
done movie_pages/0024_2013.html
done movie_pages/0025_2013.html
done movie_pages/0026_2013.html
done movie_pages/0027_2013.html
done movie_pages/0028_2013.html
done movie_pages/0029_2013.html
done movie_pages/0030_2013.html
done movie_pages/0031_2013.html
done mov

done movie_pages/0254_2013.html
done movie_pages/0255_2013.html
done movie_pages/0256_2013.html
done movie_pages/0257_2013.html
done movie_pages/0258_2013.html
done movie_pages/0259_2013.html
done movie_pages/0260_2013.html
done movie_pages/0261_2013.html
done movie_pages/0262_2013.html
done movie_pages/0263_2013.html
done movie_pages/0264_2013.html
done movie_pages/0265_2013.html
done movie_pages/0266_2013.html
done movie_pages/0267_2013.html
done movie_pages/0268_2013.html
done movie_pages/0269_2013.html
done movie_pages/0270_2013.html
done movie_pages/0271_2013.html
done movie_pages/0272_2013.html
done movie_pages/0273_2013.html
done movie_pages/0274_2013.html
done movie_pages/0275_2013.html
done movie_pages/0276_2013.html
done movie_pages/0277_2013.html
done movie_pages/0278_2013.html
done movie_pages/0279_2013.html
done movie_pages/0280_2013.html
done movie_pages/0281_2013.html
done movie_pages/0282_2013.html
done movie_pages/0283_2013.html
done movie_pages/0284_2013.html
done mov

done movie_pages/0508_2013.html
done movie_pages/0509_2013.html
done movie_pages/0510_2013.html
done movie_pages/0511_2013.html
done movie_pages/0512_2013.html
done movie_pages/0513_2013.html
done movie_pages/0514_2013.html
done movie_pages/0515_2013.html
done movie_pages/0516_2013.html
done movie_pages/0517_2013.html
done movie_pages/0518_2013.html
done movie_pages/0519_2013.html
done movie_pages/0520_2013.html
done movie_pages/0521_2013.html
done movie_pages/0522_2013.html
done movie_pages/0523_2013.html
done movie_pages/0524_2013.html
done movie_pages/0525_2013.html
done movie_pages/0526_2013.html
done movie_pages/0527_2013.html
done movie_pages/0528_2013.html
done movie_pages/0529_2013.html
done movie_pages/0530_2013.html
done movie_pages/0531_2013.html
done movie_pages/0532_2013.html
done movie_pages/0533_2013.html
done movie_pages/0534_2013.html
done movie_pages/0535_2013.html
done movie_pages/0536_2013.html
done movie_pages/0537_2013.html
done movie_pages/0538_2013.html
done mov

done movie_pages/0765_2013.html
done movie_pages/0766_2013.html
done movie_pages/0767_2013.html
done movie_pages/0768_2013.html
done movie_pages/0769_2013.html
done movie_pages/0770_2013.html
done movie_pages/0771_2013.html
done movie_pages/0772_2013.html
done movie_pages/0773_2013.html
done movie_pages/0774_2013.html
done movie_pages/0775_2013.html
done movie_pages/0776_2013.html
done movie_pages/0777_2013.html
done movie_pages/0778_2013.html
done movie_pages/0779_2013.html
done movie_pages/0780_2013.html
done movie_pages/0781_2013.html
done movie_pages/0782_2013.html
done movie_pages/0783_2013.html
done movie_pages/0784_2013.html
done movie_pages/0785_2013.html
done movie_pages/0786_2013.html
done movie_pages/0787_2014.html
done movie_pages/0788_2014.html
done movie_pages/0789_2014.html
done movie_pages/0790_2014.html
done movie_pages/0791_2014.html
done movie_pages/0792_2014.html
done movie_pages/0793_2014.html
done movie_pages/0794_2014.html
done movie_pages/0795_2014.html
done mov

done movie_pages/1022_2014.html
done movie_pages/1023_2014.html
done movie_pages/1024_2014.html
done movie_pages/1025_2014.html
done movie_pages/1026_2014.html
done movie_pages/1027_2014.html
done movie_pages/1028_2014.html
done movie_pages/1029_2014.html
done movie_pages/1030_2014.html
done movie_pages/1031_2014.html
done movie_pages/1032_2014.html
done movie_pages/1033_2014.html
done movie_pages/1034_2014.html
done movie_pages/1035_2014.html
done movie_pages/1036_2014.html
done movie_pages/1037_2014.html
done movie_pages/1038_2014.html
done movie_pages/1039_2014.html
done movie_pages/1040_2014.html
done movie_pages/1041_2014.html
done movie_pages/1042_2014.html
done movie_pages/1043_2014.html
done movie_pages/1044_2014.html
done movie_pages/1045_2014.html
done movie_pages/1046_2014.html
done movie_pages/1047_2014.html
done movie_pages/1048_2014.html
done movie_pages/1049_2014.html
done movie_pages/1050_2014.html
done movie_pages/1051_2014.html
done movie_pages/1052_2014.html
done mov

...

done movie_pages/4354_2017.html
done movie_pages/4355_2017.html
done movie_pages/4356_2017.html
done movie_pages/4357_2017.html
done movie_pages/4358_2017.html
done movie_pages/4359_2017.html
done movie_pages/4360_2017.html
done movie_pages/4361_2017.html
done movie_pages/4362_2017.html
done movie_pages/4363_2017.html
done movie_pages/4364_2017.html
done movie_pages/4365_2017.html
done movie_pages/4366_2017.html
done movie_pages/4367_2017.html
done movie_pages/4368_2017.html
done movie_pages/4369_2017.html
done movie_pages/4370_2017.html
done movie_pages/4371_2017.html
done movie_pages/4372_2017.html
done movie_pages/4373_2017.html
done movie_pages/4374_2017.html
done movie_pages/4375_2017.html
done movie_pages/4376_2017.html
done movie_pages/4377_2017.html
done movie_pages/4378_2017.html
done movie_pages/4379_2017.html
done movie_pages/4380_2017.html
done movie_pages/4381_2017.html
done movie_pages/4382_2017.html
done movie_pages/4383_2017.html
done movie_pages/4384_2017.html
done mov

done movie_pages/4611_2017.html
done movie_pages/4612_2017.html
done movie_pages/4613_2017.html
done movie_pages/4614_2017.html
done movie_pages/4615_2017.html
done movie_pages/4616_2017.html
done movie_pages/4617_2017.html
done movie_pages/4618_2017.html
done movie_pages/4619_2017.html
done movie_pages/4620_2017.html
done movie_pages/4621_2017.html
done movie_pages/4622_2017.html
done movie_pages/4623_2017.html
done movie_pages/4624_2017.html
done movie_pages/4625_2017.html
done movie_pages/4626_2017.html
done movie_pages/4627_2017.html
done movie_pages/4628_2017.html
done movie_pages/4629_2017.html
done movie_pages/4630_2017.html
done movie_pages/4631_2017.html
done movie_pages/4632_2017.html
done movie_pages/4633_2017.html
done movie_pages/4634_2017.html
done movie_pages/4635_2017.html
done movie_pages/4636_2017.html
done movie_pages/4637_2017.html
done movie_pages/4638_2017.html
done movie_pages/4639_2017.html
done movie_pages/4640_2017.html
done movie_pages/4641_2017.html
done mov

done movie_pages/4865_2017.html
done movie_pages/4866_2017.html
done movie_pages/4867_2017.html
done movie_pages/4868_2017.html
done movie_pages/4869_2017.html
done movie_pages/4870_2017.html
done movie_pages/4871_2017.html
done movie_pages/4872_2017.html
done movie_pages/4873_2017.html
done movie_pages/4874_2017.html
done movie_pages/4875_2017.html
done movie_pages/4876_2017.html
done movie_pages/4877_2017.html
done movie_pages/4878_2017.html
done movie_pages/4879_2017.html
done movie_pages/4880_2017.html
done movie_pages/4881_2017.html
done movie_pages/4882_2017.html
done movie_pages/4883_2017.html
done movie_pages/4884_2017.html
done movie_pages/4885_2017.html
done movie_pages/4886_2017.html
done movie_pages/4887_2017.html
done movie_pages/4888_2017.html
done movie_pages/4889_2017.html
done movie_pages/4890_2017.html
done movie_pages/4891_2017.html
done movie_pages/4892_2017.html
done movie_pages/4893_2017.html
done movie_pages/4894_2017.html
done movie_pages/4895_2017.html
done mov

done movie_pages/5122_2018.html
done movie_pages/5123_2018.html
done movie_pages/5124_2018.html
done movie_pages/5125_2018.html
done movie_pages/5126_2018.html
done movie_pages/5127_2018.html
done movie_pages/5128_2018.html
done movie_pages/5129_2018.html
done movie_pages/5130_2018.html
done movie_pages/5131_2018.html
done movie_pages/5132_2018.html
done movie_pages/5133_2018.html
done movie_pages/5134_2018.html
done movie_pages/5135_2018.html
done movie_pages/5136_2018.html
done movie_pages/5137_2018.html
done movie_pages/5138_2018.html
done movie_pages/5139_2018.html
done movie_pages/5140_2018.html
done movie_pages/5141_2018.html
done movie_pages/5142_2018.html
done movie_pages/5143_2018.html
done movie_pages/5144_2018.html
done movie_pages/5145_2018.html
done movie_pages/5146_2018.html
done movie_pages/5147_2018.html
done movie_pages/5148_2018.html
done movie_pages/5149_2018.html
done movie_pages/5150_2018.html
done movie_pages/5151_2018.html
done movie_pages/5152_2018.html
done mov

done movie_pages/5379_2018.html
done movie_pages/5380_2018.html
done movie_pages/5381_2018.html
done movie_pages/5382_2018.html
done movie_pages/5383_2018.html
done movie_pages/5384_2018.html
done movie_pages/5385_2018.html
done movie_pages/5386_2018.html
done movie_pages/5387_2018.html
done movie_pages/5388_2018.html
done movie_pages/5389_2018.html
done movie_pages/5390_2018.html
done movie_pages/5391_2018.html
done movie_pages/5392_2018.html
done movie_pages/5393_2018.html
done movie_pages/5394_2018.html
done movie_pages/5395_2018.html
done movie_pages/5396_2018.html
done movie_pages/5397_2018.html
done movie_pages/5398_2018.html
done movie_pages/5399_2018.html
done movie_pages/5400_2018.html
done movie_pages/5401_2018.html
done movie_pages/5402_2018.html
done movie_pages/5403_2018.html
done movie_pages/5404_2018.html
done movie_pages/5405_2018.html
done movie_pages/5406_2018.html
done movie_pages/5407_2018.html
done movie_pages/5408_2018.html
done movie_pages/5409_2018.html
done mov

In [25]:
import glob
import csv
from lxml import html
import re
from datetime import datetime

labels = ['number','year','title','domestic_box_office','international_box_office',
          'production_budget','domestic_release_date','domestic_distributor','mpaa_rating','franchise',
          'source','genre','production_method','creative_type','production_companies',
          'production_countries']

with open("data/scraped_data.csv", "w") as filex:   
    wr = csv.writer(filex, delimiter = ',' , quotechar = '"' )
    wr.writerow(labels)

search_string = 'movie_pages/*_*.html'

for filename in glob.glob(search_string):
    
    print(filename)
    
    numberx = (re.findall(r"movie_pages/(\d{4})_20\d{2}.html", filename))[0]
    
    with open(filename, encoding='utf-8') as filex:
        
        sourcex = filex.read()
        treex = html.document_fromstring(sourcex)
        
        title_year_raw = treex.xpath("//*[@id='main']/div/h1/text()")[0]
        
        year = (re.findall(r".*\s\((.*)\)", title_year_raw))[0]
        
        title = (re.findall(r"(.*)\s\(.*\)", title_year_raw))[0]
        
        domestic_box_office_raw = treex.xpath("//*[@id='movie_finances']/tr[2]/td[2]/text()")[0]
        domestic_box_office = domestic_box_office_raw.replace(",","").replace("$","")
        domestic_box_office = int(domestic_box_office)
            
        #sometimes domestic box office can be zero
        
        international_box_office_raw = treex.xpath("//*[@id='movie_finances']/tr[2]/td[2]/text()")[0]
        international_box_office = international_box_office_raw.replace(",","").replace("$","")
        international_box_office = int(international_box_office)
        
        try:
            production_budget_raw = treex.xpath\
("//*[@id='summary']//b[contains(text(),'Production') and contains(text(),'Budget')]/following::td[1]/text()")[0]
        
        except:
            print('problem with production budget on filename {}'.format(filename))
            production_budget = 0
            
        else:
            production_budget = production_budget_raw.replace(",","").replace("$","")
            production_budget = int(production_budget)
            
        
        domestic_release_date = ""

        for number in [1,2,3,4]:
            string =\
"//*[@id='summary']//b[contains(text(),'Domestic') and contains(text(),'Releases')]/following::td[1]/text()["+\
str(number) + "]"
            try:
                domestic_release_date_raw = treex.xpath(string)[0]
            except:
                continue
            else:
                if 'Wide' in domestic_release_date_raw:
                    try:
                        domestic_release_date = (re.findall(r"(.*)\,.*", domestic_release_date_raw))[0]
                        domestic_release_date = domestic_release_date[:-2]
                        domestic_release_date = domestic_release_date + " " + year
                    
                        domestic_release_date = datetime.strptime(domestic_release_date, '%B %d %Y')\
                                                        .strftime('%Y-%m-%d')
                    except:
                        domestic_release_date = ""
                        
                    stringx = \
"//*[@id='summary']//b[contains(text(),'Domestic') and contains(text(),'Releases')]/following::td[1]/a["+\
str(number) + "]/text()"
                    try:
                        domestic_distributor_raw = treex.xpath(stringx)[0]
                    except:
                        domestic_distributor = ""
                    else:
                        domestic_distributor = domestic_distributor_raw
                            
                        
        if domestic_release_date == "":
            
            for number in [1,2,3,4]:
                string =\
"//*[@id='summary']//b[contains(text(),'Domestic') and contains(text(),'Releases')]/following::td[1]/text()["+\
    str(number) + "]"
                try:
                    domestic_release_date_raw = treex.xpath(string)[0]
                except:
                    continue
                else:
                    if 'Limited' in domestic_release_date_raw:
                        try:
                            domestic_release_date = (re.findall(r"(.*)\,.*", domestic_release_date_raw))[0]
                            domestic_release_date = domestic_release_date[:-2]
                            domestic_release_date = domestic_release_date + " " + year
                        
                            domestic_release_date = datetime.strptime(domestic_release_date, '%B %d %Y')\
                                                            .strftime('%Y-%m-%d')
                        except:
                            domestic_release_date = ""
                            
                        stringz = \
"//*[@id='summary']//b[contains(text(),'Domestic') and contains(text(),'Releases')]/following::td[1]/a["+\
str(number) + "]/text()"
                        try:
                            domestic_distributor_raw = treex.xpath(stringz)[0]
                        except:
                            domestic_distributor = ""
                        else:
                            domestic_distributor = domestic_distributor_raw
                            
                            
        try:
            mpaa_rating =\
                treex.xpath\
("//*[@id='summary']//b[contains(text(),'MPAA') and contains(text(),'Rating')]/following::td[1]/a/text()")[0]
        except:
            mpaa_rating = ""
    
        try:
            franchise_raw = treex.xpath\
("//*[@id='summary']//b[contains(text(),'Franchise')]/following::td[1]/a/text()")[0]
        
        except:
            franchise = ""
        else:
            franchise = franchise_raw
        
        try:
            source = treex.xpath\
    ("//*[@id='summary']//b[contains(text(),'Source')]/following::td[1]/a/text()")[0]
        except:
            source = ""
        
        try:
            genre = treex.xpath\
    ("//*[@id='summary']//b[contains(text(),'Genre')]/following::td[1]/a/text()")[0]
        except:
            genre = ""
            
        try:
            production_method = treex.xpath\
    ("//*[@id='summary']//b[contains(text(),'Production') and contains(text(),'Method')]/following::td[1]/a/text()")[0]
        except:
            production_method = ""
        
        try:
            creative_type = treex.xpath\
    ("//*[@id='summary']//b[contains(text(),'Creative') and contains(text(),'Type')]/following::td[1]/a/text()")[0]
        except:
            creative_type = ""
            
        try:
            production_companies_raw = treex.xpath\
("//*[@id='summary']//b[contains(text(),'Production') and contains(text(),'Companies')]/following::td[1]//a")
            production_companies_list = []
            for a in production_companies_raw:
                production_company_single = a.xpath("text()")[0]
                production_companies_list.append(production_company_single)
                
        except:
            production_companies = ""
        else:
            production_companies = ",".join(production_companies_list)

        
        try:
            production_countries_raw = treex.xpath\
("//*[@id='summary']//b[contains(text(),'Production') and contains(text(),'Countries')]/following::td[1]//a")
            production_countries_list = []
            for a in production_countries_raw:
                production_country_single = a.xpath("text()")[0]
                production_countries_list.append(production_country_single)

        except:
            production_countries = ""
            
        else:
            production_countries = ",".join(production_countries_list)
        
        new_row = [numberx, year, title, domestic_box_office, international_box_office,
                   production_budget, domestic_release_date, domestic_distributor, mpaa_rating, franchise,
                   source, genre, production_method, creative_type, production_companies,
                   production_countries]

        with open("data/scraped_data.csv", "a") as filez:
            wr = csv.writer(filez, delimiter = ',' , quotechar = '"' )
            wr.writerow(new_row)
    
print("DONE AND DONE")

movie_pages/4025_2017.html
problem with production budget on filename movie_pages/4025_2017.html
movie_pages/0269_2013.html
problem with production budget on filename movie_pages/0269_2013.html
movie_pages/4428_2017.html
problem with production budget on filename movie_pages/4428_2017.html
movie_pages/0650_2013.html
problem with production budget on filename movie_pages/0650_2013.html
movie_pages/1882_2015.html
problem with production budget on filename movie_pages/1882_2015.html
movie_pages/1187_2014.html
problem with production budget on filename movie_pages/1187_2014.html
movie_pages/2230_2015.html
problem with production budget on filename movie_pages/2230_2015.html
movie_pages/0559_2013.html
problem with production budget on filename movie_pages/0559_2013.html
movie_pages/0164_2013.html
movie_pages/1451_2014.html
problem with production budget on filename movie_pages/1451_2014.html
movie_pages/4608_2017.html
problem with production budget on filename movie_pages/4608_2017.html
mov

movie_pages/2772_2015.html
movie_pages/3157_2016.html
problem with production budget on filename movie_pages/3157_2016.html
movie_pages/1476_2014.html
problem with production budget on filename movie_pages/1476_2014.html
movie_pages/5240_2018.html
problem with production budget on filename movie_pages/5240_2018.html
movie_pages/2714_2015.html
movie_pages/0504_2013.html
problem with production budget on filename movie_pages/0504_2013.html
movie_pages/2337_2015.html
movie_pages/2927_2016.html
movie_pages/4406_2017.html
problem with production budget on filename movie_pages/4406_2017.html
movie_pages/0870_2014.html
movie_pages/1173_2014.html
problem with production budget on filename movie_pages/1173_2014.html
movie_pages/1362_2014.html
problem with production budget on filename movie_pages/1362_2014.html
movie_pages/1370_2014.html
problem with production budget on filename movie_pages/1370_2014.html
movie_pages/0618_2013.html
problem with production budget on filename movie_pages/0618_20

movie_pages/0908_2014.html
movie_pages/1125_2014.html
movie_pages/1587_2014.html
problem with production budget on filename movie_pages/1587_2014.html
movie_pages/0323_2013.html
problem with production budget on filename movie_pages/0323_2013.html
movie_pages/3293_2016.html
problem with production budget on filename movie_pages/3293_2016.html
movie_pages/2121_2015.html
problem with production budget on filename movie_pages/2121_2015.html
movie_pages/5367_2018.html
problem with production budget on filename movie_pages/5367_2018.html
movie_pages/5296_2018.html
problem with production budget on filename movie_pages/5296_2018.html
movie_pages/4278_2017.html
problem with production budget on filename movie_pages/4278_2017.html
movie_pages/1245_2014.html
problem with production budget on filename movie_pages/1245_2014.html
movie_pages/5125_2018.html
problem with production budget on filename movie_pages/5125_2018.html
movie_pages/4139_2017.html
problem with production budget on filename mov

problem with production budget on filename movie_pages/4024_2017.html
movie_pages/0039_2013.html
movie_pages/1805_2015.html
movie_pages/0052_2013.html
movie_pages/4560_2017.html
problem with production budget on filename movie_pages/4560_2017.html
movie_pages/2124_2015.html
problem with production budget on filename movie_pages/2124_2015.html
movie_pages/5306_2018.html
problem with production budget on filename movie_pages/5306_2018.html
movie_pages/1045_2014.html
problem with production budget on filename movie_pages/1045_2014.html
movie_pages/0873_2014.html
problem with production budget on filename movie_pages/0873_2014.html
movie_pages/4832_2017.html
problem with production budget on filename movie_pages/4832_2017.html
movie_pages/1753_2015.html
movie_pages/5383_2018.html
problem with production budget on filename movie_pages/5383_2018.html
movie_pages/5501_2018.html
problem with production budget on filename movie_pages/5501_2018.html
movie_pages/1548_2014.html
problem with produc

problem with production budget on filename movie_pages/1157_2014.html
movie_pages/4770_2017.html
problem with production budget on filename movie_pages/4770_2017.html
movie_pages/4446_2017.html
problem with production budget on filename movie_pages/4446_2017.html
movie_pages/0160_2013.html
movie_pages/2936_2016.html
movie_pages/2956_2016.html
movie_pages/5356_2018.html
problem with production budget on filename movie_pages/5356_2018.html
movie_pages/1477_2014.html
problem with production budget on filename movie_pages/1477_2014.html
movie_pages/4831_2017.html
problem with production budget on filename movie_pages/4831_2017.html
movie_pages/1360_2014.html
problem with production budget on filename movie_pages/1360_2014.html
movie_pages/5402_2018.html
problem with production budget on filename movie_pages/5402_2018.html
movie_pages/0503_2013.html
problem with production budget on filename movie_pages/0503_2013.html
movie_pages/3016_2016.html
movie_pages/3143_2016.html
problem with produc

...

problem with production budget on filename movie_pages/4212_2017.html
movie_pages/3678_2016.html
problem with production budget on filename movie_pages/3678_2016.html
movie_pages/2316_2015.html
problem with production budget on filename movie_pages/2316_2015.html
movie_pages/1118_2014.html
movie_pages/0513_2013.html
problem with production budget on filename movie_pages/0513_2013.html
movie_pages/4087_2017.html
problem with production budget on filename movie_pages/4087_2017.html
movie_pages/1745_2015.html
movie_pages/1165_2014.html
problem with production budget on filename movie_pages/1165_2014.html
movie_pages/1975_2015.html
problem with production budget on filename movie_pages/1975_2015.html
movie_pages/0262_2013.html
problem with production budget on filename movie_pages/0262_2013.html
movie_pages/4522_2017.html
problem with production budget on filename movie_pages/4522_2017.html
movie_pages/0784_2013.html
problem with production budget on filename movie_pages/0784_2013.html
mov

movie_pages/3878_2017.html
movie_pages/5437_2018.html
problem with production budget on filename movie_pages/5437_2018.html
movie_pages/0312_2013.html
problem with production budget on filename movie_pages/0312_2013.html
movie_pages/1864_2015.html
movie_pages/2707_2015.html
problem with production budget on filename movie_pages/2707_2015.html
movie_pages/4125_2017.html
problem with production budget on filename movie_pages/4125_2017.html
movie_pages/0097_2013.html
movie_pages/4034_2017.html
problem with production budget on filename movie_pages/4034_2017.html
movie_pages/4207_2017.html
problem with production budget on filename movie_pages/4207_2017.html
movie_pages/4960_2017.html
problem with production budget on filename movie_pages/4960_2017.html
movie_pages/4844_2017.html
problem with production budget on filename movie_pages/4844_2017.html
movie_pages/3809_2016.html
problem with production budget on filename movie_pages/3809_2016.html
movie_pages/1776_2015.html
movie_pages/4549_20

movie_pages/2080_2015.html
problem with production budget on filename movie_pages/2080_2015.html
movie_pages/2932_2016.html
movie_pages/4461_2017.html
problem with production budget on filename movie_pages/4461_2017.html
movie_pages/1985_2015.html
problem with production budget on filename movie_pages/1985_2015.html
movie_pages/1007_2014.html
problem with production budget on filename movie_pages/1007_2014.html
movie_pages/2032_2015.html
problem with production budget on filename movie_pages/2032_2015.html
movie_pages/0972_2014.html
problem with production budget on filename movie_pages/0972_2014.html
movie_pages/1361_2014.html
problem with production budget on filename movie_pages/1361_2014.html
movie_pages/1993_2015.html
problem with production budget on filename movie_pages/1993_2015.html
movie_pages/1911_2015.html
problem with production budget on filename movie_pages/1911_2015.html
movie_pages/2325_2015.html
problem with production budget on filename movie_pages/2325_2015.html
mov

movie_pages/1031_2014.html
problem with production budget on filename movie_pages/1031_2014.html
movie_pages/1901_2015.html
problem with production budget on filename movie_pages/1901_2015.html
movie_pages/2206_2015.html
movie_pages/2039_2015.html
problem with production budget on filename movie_pages/2039_2015.html
movie_pages/0122_2013.html
movie_pages/5052_2017.html
problem with production budget on filename movie_pages/5052_2017.html
movie_pages/2887_2016.html
movie_pages/1557_2014.html
problem with production budget on filename movie_pages/1557_2014.html
movie_pages/3072_2016.html
movie_pages/2990_2016.html
movie_pages/3276_2016.html
problem with production budget on filename movie_pages/3276_2016.html
movie_pages/1937_2015.html
problem with production budget on filename movie_pages/1937_2015.html
movie_pages/3032_2016.html
movie_pages/3921_2017.html
problem with production budget on filename movie_pages/3921_2017.html
movie_pages/5493_2018.html
problem with production budget on f

movie_pages/0104_2013.html
movie_pages/0485_2013.html
problem with production budget on filename movie_pages/0485_2013.html
movie_pages/0649_2013.html
problem with production budget on filename movie_pages/0649_2013.html
movie_pages/4535_2017.html
problem with production budget on filename movie_pages/4535_2017.html
movie_pages/0916_2014.html
problem with production budget on filename movie_pages/0916_2014.html
movie_pages/4557_2017.html
problem with production budget on filename movie_pages/4557_2017.html
movie_pages/1552_2014.html
problem with production budget on filename movie_pages/1552_2014.html
movie_pages/2276_2015.html
movie_pages/4373_2017.html
problem with production budget on filename movie_pages/4373_2017.html
movie_pages/4491_2017.html
problem with production budget on filename movie_pages/4491_2017.html
movie_pages/3660_2016.html
problem with production budget on filename movie_pages/3660_2016.html
movie_pages/2398_2015.html
problem with production budget on filename mov

In [26]:
import pandas as pd

scraped_data_df = pd.read_csv('data/scraped_data.csv', converters={'number': str})
scraped_data_df.head()

number  year                                  title  domestic_box_office  \
0   4025  2017                          Brad’s Status              2133158   
1   0269  2013  Free Angela & All Political Prisoners               129102   
2   4428  2017                          The Long Home                    0   
3   0650  2013                         Big Ass Spider                    0   
4   1882  2015                             Apparition                    0   

   international_box_office  production_budget domestic_release_date  \
0                   2133158                  0            2017-09-15   
1                    129102                  0            2013-04-05   
2                         0                  0                   NaN   
3                         0                  0            2013-10-18   
4                         0                  0                   NaN   

        domestic_distributor mpaa_rating franchise  \
0         Annapurna Pictures           R       NaN   
1  CODEBLACK Films/Lionsgate   Not Rated       NaN   
2  CODEBLACK Films/Lionsgate           R       NaN   
3        Epic Pictures Group       PG-13       NaN   
4        Epic Pictures Group   Not Rated       NaN   

                              source              genre production_method  \
0                Original Screenplay             Comedy       Live Action   
1          Based on Real Life Events        Documentary       Live Action   
2  Based on Fiction Book/Short Story              Drama       Live Action   
3                Original Screenplay             Comedy       Live Action   
4                Original Screenplay  Thriller/Suspense       Live Action   

          creative_type                               production_companies  \
0  Contemporary Fiction                                                NaN   
1               Factual  REALside Productions,De Films en Aiguille,Dire...   
2    Historical Fiction                         Rabbit Bandini Productions   
3       Science Fiction                                Epic Pictures Group   
4               Fantasy                                                NaN   

  production_countries  
0        United States  
1        United States  
2        United States  
3        United States  
4        United States

In [27]:
scraped_data_df.shape

(5566, 16)

In [28]:
scraped_data_df.dtypes

number                      object
year                         int64
title                       object
domestic_box_office          int64
international_box_office     int64
production_budget            int64
domestic_release_date       object
domestic_distributor        object
mpaa_rating                 object
franchise                   object
source                      object
genre                       object
production_method           object
creative_type               object
production_companies        object
production_countries        object
dtype: object

In [37]:
len(scraped_data_df)

5566

In [47]:
len(scraped_data_df[scraped_data_df['domestic_box_office'] >= 500000])

1078

In [48]:
scraped_data_df_500000 = scraped_data_df[scraped_data_df['domestic_box_office'] >= 500000]

In [49]:
scraped_data_df_500000.to_csv('data/scraped_data_500000.csv', index=False)

In [ ]:
#by keeping the minimum US box office at half million, ensure big arthouse/indie movies aren't filtered out

In [170]:
scraped_data_df_500000 = pd.read_csv("data/scraped_data_500000.csv")

In [171]:
scraped_data_df_500000.head()

number  year                  title  domestic_box_office  \
0    4025  2017          Brad’s Status              2133158   
1     164  2013               The East              2274649   
2    5442  2018  The Catcher Was A Spy               714205   
3    3062  2016            Miles Ahead              2610896   
4      12  2013            World War Z            202359711   

   international_box_office  production_budget domestic_release_date  \
0                   2133158                  0            2017-09-15   
1                   2274649            6500000            2013-05-31   
2                    714205                  0            2018-06-22   
3                   2610896                  0            2016-04-01   
4                 202359711          190000000            2013-06-21   

     domestic_distributor mpaa_rating    franchise  \
0      Annapurna Pictures           R          NaN   
1         Fox Searchlight       PG-13          NaN   
2               IFC Films           R          NaN   
3  Sony Pictures Classics           R          NaN   
4      Paramount Pictures       PG-13  World War Z   

                              source   genre production_method  \
0                Original Screenplay  Comedy       Live Action   
1                Original Screenplay   Drama       Live Action   
2  Based on Fiction Book/Short Story   Drama       Live Action   
3          Based on Real Life Events   Drama       Live Action   
4  Based on Fiction Book/Short Story  Action       Live Action   

          creative_type                               production_companies  \
0  Contemporary Fiction                                                NaN   
1  Contemporary Fiction                                   Scott Free Films   
2    Historical Fiction  Animus Films,PalmStar Media,Serena Films,Windy...   
3         Dramatization  Bifrost Pictures,Sony Pictures Classics,Miles ...   
4       Science Fiction  Skydance Productions,Hemisphere Media Capital,...   

  production_countries  
0        United States  
1        United States  
2        United States  
3        United States  
4        United States

In [172]:
scraped_data_df_500000.dtypes

number                       int64
year                         int64
title                       object
domestic_box_office          int64
international_box_office     int64
production_budget            int64
domestic_release_date       object
domestic_distributor        object
mpaa_rating                 object
franchise                   object
source                      object
genre                       object
production_method           object
creative_type               object
production_companies        object
production_countries        object
dtype: object

In [173]:
#number of movies in this list for which we don't have estimates of production budgets 

len(scraped_data_df_500000[scraped_data_df_500000['production_budget'] == 0])

320

In [174]:
bms_release_list = pd.read_csv("data/bookmyshow_list.csv")
bms_release_list

Release_Year                                EventGroup_strTitle  \
0             2013                    Hansel And Gretel Witch Hunters   
1             2013                              7 Days In Slow Motion   
2             2013                                     Chinese Zodiac   
3             2013                                     The Impossible   
4             2013                                   Tropical Races 3   
5             2013                Universal Soldier: Day Of Reckoning   
6             2013                                      Comic Vampire   
7             2013                              Dinosaur Reappearance   
8             2013                Roller Coaster & Dinosaur Adventure   
9             2013                                     Gangster Squad   
10            2013                                    Les Miserables.   
11            2013                                      Promised Land   
12            2013                                        Broken City   
13            2013                                     The Last Stand   
14            2013                                         This Is 40   
15            2013                                       End of Watch   
16            2013                                     Dance Of Death   
17            2013            Strange Stories & Dinosaur Reappearance   
18            2013                                Bullet To The Head    
19            2013                                Here Comes the Boom   
20            2013                                Midnight`s Children   
21            2013                                             Parker   
22            2013                                               Argo   
23            2013                                            Lincoln   
24            2013                                               Mama   
25            2013                                Beautiful Creatures   
26            2013                     Forest Adventure & Ice Fighter   
27            2013                  Forest Adventure & Roller Coaster   
28            2013                       Ice Fighter & Roller Coaster   
29            2013                    The Perks Of Being A Wallflower   
30            2013                                   Zero Dark Thirty   
31            2013                             A Good Day To Die Hard   
32            2013                                         Dark Skies   
33            2013                            Silver Linings Playbook   
34            2013                                          Pinocchio   
35            2013                                             Flight   
36            2013                   Haunted Graves + Night With Toys   
37            2013                             Jack The Giant Slayer    
38            2013                Night At Toy Store + Roller Coaster   
39            2013                        Pharaoh Queen +Time Machine   
40            2013            Predator Attack + Prehistoric Adventure   
41            2013                        Rescue And Path Finder Snow   
42            2013                                          Dandelion   
43            2013            Prehistoric Adventure + Night With Toys   
44            2013                                          21 & Over   
45            2013                           All I Want Is Everything   
46            2013                      Flying Swords of Dragon Gate    
47            2013                        Oz The Great And Powerful     
48            2013                                             Snitch   
49            2013                                             Zarafa   
50            2013                                     Texas Chainsaw   
51            2013                    The Incredible Burt Wonderstone   
52            2013                                         The Master   
53            2013                                     Identity 

In [175]:
bms_release_list.dtypes

Release_Year             int64
EventGroup_strTitle     object
Event_dtmReleaseDate    object
dtype: object

In [176]:
bms_release_list.rename(columns={'Release_Year': 'release_year',
                                  'EventGroup_strTitle':'title',
                                  'Event_dtmReleaseDate':'release_date'}, inplace=True)

In [177]:
bms_release_list.dtypes

release_year     int64
title           object
release_date    object
dtype: object

In [178]:
#useful snippets
#scraped_data_df_500000.loc[scraped_data_df_500000['title'].str.contains(":")]
#len(scraped_data_df[(scraped_data_df['international_box_office'] == 0) &
  #                 (scraped_data_df['domestic_box_office'] == 0)])
#     scraped_data_df.loc[(scraped_data_df['domestic_box_office'] != 0) &
#                    (scraped_data_df['production_budget'] == 0)]

In [179]:
bms_release_list.loc[india_release_list['title'].str.contains("Pirates")]

release_year                                        title  \
77            2013              Pirates and Roller Coaster Ride   
105           2013                           Predator & Pirates   
557           2014                                      Pirates   
712           2014                     Pirates and Wild Coaster   
886           2015                 Pirates and Crazy Snowmobile   
1608          2017  Pirates of the Caribbean: Salazar`s Revenge   

             release_date  
77    24/04/2013 00:00:00  
105   29/05/2013 00:00:00  
557   01/04/2014 00:00:00  
712   01/09/2014 00:00:00  
886   15/02/2015 00:00:00  
1608  26/05/2017 00:00:00

In [180]:
import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in scraped_data_df_500000.iterrows():
    
    print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ") #we get a list of words here
    
    scraped_title_year = row['year']
    
    for indexx,rowx in bms_release_list.iterrows():
        
        bms_title = simplify_title(rowx['title'])

        bms_title_words = bms_title.split(' ')
        
        bms_title_year = rowx['release_year']
        
        if ((all(word in bms_title_words for word in scraped_title_words)) &
                            (bms_title_year == scraped_title_year)):
            
            scraped_data_df_500000.loc[index,'all_words_there'] = 'yes'
            
            scraped_data_df_500000.loc[index,'all_words_there_bms_csv_text'] = rowx['title']
            
            break
            
        else:
            
            continue
        
print("DONE AND DONE")

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [181]:
scraped_data_df_500000.head()

number  year                  title  domestic_box_office  \
0    4025  2017          Brad’s Status              2133158   
1     164  2013               The East              2274649   
2    5442  2018  The Catcher Was A Spy               714205   
3    3062  2016            Miles Ahead              2610896   
4      12  2013            World War Z            202359711   

   international_box_office  production_budget domestic_release_date  \
0                   2133158                  0            2017-09-15   
1                   2274649            6500000            2013-05-31   
2                    714205                  0            2018-06-22   
3                   2610896                  0            2016-04-01   
4                 202359711          190000000            2013-06-21   

     domestic_distributor mpaa_rating    franchise  \
0      Annapurna Pictures           R          NaN   
1         Fox Searchlight       PG-13          NaN   
2               IFC Films           R          NaN   
3  Sony Pictures Classics           R          NaN   
4      Paramount Pictures       PG-13  World War Z   

                              source   genre production_method  \
0                Original Screenplay  Comedy       Live Action   
1                Original Screenplay   Drama       Live Action   
2  Based on Fiction Book/Short Story   Drama       Live Action   
3          Based on Real Life Events   Drama       Live Action   
4  Based on Fiction Book/Short Story  Action       Live Action   

          creative_type                               production_companies  \
0  Contemporary Fiction                                                NaN   
1  Contemporary Fiction                                   Scott Free Films   
2    Historical Fiction  Animus Films,PalmStar Media,Serena Films,Windy...   
3         Dramatization  Bifrost Pictures,Sony Pictures Classics,Miles ...   
4       Science Fiction  Skydance Productions,Hemisphere Media Capital,...   

  production_countries all_words_there all_words_there_bms_csv_text  
0        United States             NaN                          NaN  
1        United States             yes                     The East  
2        United States             NaN                          NaN  
3        United States             NaN                          NaN  
4        United States             yes                 World War Z

In [182]:
import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in scraped_data_df_500000.iterrows():
    
    print(index)
    
    scraped_title = simplify_title(row['title'])
    
    scraped_title_year = row['year']

    for indexx,rowx in bms_release_list.iterrows():
        
        bms_title = simplify_title(rowx['title'])
        
        bms_title_year = rowx['release_year']

        if ((bms_title == scraped_title) & (bms_title_year == scraped_title_year)):
            
            scraped_data_df_500000.loc[index,'exact_match'] = 'yes'
            
            scraped_data_df_500000.loc[index,'exact_match_bms_csv_text'] = rowx['title']
            
            break
            
        else:
            
            continue
        
print("DONE AND DONE")

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [183]:
#for some reason we get Nan results with len(scraped_data_df_500000['exact_match'] == 'yes') 
    #so not using it

len(scraped_data_df_500000.loc[scraped_data_df_500000['exact_match'] == 'yes'])

618

In [184]:
#the code below from https://chrisalbon.com/machine_learning/preprocessing_text/remove_stop_words/

# Load library
from nltk.corpus import stopwords

# You will have to download the set of stop words the first time
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/shijith/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [185]:
stop_words = stopwords.words('english')
stop_words[:5]

['i', 'me', 'my', 'myself', 'we']

In [186]:
len(stop_words)

179

In [187]:
import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in scraped_data_df_500000.iterrows():
    
    print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ") #we get a list of words here
    
    scraped_title_words_remaining = [word for word in scraped_title_words if word not in stop_words]
    
    scraped_title_year = row['year']
    
    for indexx,rowx in bms_release_list.iterrows():
        
        bms_title = simplify_title(rowx['title'])

        bms_title_words = bms_title.split(' ')
        
        bms_title_words_remaining = [word for word in bms_title_words if word not in stop_words]
        
        bms_title_year = rowx['release_year']
        
        if ((set(bms_title_words_remaining) == set(scraped_title_words_remaining)) &
                            (bms_title_year == scraped_title_year)):
            
            scraped_data_df_500000.loc[index,'after_stopwords_removed'] = 'yes'
            
            scraped_data_df_500000.loc[index,'after_stopwords_removed_bms_csv_text'] = rowx['title']
            
            break
            
        else:
            
            continue
        
print("DONE AND DONE")

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [188]:
import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in scraped_data_df_500000.iterrows():
    
    print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ") #we get a list of words here
    
    scraped_title_year = row['year']
    
    for indexx,rowx in bms_release_list.iterrows():
        
        bms_title = simplify_title(rowx['title'])

        bms_title_words = bms_title.split(' ')
        
        bms_title_year = rowx['release_year']
        
        if ((set(bms_title_words) == set(scraped_title_words)) &
                            (bms_title_year == scraped_title_year)):
            
            scraped_data_df_500000.loc[index,'words_same'] = 'yes'
            
            scraped_data_df_500000.loc[index,'words_same_bms_csv_text'] = rowx['title']
            
            break
            
        else:
            
            continue
        
print("DONE AND DONE")

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [189]:
scraped_data_df_500000.columns

Index(['number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text'],
      dtype='object')

In [190]:
len(scraped_data_df_500000.loc[scraped_data_df_500000['exact_match'] == 'yes'])

618

In [191]:
len(scraped_data_df_500000.loc[scraped_data_df_500000['all_words_there'] == 'yes'])

633

In [192]:
len(scraped_data_df_500000.loc[scraped_data_df_500000['words_same'] == 'yes'])

618

In [193]:
len(scraped_data_df_500000.loc[scraped_data_df_500000['after_stopwords_removed'] == 'yes'])

630

In [194]:
len(scraped_data_df_500000.loc[(scraped_data_df_500000['all_words_there'] == 'yes') |
                    (scraped_data_df_500000['after_stopwords_removed'] == 'yes') |
                    (scraped_data_df_500000['words_same'] == 'yes') |
                    (scraped_data_df_500000['exact_match'] == 'yes') 
                              ])

642

In [195]:
#changing number of rows that can be displayed in pandas

pd.set_option('display.max_rows', 700)

In [206]:
master_list_df = scraped_data_df_500000.loc[(scraped_data_df_500000['all_words_there'] == 'yes') |
                    (scraped_data_df_500000['after_stopwords_removed'] == 'yes') |
                    (scraped_data_df_500000['words_same'] == 'yes') |
                    (scraped_data_df_500000['exact_match'] == 'yes') 
                              ]

In [207]:
len(scraped_data_df_500000)

1078

In [208]:
len(master_list_df)

642

In [209]:
master_list_df_inverse = scraped_data_df_500000.loc[~((scraped_data_df_500000['all_words_there'] == 'yes') |
                    (scraped_data_df_500000['after_stopwords_removed'] == 'yes') |
                    (scraped_data_df_500000['words_same'] == 'yes') |
                    (scraped_data_df_500000['exact_match'] == 'yes')) 
                              ]

In [210]:
len(master_list_df_inverse)

436

In [197]:
# master_list_df.reset_index(drop=True,inplace=True)

In [211]:
master_list_df.columns

Index(['number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text'],
      dtype='object')

In [212]:
# column_drop_list = ['domestic_box_office',
#        'international_box_office', 'production_budget',
#        'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
#        'franchise', 'source', 'genre', 'production_method', 'creative_type',
#        'production_companies', 'production_countries']

# master_list_df_for_check = master_list_df.drop(column_drop_list, axis=1) #no inplace=True

In [220]:
master_list_df_further_check = master_list_df.loc[\
                                        (master_list_df['exact_match'] != 'yes')]

In [221]:
master_list_df_confirmed = master_list_df.loc[\
                                        (master_list_df['exact_match'] == 'yes')]

In [222]:
master_list_df_confirmed['released_in_india'] = 'yes'

/home/shijith/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [223]:
master_list_df_inverse['released_in_india'] = 'no'

/home/shijith/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [224]:
master_list_df_further_check

number  year                           title  domestic_box_office  \
66      4054  2017                        Inhumans               500000   
199     1835  2015                        Criminal             14708696   
215     3030  2016               Ratchet and Clank              8813410   
241      156  2013                              No              2341226   
307     2949  2016                        Why Him?             60323786   
322      835  2014         Planes: Fire and Rescue             59157732   
353     4008  2017                        The Wall              1803064   
385     5188  2018             The Hurricane Heist              6115824   
410     4052  2017                The Little Hours              1647175   
471     1817  2015                   Woman in Gold             33307793   
480     5184  2018    The Strangers: Prey at Night             24431472   
494     3923  2017                        The Star             40847995   
500        6  2013              Fast and Furious 6            238679850   
554       38  2013  Hansel & Gretel: Witch Hunters             55703475   
556     1738  2015                       Furious 7            353007020   
618      880  2014                            Wild             37880356   
624     4042  2017                            Jane              1723379   
769     1761  2015               The Peanuts Movie            130178411   
881      197  2013                         Phantom              1034589   
902       10  2013            Thor: The Dark World            206362140   
975     4004  2017          An Inconvenient Sequel              3496795   
998       77  2013                     Pain & Gain             49875291   
1015    4050  2017                           Lucky               955925   
1065     108  2013                     21 and Over             25682380   

      international_box_office  production_budget domestic_release_date  \
66                      500000                  0                   NaN   
199                   14708696           31500000            2015-04-15   
215                    8813410           20000000            2016-04-29   
241                    2341226                  0            2013-02-15   
307                   60323786           38000000            2016-12-23   
322                   59157732           50000000            2014-07-18   
353                    1803064            3000000            2017-05-12   
385                    6115824           40000000            2018-03-09   
410                    1647175                  0            2017-06-30   
471                   33307793           11000000            2015-04-01   
480                   24431472                  0            2018-03-09   
494                   40847995           20000000            2017-11-17   
500                  238679850          160000000            2013-05-24   
554                   55703475           50000000            2013-01-25   
556                  353007020          190000000            2015-04-03   
618                   37880356           15000000            2014-12-03   
624                    1723379                  0            2017-10-20   
769                  130178411           99000000            2015-11-06   
881                    1034589           18000000            2013-03-01   
902                  206362140          150000000            2013-11-08   
975                    3496795            1000000            2017-07-28   
998                   49875291           26000000            2013-04-26   
1015                    955925                  0            2017-09-29   
1065                  25682380           13000000            2013-03-01   

                       domestic_distributor mpaa_rating  \
66                       Parkside Releasing   Not Rated   
199                               Lionsgate           R   
215                          Focus Features          PG   
241               

In [225]:
master_list_df_further_check['released_in_india'] = 'yes'

/home/shijith/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [227]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [226]:
master_list_df_further_check

number  year                           title  domestic_box_office  \
66      4054  2017                        Inhumans               500000   
199     1835  2015                        Criminal             14708696   
215     3030  2016               Ratchet and Clank              8813410   
241      156  2013                              No              2341226   
307     2949  2016                        Why Him?             60323786   
322      835  2014         Planes: Fire and Rescue             59157732   
353     4008  2017                        The Wall              1803064   
385     5188  2018             The Hurricane Heist              6115824   
410     4052  2017                The Little Hours              1647175   
471     1817  2015                   Woman in Gold             33307793   
480     5184  2018    The Strangers: Prey at Night             24431472   
494     3923  2017                        The Star             40847995   
500        6  2013              Fast and Furious 6            238679850   
554       38  2013  Hansel & Gretel: Witch Hunters             55703475   
556     1738  2015                       Furious 7            353007020   
618      880  2014                            Wild             37880356   
624     4042  2017                            Jane              1723379   
769     1761  2015               The Peanuts Movie            130178411   
881      197  2013                         Phantom              1034589   
902       10  2013            Thor: The Dark World            206362140   
975     4004  2017          An Inconvenient Sequel              3496795   
998       77  2013                     Pain & Gain             49875291   
1015    4050  2017                           Lucky               955925   
1065     108  2013                     21 and Over             25682380   

      international_box_office  production_budget domestic_release_date  \
66                      500000                  0                   NaN   
199                   14708696           31500000            2015-04-15   
215                    8813410           20000000            2016-04-29   
241                    2341226                  0            2013-02-15   
307                   60323786           38000000            2016-12-23   
322                   59157732           50000000            2014-07-18   
353                    1803064            3000000            2017-05-12   
385                    6115824           40000000            2018-03-09   
410                    1647175                  0            2017-06-30   
471                   33307793           11000000            2015-04-01   
480                   24431472                  0            2018-03-09   
494                   40847995           20000000            2017-11-17   
500                  238679850          160000000            2013-05-24   
554                   55703475           50000000            2013-01-25   
556                  353007020          190000000            2015-04-03   
618                   37880356           15000000            2014-12-03   
624                    1723379                  0            2017-10-20   
769                  130178411           99000000            2015-11-06   
881                    1034589           18000000            2013-03-01   
902                  206362140          150000000            2013-11-08   
975                    3496795            1000000            2017-07-28   
998                   49875291           26000000            2013-04-26   
1015                    955925                  0            2017-09-29   
1065                  25682380           13000000            2013-03-01   

                       domestic_distributor mpaa_rating  \
66                       Parkside Releasing   Not Rated   
199                               Lionsgate           R   
215                          Focus Features          PG   
241               

In [228]:
change_list = [199,241,307,353,494,618,624,881,1015]

for index_number in change_list:
    master_list_df_further_check.loc[index_number,'released_in_india'] = 'no'

/home/shijith/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:517: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [229]:
master_list_df_further_check

number  year                           title  domestic_box_office  \
66      4054  2017                        Inhumans               500000   
199     1835  2015                        Criminal             14708696   
215     3030  2016               Ratchet and Clank              8813410   
241      156  2013                              No              2341226   
307     2949  2016                        Why Him?             60323786   
322      835  2014         Planes: Fire and Rescue             59157732   
353     4008  2017                        The Wall              1803064   
385     5188  2018             The Hurricane Heist              6115824   
410     4052  2017                The Little Hours              1647175   
471     1817  2015                   Woman in Gold             33307793   
480     5184  2018    The Strangers: Prey at Night             24431472   
494     3923  2017                        The Star             40847995   
500        6  2013              Fast and Furious 6            238679850   
554       38  2013  Hansel & Gretel: Witch Hunters             55703475   
556     1738  2015                       Furious 7            353007020   
618      880  2014                            Wild             37880356   
624     4042  2017                            Jane              1723379   
769     1761  2015               The Peanuts Movie            130178411   
881      197  2013                         Phantom              1034589   
902       10  2013            Thor: The Dark World            206362140   
975     4004  2017          An Inconvenient Sequel              3496795   
998       77  2013                     Pain & Gain             49875291   
1015    4050  2017                           Lucky               955925   
1065     108  2013                     21 and Over             25682380   

      international_box_office  production_budget domestic_release_date  \
66                      500000                  0                   NaN   
199                   14708696           31500000            2015-04-15   
215                    8813410           20000000            2016-04-29   
241                    2341226                  0            2013-02-15   
307                   60323786           38000000            2016-12-23   
322                   59157732           50000000            2014-07-18   
353                    1803064            3000000            2017-05-12   
385                    6115824           40000000            2018-03-09   
410                    1647175                  0            2017-06-30   
471                   33307793           11000000            2015-04-01   
480                   24431472                  0            2018-03-09   
494                   40847995           20000000            2017-11-17   
500                  238679850          160000000            2013-05-24   
554                   55703475           50000000            2013-01-25   
556                  353007020          190000000            2015-04-03   
618                   37880356           15000000            2014-12-03   
624                    1723379                  0            2017-10-20   
769                  130178411           99000000            2015-11-06   
881                    1034589           18000000            2013-03-01   
902                  206362140          150000000            2013-11-08   
975                    3496795            1000000            2017-07-28   
998                   49875291           26000000            2013-04-26   
1015                    955925                  0            2017-09-29   
1065                  25682380           13000000            2013-03-01   

                       domestic_distributor mpaa_rating  \
66                       Parkside Releasing   Not Rated   
199                               Lionsgate           R   
215                          Focus Features          PG   
241               

In [230]:
master_list_df_reconstituted = pd.concat([master_list_df_inverse, master_list_df_confirmed, master_list_df_further_check])
len(master_list_df_reconstituted)

1078

In [231]:
# add pirates caribbean title

#know for a fact that pirates of the caribbean was released under another name outside India, so changing that entry specifically

master_list_df_reconstituted.loc[master_list_df_reconstituted['title'].str.contains("Pirates")]

number  year                                             title  \
77    3867  2017  Pirates of the Caribbean: Dead Men Tell No Tales   

    domestic_box_office  international_box_office  production_budget  \
77            172558876                 172558876          230000000   

   domestic_release_date domestic_distributor mpaa_rating  \
77            2017-05-26          Walt Disney       PG-13   

                   franchise        ...        production_countries  \
77  Pirates of the Caribbean        ...               United States   

   all_words_there all_words_there_bms_csv_text exact_match  \
77             NaN                          NaN         NaN   

   exact_match_bms_csv_text after_stopwords_removed  \
77                      NaN                     NaN   

   after_stopwords_removed_bms_csv_text words_same words_same_bms_csv_text  \
77                                  NaN        NaN                     NaN   

   released_in_india  
77                no  

[1 rows x 25 columns]

In [232]:
master_list_df_reconstituted.loc[77,'released_in_india'] = 'yes'

In [233]:
master_list_df_reconstituted.loc[master_list_df_reconstituted['title'].str.contains("Pirates")]

number  year                                             title  \
77    3867  2017  Pirates of the Caribbean: Dead Men Tell No Tales   

    domestic_box_office  international_box_office  production_budget  \
77            172558876                 172558876          230000000   

   domestic_release_date domestic_distributor mpaa_rating  \
77            2017-05-26          Walt Disney       PG-13   

                   franchise        ...        production_countries  \
77  Pirates of the Caribbean        ...               United States   

   all_words_there all_words_there_bms_csv_text exact_match  \
77             NaN                          NaN         NaN   

   exact_match_bms_csv_text after_stopwords_removed  \
77                      NaN                     NaN   

   after_stopwords_removed_bms_csv_text words_same words_same_bms_csv_text  \
77                                  NaN        NaN                     NaN   

   released_in_india  
77               yes  

[1 rows x 25 columns]

In [238]:
master_list_df_reconstituted.head()

number  year                  title  domestic_box_office  \
0    4025  2017          Brad’s Status              2133158   
2    5442  2018  The Catcher Was A Spy               714205   
3    3062  2016            Miles Ahead              2610896   
5    3145  2016              Unsullied               510957   
6      19  2013         The Hangover 3            112200072   

   international_box_office  production_budget domestic_release_date  \
0                   2133158                  0            2017-09-15   
2                    714205                  0            2018-06-22   
3                   2610896                  0            2016-04-01   
5                    510957            1500000            2016-04-22   
6                 112200072          103000000            2013-05-23   

     domestic_distributor mpaa_rating franchise        ...         \
0      Annapurna Pictures           R       NaN        ...          
2               IFC Films           R       NaN        ...          
3  Sony Pictures Classics           R       NaN        ...          
5        Indican Pictures           R       NaN        ...          
6            Warner Bros.           R  Hangover        ...          

  production_countries all_words_there all_words_there_bms_csv_text  \
0        United States             NaN                          NaN   
2        United States             NaN                          NaN   
3        United States             NaN                          NaN   
5        United States             NaN                          NaN   
6        United States             NaN                          NaN   

  exact_match exact_match_bms_csv_text after_stopwords_removed  \
0         NaN                      NaN                     NaN   
2         NaN                      NaN                     NaN   
3         NaN                      NaN                     NaN   
5         NaN                      NaN                     NaN   
6         NaN                      NaN                     NaN   

  after_stopwords_removed_bms_csv_text words_same words_same_bms_csv_text  \
0                                  NaN        NaN                     NaN   
2                                  NaN        NaN                     NaN   
3                                  NaN        NaN                     NaN   
5                                  NaN        NaN                     NaN   
6                                  NaN        NaN                     NaN   

  released_in_india  
0                no  
2                no  
3                no  
5                no  
6                no  

[5 rows x 25 columns]

In [241]:
master_list_df_reconstituted.to_csv('data/india_release_check_v1.csv', encoding='utf_8_sig')

In [236]:
index_number_list = list(range(1,1079))
for index,row in master_list_df_reconstituted.iterrows():
    if index not in index_number_list:
        print(index)
        
print('done')

0
done


In [242]:
master_list_df_reconstituted.head()

number  year                  title  domestic_box_office  \
0    4025  2017          Brad’s Status              2133158   
2    5442  2018  The Catcher Was A Spy               714205   
3    3062  2016            Miles Ahead              2610896   
5    3145  2016              Unsullied               510957   
6      19  2013         The Hangover 3            112200072   

   international_box_office  production_budget domestic_release_date  \
0                   2133158                  0            2017-09-15   
2                    714205                  0            2018-06-22   
3                   2610896                  0            2016-04-01   
5                    510957            1500000            2016-04-22   
6                 112200072          103000000            2013-05-23   

     domestic_distributor mpaa_rating franchise        ...         \
0      Annapurna Pictures           R       NaN        ...          
2               IFC Films           R       NaN        ...          
3  Sony Pictures Classics           R       NaN        ...          
5        Indican Pictures           R       NaN        ...          
6            Warner Bros.           R  Hangover        ...          

  production_countries all_words_there all_words_there_bms_csv_text  \
0        United States             NaN                          NaN   
2        United States             NaN                          NaN   
3        United States             NaN                          NaN   
5        United States             NaN                          NaN   
6        United States             NaN                          NaN   

  exact_match exact_match_bms_csv_text after_stopwords_removed  \
0         NaN                      NaN                     NaN   
2         NaN                      NaN                     NaN   
3         NaN                      NaN                     NaN   
5         NaN                      NaN                     NaN   
6         NaN                      NaN                     NaN   

  after_stopwords_removed_bms_csv_text words_same words_same_bms_csv_text  \
0                                  NaN        NaN                     NaN   
2                                  NaN        NaN                     NaN   
3                                  NaN        NaN                     NaN   
5                                  NaN        NaN                     NaN   
6                                  NaN        NaN                     NaN   

  released_in_india  
0                no  
2                no  
3                no  
5                no  
6                no  

[5 rows x 25 columns]

In [244]:
master_list_df_reconstituted.replace({"`":"'"}, regex=True)

number  year                                              title  \
0       4025  2017                                      Brad’s Status   
2       5442  2018                              The Catcher Was A Spy   
3       3062  2016                                        Miles Ahead   
5       3145  2016                                          Unsullied   
6         19  2013                                     The Hangover 3   
7       4000  2017  Norman: The Moderate Rise and Tragic Fall of a...   
8       1955  2015                               Faith of Our Fathers   
9        209  2013                                      Muscle Shoals   
10       939  2014                                        CitizenFour   
12      1006  2014                    On Any Sunday: The Next Chapter   
16      3137  2016                                         The Bronze   
19      3968  2017                                The Case for Christ   
23       870  2014                                     God’s Not Dead   
25      3904  2017          Three Billboards Outside Ebbing, Missouri   
26      3940  2017                                         Wind River   
30      1866  2015                                       Love & Mercy   
34      3906  2017                                         Girls Trip   
41      5125  2018                                             Samson   
43       192  2013                                   What Maisie Knew   
44       940  2014                                 The Skeleton Twins   
46      4070  2017                                           Landline   
48       165  2013                         The Met: Live in HD - Aida   
49      5119  2018                                 Fifty Shades Freed   
50       178  2013                                  2013 Oscar Shorts   
55       964  2014                       Awake: The Life of Yogananda   
58      5127  2017                               Una mujer fantástica   
61      4024  2017                                   Ingrid Goes West   
63      1805  2015                                           War Room   
67      3045  2016                                          Compadres   
68      3961  2017                                          Wish Upon   
69       115  2013                                    Spring Breakers   
77      3867  2017   Pirates of the Caribbean: Dead Men Tell No Tales   
80      1796  2015                                          Spotlight   
82      3127  2016                                 Saturday’s Warrior   
83      3996  2017                                        Tulip Fever   
85      4026  2017                                       Wonderstruck   
86      3042  2016                                 A Beautiful Planet   
92      3016  2016                              Fifty Shades of Black   
93      3143  2016                                           Range 15   
95       977  2014                                         Repentance   
97      4093  2017                                            Dolores   
102      952  2014                                   The Fluffy Movie   
103     3900  2017                                     Daddy’s Home 2   
106     1890  2015                                              Truth   
108     2942  2016                                      Pete’s Dragon   
111     3932  2017                         All the Money in the World   
115      153  2013                                      Stand Up Guys   
118     4022  2017                               Til Death Do Us Part   
119     1000  2014                                  Jodorowsky’s Dune   
121      959  2014                                  2014 Oscar Shorts   
123     1923  2015                        The Diary of a Teenage Girl   
124     2920  2016                                     Hidden Figures   
130     3140  2016                                            Gleason   
134     2976  2016                                     Monster T

In [245]:
master_list_df_reconstituted.replace({"’":"'"}, regex=True)

number  year                                              title  \
0       4025  2017                                      Brad's Status   
2       5442  2018                              The Catcher Was A Spy   
3       3062  2016                                        Miles Ahead   
5       3145  2016                                          Unsullied   
6         19  2013                                     The Hangover 3   
7       4000  2017  Norman: The Moderate Rise and Tragic Fall of a...   
8       1955  2015                               Faith of Our Fathers   
9        209  2013                                      Muscle Shoals   
10       939  2014                                        CitizenFour   
12      1006  2014                    On Any Sunday: The Next Chapter   
16      3137  2016                                         The Bronze   
19      3968  2017                                The Case for Christ   
23       870  2014                                     God's Not Dead   
25      3904  2017          Three Billboards Outside Ebbing, Missouri   
26      3940  2017                                         Wind River   
30      1866  2015                                       Love & Mercy   
34      3906  2017                                         Girls Trip   
41      5125  2018                                             Samson   
43       192  2013                                   What Maisie Knew   
44       940  2014                                 The Skeleton Twins   
46      4070  2017                                           Landline   
48       165  2013                         The Met: Live in HD - Aida   
49      5119  2018                                 Fifty Shades Freed   
50       178  2013                                  2013 Oscar Shorts   
55       964  2014                       Awake: The Life of Yogananda   
58      5127  2017                               Una mujer fantástica   
61      4024  2017                                   Ingrid Goes West   
63      1805  2015                                           War Room   
67      3045  2016                                          Compadres   
68      3961  2017                                          Wish Upon   
69       115  2013                                    Spring Breakers   
77      3867  2017   Pirates of the Caribbean: Dead Men Tell No Tales   
80      1796  2015                                          Spotlight   
82      3127  2016                                 Saturday's Warrior   
83      3996  2017                                        Tulip Fever   
85      4026  2017                                       Wonderstruck   
86      3042  2016                                 A Beautiful Planet   
92      3016  2016                              Fifty Shades of Black   
93      3143  2016                                           Range 15   
95       977  2014                                         Repentance   
97      4093  2017                                            Dolores   
102      952  2014                                   The Fluffy Movie   
103     3900  2017                                     Daddy's Home 2   
106     1890  2015                                              Truth   
108     2942  2016                                      Pete's Dragon   
111     3932  2017                         All the Money in the World   
115      153  2013                                      Stand Up Guys   
118     4022  2017                               Til Death Do Us Part   
119     1000  2014                                  Jodorowsky's Dune   
121      959  2014                                  2014 Oscar Shorts   
123     1923  2015                        The Diary of a Teenage Girl   
124     2920  2016                                     Hidden Figures   
130     3140  2016                                            Gleason   
134     2976  2016                                     Monster T

In [252]:
master_list_df_reconstituted['released_in_india_2nd_check'] = master_list_df_reconstituted['released_in_india']

In [253]:
master_list_df_reconstituted['released_in_india_2nd_check_match_1'] = master_list_df_reconstituted['released_in_india']

In [254]:
master_list_df_reconstituted['released_in_india_2nd_check_match_2'] = master_list_df_reconstituted['released_in_india']

In [255]:
master_list_df_reconstituted['released_in_india_2nd_check_match_3'] = master_list_df_reconstituted['released_in_india']

In [263]:
#just backing up the df to a csv 

master_list_df_reconstituted.to_csv('data/india_release_check_v2.csv')

In [292]:
bms_release_list = pd.read_csv("data/bookmyshow_list.csv")
bms_release_list

Release_Year                                EventGroup_strTitle  \
0             2013                    Hansel And Gretel Witch Hunters   
1             2013                              7 Days In Slow Motion   
2             2013                                     Chinese Zodiac   
3             2013                                     The Impossible   
4             2013                                   Tropical Races 3   
5             2013                Universal Soldier: Day Of Reckoning   
6             2013                                      Comic Vampire   
7             2013                              Dinosaur Reappearance   
8             2013                Roller Coaster & Dinosaur Adventure   
9             2013                                     Gangster Squad   
10            2013                                    Les Miserables.   
11            2013                                      Promised Land   
12            2013                                        Broken City   
13            2013                                     The Last Stand   
14            2013                                         This Is 40   
15            2013                                       End of Watch   
16            2013                                     Dance Of Death   
17            2013            Strange Stories & Dinosaur Reappearance   
18            2013                                Bullet To The Head    
19            2013                                Here Comes the Boom   
20            2013                                Midnight's Children   
21            2013                                             Parker   
22            2013                                               Argo   
23            2013                                            Lincoln   
24            2013                                               Mama   
25            2013                                Beautiful Creatures   
26            2013                     Forest Adventure & Ice Fighter   
27            2013                  Forest Adventure & Roller Coaster   
28            2013                       Ice Fighter & Roller Coaster   
29            2013                    The Perks Of Being A Wallflower   
30            2013                                   Zero Dark Thirty   
31            2013                             A Good Day To Die Hard   
32            2013                                         Dark Skies   
33            2013                            Silver Linings Playbook   
34            2013                                          Pinocchio   
35            2013                                             Flight   
36            2013                   Haunted Graves + Night With Toys   
37            2013                             Jack The Giant Slayer    
38            2013                Night At Toy Store + Roller Coaster   
39            2013                        Pharaoh Queen +Time Machine   
40            2013            Predator Attack + Prehistoric Adventure   
41            2013                        Rescue And Path Finder Snow   
42            2013                                          Dandelion   
43            2013            Prehistoric Adventure + Night With Toys   
44            2013                                          21 & Over   
45            2013                           All I Want Is Everything   
46            2013                      Flying Swords of Dragon Gate    
47            2013                        Oz The Great And Powerful     
48            2013                                             Snitch   
49            2013                                             Zarafa   
50            2013                                     Texas Chainsaw   
51            2013                    The Incredible Burt Wonderstone   
52            2013                                         The Master   
53            2013                                     Identity 

In [293]:
bms_release_list.dtypes

Release_Year             int64
EventGroup_strTitle     object
Event_dtmReleaseDate    object
dtype: object

In [294]:
bms_release_list.rename(columns={'Release_Year': 'release_year',
                                  'EventGroup_strTitle':'title',
                                  'Event_dtmReleaseDate':'release_date'}, inplace=True)

In [295]:
bms_release_list.dtypes

release_year     int64
title           object
release_date    object
dtype: object

In [330]:
master_list_df_reconstituted = pd.read_csv("data/india_release_check_v2.csv")

In [331]:
master_list_df_reconstituted['released_in_india_2nd_check_match_4'] = master_list_df_reconstituted['released_in_india']

master_list_df_reconstituted['released_in_india_2nd_check_match_5'] = master_list_df_reconstituted['released_in_india']

master_list_df_reconstituted['released_in_india_2nd_check_match_6'] = master_list_df_reconstituted['released_in_india']

master_list_df_reconstituted['released_in_india_2nd_check_match_7'] = master_list_df_reconstituted['released_in_india']

master_list_df_reconstituted['released_in_india_2nd_check_match_8'] = master_list_df_reconstituted['released_in_india']

In [332]:
master_list_df_reconstituted['released_in_india_2nd_check_match_1_bms_csv_text'] = ""

master_list_df_reconstituted['released_in_india_2nd_check_match_2_bms_csv_text'] = ""

master_list_df_reconstituted['released_in_india_2nd_check_match_3_bms_csv_text'] = ""

master_list_df_reconstituted['released_in_india_2nd_check_match_4_bms_csv_text'] = ""

master_list_df_reconstituted['released_in_india_2nd_check_match_5_bms_csv_text'] = ""

master_list_df_reconstituted['released_in_india_2nd_check_match_6_bms_csv_text'] = ""

master_list_df_reconstituted['released_in_india_2nd_check_match_7_bms_csv_text'] = ""

master_list_df_reconstituted['released_in_india_2nd_check_match_8_bms_csv_text'] = ""

In [333]:
# Load library
from nltk.corpus import stopwords

# You will have to download the set of stop words the first time
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/shijith/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [334]:
stop_words = stopwords.words('english')

In [335]:
master_list_df_reconstituted.shape

(1078, 43)

In [336]:
master_list_df_reconstituted_yes = master_list_df_reconstituted[master_list_df_reconstituted['released_in_india']=='yes']

In [337]:
master_list_df_reconstituted_no = master_list_df_reconstituted[master_list_df_reconstituted['released_in_india']=='no']

In [339]:
#master_list_df_reconstituted_no

import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in master_list_df_reconstituted_no.iterrows():
    
    print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ") #we get a list of words here
    
    scraped_title_words = [word for word in scraped_title_words if word not in stop_words]
    
    len_scraped_title_words = len(scraped_title_words)
    
    if len_scraped_title_words == 0:
        
        print('no words to search for title -- {}'.format(row['title']))
        
        continue
        
    elif len_scraped_title_words == 1:
        
        for indexx,rowx in bms_release_list.iterrows():

            bms_title = simplify_title(rowx['title'])

            bms_title_words = bms_title.split(' ')
            
            bms_title_words = [word for word in bms_title_words if word not in stop_words]
            
            if (set(bms_title_words) == set(scraped_title_words)):
                
                master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_1'] = 'yes'
                
                master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_1_bms_csv_text'] = rowx['title']
                
                break
            
            else:
                
                continue
            
        continue
        
    elif len_scraped_title_words > 1:
        
        scraped_title_words_combo_list = list(itertools.combinations(scraped_title_words, (len_scraped_title_words - 1))) #you get a list of tuples here
        
        #if you want to understand what's going on here, list(itertools.combinations([1,2,3], 2)) gives us [(1, 2), (1, 3), (2, 3)]
        
        iteratorx = 0
        
        #you have the pass statement available to you as well

        #what happens if we don't even get a 1st match?

        for indexx,rowx in bms_release_list.iterrows():

            bms_title = simplify_title(rowx['title'])

            bms_title_words = bms_title.split(' ')
            
            bms_title_words = [word for word in bms_title_words if word not in stop_words]
            
            if iteratorx == 0:
            
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_1'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_1_bms_csv_text'] = rowx['title']

                        iteratorx = 1

                        break

                    else:

                        continue
                
                continue
            
            elif iteratorx == 1:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_2'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_2_bms_csv_text'] = rowx['title']

                        iteratorx = 2

                        break

                    else:

                        continue
                
                continue
            
            elif iteratorx == 2:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_3'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_3_bms_csv_text'] = rowx['title']

                        iteratorx = 3

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 3:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_4'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_4_bms_csv_text'] = rowx['title']

                        iteratorx = 4

                        break

                    else:

                        continue
                
                continue
                
                
            elif iteratorx == 4:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_5'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_5_bms_csv_text'] = rowx['title']

                        iteratorx = 5

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 5:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_6'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_6_bms_csv_text'] = rowx['title']

                        iteratorx = 6

                        break

                    else:

                        continue
                
                continue
                
            elif iteratorx == 6:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_7'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_7_bms_csv_text'] = rowx['title']

                        iteratorx = 7

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 7:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_8'] = 'yes'

                        master_list_df_reconstituted_no.loc[index,'released_in_india_2nd_check_match_8_bms_csv_text'] = rowx['title']

                        iteratorx = 8

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 8:

                break

        continue

print("DONE AND DONE")

0
1


/home/shijith/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:517: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
2

In [340]:
master_list_df_reconstituted_no.columns

Index(['Unnamed: 0', 'number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text', 'released_in_india',
       'released_in_india_2nd_check', 'released_in_india_2nd_check_match_1',
       'released_in_india_2nd_check_match_2',
       'released_in_india_2nd_check_match_3',
       'released_in_india_2nd_check_match_4',
       'released_in_india_2nd_check_match_5',
       'released_in_india_2nd_check_match_6',
       'released_in_india_2nd_check_match_7',
       'released_in_india_2nd_check_match_8',
       'released_in_

In [341]:
master_list_df_reconstituted_no_for_check = master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check_match_1'] == 'yes') |
                                                                                (master_list_df_reconstituted_no['released_in_india_2nd_check_match_2'] == 'yes') |
                                                                                (master_list_df_reconstituted_no['released_in_india_2nd_check_match_3'] == 'yes') |
                                                                                (master_list_df_reconstituted_no['released_in_india_2nd_check_match_4'] == 'yes') |
                                                                                (master_list_df_reconstituted_no['released_in_india_2nd_check_match_5'] == 'yes') |
                                                                                (master_list_df_reconstituted_no['released_in_india_2nd_check_match_6'] == 'yes') |
                                                                                (master_list_df_reconstituted_no['released_in_india_2nd_check_match_7'] == 'yes') |
                                                                                (master_list_df_reconstituted_no['released_in_india_2nd_check_match_8'] == 'yes') ]

In [348]:
from IPython.core.display import HTML
HTML("<style>.rendered_html th {max-width: 50px;}</style>")

In [342]:
master_list_df_reconstituted_no_for_check.loc[:, ['title',
                                                  'released_in_india_2nd_check_match_1_bms_csv_text',
                                                  'released_in_india_2nd_check_match_2_bms_csv_text',
                                                  'released_in_india_2nd_check_match_3_bms_csv_text',
                                                  'released_in_india_2nd_check_match_4_bms_csv_text',
                                                  'released_in_india_2nd_check_match_5_bms_csv_text',
                                                  'released_in_india_2nd_check_match_6_bms_csv_text',
                                                  'released_in_india_2nd_check_match_7_bms_csv_text',
                                                  'released_in_india_2nd_check_match_8_bms_csv_text']]

title  \
1                                The Catcher Was A Spy   
4                                       The Hangover 3   
11                                 The Case for Christ   
12                                      God's Not Dead   
13           Three Billboards Outside Ebbing, Missouri   
14                                          Wind River   
15                                        Love & Mercy   
16                                          Girls Trip   
18                                    What Maisie Knew   
22                                  Fifty Shades Freed   
24                        Awake: The Life of Yogananda   
27                                            War Room   
29                                           Wish Upon   
32                                           Spotlight   
33                                  Saturday's Warrior   
34                                         Tulip Fever   
36                                  A Beautiful Planet   
37                               Fifty Shades of Black   
38                                            Range 15   
41                                    The Fluffy Movie   
42                                      Daddy's Home 2   
43                                               Truth   
44                                       Pete's Dragon   
45                          All the Money in the World   
46                                       Stand Up Guys   
48                                   Jodorowsky's Dune   
50                         The Diary of a Teenage Girl   
51                                      Hidden Figures   
53                                      Monster Trucks   
55                   Anchorman 2: The Legend Continues   
56                                      All Eyez on Me   
57                                       Obvious Child   
58                                         Cartel Land   
59                                     A Monster Calls   
60                                       I Feel Pretty   
61                                            Rock Dog   
62                             Justin Bieber's Believe   
63                                  The Eagle Huntress   
64                            The Theory of Everything   
66                                     Love is Strange   
69                                              Fences   
72                                 Inside Llewyn Davis   
73                                 Fifty Shades Darker   
78                                          Downsizing   
79                                     Best of Enemies   
80                                            Marshall   
86                                   The Hateful Eight   
90         Miss Peregrine's Home for Peculiar Children   
92                                            Papillon   
95                                        Mother's Day   
98                                       A Ghost Story   
101                                               Room   
104                                           47 Ronin   
106   Teenage Mutant Ninja Turtles: Out of the Shadows   
109                                   My Friend Dahmer   
111                                     Irrational Man   
113                                           99 Homes   
114                                           Hostiles   
120                                  The Water Diviner   
121                                          Moonlight   
125                                        Filly Brown   
128                                Battle of the Sexes   
129                                          Incarnate   
131                                    Beyond the Mask   
132                                     Bleed for This   
134                                     American Ultra   
136                                 Let There Be Light   
137                            The Fate of the Furious   
138                                The Florida 

In [349]:
#there's a title 'why him' that was released in the US but isn't showing up, i guess because both 'why' and 'him' are stop words, so just manually correcting for this title
#am getting the index number for it

master_list_df_reconstituted_no.loc[master_list_df_reconstituted_no['title'].str.contains("Why Him")]

Unnamed: 0  number  year     title  domestic_box_office  \
1058         307    2949  2016  Why Him?             60323786   

      international_box_office  production_budget domestic_release_date  \
1058                  60323786           38000000            2016-12-23   

     domestic_distributor mpaa_rating  \
1058     20th Century Fox           R   

                           ...                         \
1058                       ...                          

     released_in_india_2nd_check_match_7 released_in_india_2nd_check_match_8  \
1058                                  no                                  no   

     released_in_india_2nd_check_match_1_bms_csv_text  \
1058                                                    

     released_in_india_2nd_check_match_2_bms_csv_text  \
1058                                                    

     released_in_india_2nd_check_match_3_bms_csv_text  \
1058                                                    

     released_in_india_2nd_check_match_4_bms_csv_text  \
1058                                                    

     released_in_india_2nd_check_match_5_bms_csv_text  \
1058                                                    

     released_in_india_2nd_check_match_6_bms_csv_text  \
1058                                                    

     released_in_india_2nd_check_match_7_bms_csv_text  \
1058                                                    

     released_in_india_2nd_check_match_8_bms_csv_text  
1058                                                   

[1 rows x 43 columns]

In [350]:
#got this correction list by going through the table above
#so i have like 8 potential matches in the bookmyshow list for each movie released domestically in the US (and which grossed at least $500,000 at the box office)
#if it seems like one of the 8 matches is actually a match, have entered the index number in this list, the correction_list

correction_list = [4,12,13,24,29,32,42,43,48,50,51,53,55,56,59,61,62,64,69,72,78,80,86,90,92,95,101,104,106,114,120,121,128,129,132,134,137,138,139,140,145,146,148,149,157,159,166,172,173,176,178,182,186,
                187,188,190,197,203,205,206,208,209,212,215,221,225,233,
239,241,243,244,250,255,256,257,258,259,262,264,265,266,271,272,274,277,278,281,282,283,286,296,297,299,316,317,320,322,327,329,331,338,340,343,348,354,359,361,366,367,370,371,373,376,379,383,384,
                385,386,387,388,389,390,393,394,396,401,407,409,
414,419,421,425,428,431,434,1055,1060,1065,1069,1058]

In [351]:
master_list_df_reconstituted_no.shape

(444, 43)

In [353]:
len(master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'yes')])

0

In [354]:
len(master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'no')])

444

In [355]:
for index_number in correction_list:
    master_list_df_reconstituted_no.loc[index_number,'released_in_india_2nd_check'] = 'yes'

/home/shijith/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:517: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [356]:
len(master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'yes')])

140

In [357]:
len(master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'no')])

304

In [358]:
master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'yes')]

Unnamed: 0  number  year  \
4              6      19  2013   
12            23     870  2014   
13            25    3904  2017   
24            55     964  2014   
29            68    3961  2017   
32            80    1796  2015   
42           103    3900  2017   
43           106    1890  2015   
48           119    1000  2014   
50           123    1923  2015   
51           124    2920  2016   
53           134    2976  2016   
55           142      46  2013   
56           143    2980  2016   
59           146    2985  2016   
61           150    3008  2016   
62           151     113  2013   
64           155     843  2014   
69           161    2974  2016   
72           165     111  2013   
78           172    3935  2017   
80           176    3982  2017   
86           194    1778  2015   
90           203    2915  2016   
92           209    4010  2017   
95           216    2983  2016   
101          237    1837  2015   
104          243      49  2013   
106          250    2917  2016   
114          262    3949  2017   
120          276     900  2014   
121          277    2973  2016   
128          291    3967  2017   
129          292    3039  2016   
132          304    3052  2016   
134          309    1848  2015   
137          326    3859  2017   
138          328    3978  2017   
139          329     822  2014   
140          332    2937  2016   
145          347    3067  2016   
146          349    3928  2017   
148          357    1878  2015   
149          363    3894  2017   
157          379     123  2013   
159          387     832  2014   
166          406      42  2013   
172          419    5271  2017   
173          430    1827  2015   
176          434    1871  2015   
178          437     818  2014   
182          447    2934  2016   
186          456    1852  2015   
187          457     169  2013   
188          458     894  2014   
190          462    3929  2017   
197          476    3914  2017   
203          489    3917  2017   
205          502    1820  2015   
206          503    1780  2015   
208          507     920  2014   
209          508     100  2013   
212          513     911  2014   
215          521    3931  2017   
221          533    3963  2017   
225          547    5505  2018   
233          572    3025  2016   
239          587    1759  2015   
241          592    3957  2017   
243          596     919  2014   
244          598     799  2014   
250          610      79  2013   
255          616      43  2013   
256          617    1808  2015   
257          620    2914  2016   
258          622     931  2014   
259          629     846  2014   
262          636    2999  2016   
264          642    3001  2016   
265          645    2912  2016   
266          646    4020  2017   
271          658    1779  2015   
272          667    3920  2017   
274          672    2946  2016   
277          678    3000  2016   
278          679    1791  2015   
281          688    3011  2016   
282          691      51  2013   
283          692    3068  2016   
286          700    2910  2016   
296          735    3896  2017   
297          737    3009  2016   
299          744     839  2014   
316          782    3990  2017   
317          783      86  2013   
320          789    1841  2015   
322          791    3898  2017   
327          798      58  2013   
329          801    1887  2015   
331          808      32  2013   
338          826    1782  2015   
340          832    3897  2017   
343          843      76  2013   
348          855    2918  2016   
354          874    1764  2015   
359          885    1838  2015   
361          889    3078  2016   
366          905    3044  2016   
367          907    3901  2017   
370          913    1904  2015   
371          915    1799  2015   
373          921     179  2013   
376          927     925  2014   
379          938    3005  2016   
383          952    3975  2017   
384          956    2925  2016   
385          957      35  20

In [359]:
master_list_df_reconstituted_no.loc[:, ['title',
                                                  'released_in_india',
                                                  'released_in_india_2nd_check']]

title released_in_india  \
0                                         Brad's Status                no   
1                                 The Catcher Was A Spy                no   
2                                           Miles Ahead                no   
3                                             Unsullied                no   
4                                        The Hangover 3                no   
5     Norman: The Moderate Rise and Tragic Fall of a...                no   
6                                  Faith of Our Fathers                no   
7                                         Muscle Shoals                no   
8                                           CitizenFour                no   
9                       On Any Sunday: The Next Chapter                no   
10                                           The Bronze                no   
11                                  The Case for Christ                no   
12                                       God's Not Dead                no   
13            Three Billboards Outside Ebbing, Missouri                no   
14                                           Wind River                no   
15                                         Love & Mercy                no   
16                                           Girls Trip                no   
17                                               Samson                no   
18                                     What Maisie Knew                no   
19                                   The Skeleton Twins                no   
20                                             Landline                no   
21                           The Met: Live in HD - Aida                no   
22                                   Fifty Shades Freed                no   
23                                    2013 Oscar Shorts                no   
24                         Awake: The Life of Yogananda                no   
25                                 Una mujer fantástica                no   
26                                     Ingrid Goes West                no   
27                                             War Room                no   
28                                            Compadres                no   
29                                            Wish Upon                no   
30                                      Spring Breakers                no   
32                                            Spotlight                no   
33                                   Saturday's Warrior                no   
34                                          Tulip Fever                no   
35                                         Wonderstruck                no   
36                                   A Beautiful Planet                no   
37                                Fifty Shades of Black                no   
38                                             Range 15                no   
39                                           Repentance                no   
40                                              Dolores                no   
41                                     The Fluffy Movie                no   
42                                       Daddy's Home 2                no   
43                                                Truth                no   
44                                        Pete's Dragon                no   
45                           All the Money in the World                no   
46                                        Stand Up Guys                no   
47                                 Til Death Do Us Part                no   
48                                    Jodorowsky's Dune                no   
49                                    2014 Oscar Shorts                no   
50                          The Diary of a Teenage Girl                no   
51                                       Hidden Figures                no   
52                                            

In [363]:
#so colons in the title names were throwing my search off
#below is a list of all the films with the colon mark ':' in their titles and have been marked as not released in India
#will be checking this list manually and compiling another correction list

master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['title'].str.contains(":")) & (master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'no')]

Unnamed: 0  number  year  \
5             7    4000  2017   
9            12    1006  2014   
21           48     165  2013   
75          168    4077  2017   
83          180    4045  2017   
100         230    3081  2016   
102         238     924  2014   
108         253    5189  2018   
110         256    3035  2016   
112         258    3103  2016   
115         264     194  2013   
155         376    1959  2015   
164         398    1938  2015   
169         409    2962  2016   
184         450    1990  2015   
191         463    3085  2016   
213         518    2952  2016   
220         532    3010  2016   
228         557    3013  2016   
230         565    1947  2015   
234         575      48  2013   
245         599    2913  2016   
246         601    3086  2016   
269         654    3028  2016   
301         747    5513  2018   
311         763    3857  2017   
330         805    5269  2018   
336         823    4068  2017   
341         837     215  2013   
345         851    3111  2016   
355         876    1994  2015   
356         880    3070  2016   
364         897    3902  2017   
365         903     993  2014   
423        1050     927  2014   
432        1074    1736  2015   

                                                 title  domestic_box_office  \
5    Norman: The Moderate Rise and Tragic Fall of a...              3814868   
9                      On Any Sunday: The Next Chapter               509916   
21                          The Met: Live in HD - Aida              2800000   
75       May it Last: A Portrait of the Avett Brothers               725286   
83   Mark Felt: The Man Who Brought Down the White ...               768646   
100                            Hillsong: Let Hope Rise              2394725   
102               America: Imagine a World Without Her             14444502   
108                God's Not Dead: A Light in Darkness              5728940   
110                     The Beatles: Eight Days a Week              2934445   
112  The Music of Strangers: Yo-Yo Ma and the Silk ...              1169214   
115           Walking the Camino: Six Ways to Santiago               612717   
155                           Seymour: An Introduction               729744   
164               Game of Thrones: The IMAX Experience              1896092   
169                              Ouija: Origin of Evil             35144505   
184     The Black Panthers: Vanguard of the Revolution               516893   
191             The Met: Live in HD - Madama Butterfly              1700900   
213                       Neighbors 2: Sorority Rising             55340730   
220                              Kevin Hart: What Now?             23591043   
228          Middle School: The Worst Years of My Life             20007149   
230                   The Met: Live in HD - Tannhauser              1150000   
234                      Jackass Presents: Bad Grandpa            102003019   
245           The Conjuring 2: The Enfield Poltergeist            102470008   
246                The Met: Live in HD - Manon Lescaut              1770000   
269  Hillary's America: The Secret History of the D...             13099931   
301                               Unfriended: Dark Web              8783985   
311                  Star Wars Ep. VIII: The Last Jedi            620181382   
330                      Sgt. Stubby: An American Hero              3054285   
336                   Bombshell: The Hedy Lamarr Story               820300   
341  The Lost Medallion: The Adventures of Billy Stone               549632   
345               Vaxxed: From Cover Up to Catastrophe              1163265   
355                                Deli Man: The Movie               502294   
356                           Batman: The Killing Joke              3775000   
364                             John Wick: Chapter Two             92029184   
365                  Atlas Shrugged: Who Is John Galt?               851690   
423               

In [362]:
master_list_df_reconstituted_no.loc[master_list_df_reconstituted_no['title'].str.contains("\(")]

Unnamed: 0  number  year  \
429        1061     850  2014   

                                               title  domestic_box_office  \
429  Birdman or (The Unexpected Virtue of Ignorance)             42340598   

     international_box_office  production_budget domestic_release_date  \
429                  42340598           18000000            2014-10-17   

    domestic_distributor mpaa_rating  \
429      Fox Searchlight           R   

                          ...                         \
429                       ...                          

    released_in_india_2nd_check_match_7 released_in_india_2nd_check_match_8  \
429                                  no                                  no   

    released_in_india_2nd_check_match_1_bms_csv_text  \
429                                                    

    released_in_india_2nd_check_match_2_bms_csv_text  \
429                                                    

    released_in_india_2nd_check_match_3_bms_csv_text  \
429                                                    

    released_in_india_2nd_check_match_4_bms_csv_text  \
429                                                    

    released_in_india_2nd_check_match_5_bms_csv_text  \
429                                                    

    released_in_india_2nd_check_match_6_bms_csv_text  \
429                                                    

    released_in_india_2nd_check_match_7_bms_csv_text  \
429                                                    

    released_in_india_2nd_check_match_8_bms_csv_text  
429                                                   

[1 rows x 43 columns]

In [364]:
len(master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'yes')])

140

In [365]:
#looked at the table above, checked the csv manually, found which movies were released and which weren't

correction_list_2 = [429,83,169,234,245,301,311,364,432]

for index_number in correction_list_2:
    master_list_df_reconstituted_no.loc[index_number,'released_in_india_2nd_check'] = 'yes'

/home/shijith/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:517: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [366]:
len(master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'yes')])

149

In [367]:
#time to reconstitute the dataframe again

master_list_df_reconstituted_no.shape

(444, 43)

In [368]:
master_list_df_reconstituted_yes.shape

(634, 43)

In [369]:
master_list_df_reconstituted_again = pd.concat([master_list_df_reconstituted_yes, master_list_df_reconstituted_no])
len(master_list_df_reconstituted_again)

1078

In [371]:
master_list_df_reconstituted_again.columns

Index(['Unnamed: 0', 'number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text', 'released_in_india',
       'released_in_india_2nd_check', 'released_in_india_2nd_check_match_1',
       'released_in_india_2nd_check_match_2',
       'released_in_india_2nd_check_match_3',
       'released_in_india_2nd_check_match_4',
       'released_in_india_2nd_check_match_5',
       'released_in_india_2nd_check_match_6',
       'released_in_india_2nd_check_match_7',
       'released_in_india_2nd_check_match_8',
       'released_in_

In [372]:
master_list_df_reconstituted_again.drop('Unnamed: 0', axis=1, inplace=True)

In [373]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text', 'released_in_india',
       'released_in_india_2nd_check', 'released_in_india_2nd_check_match_1',
       'released_in_india_2nd_check_match_2',
       'released_in_india_2nd_check_match_3',
       'released_in_india_2nd_check_match_4',
       'released_in_india_2nd_check_match_5',
       'released_in_india_2nd_check_match_6',
       'released_in_india_2nd_check_match_7',
       'released_in_india_2nd_check_match_8',
       'released_in_india_2nd_chec

In [374]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v3', index = False)

In [375]:
master_list_df_reconstituted_again['domestic_box_office_ranked'] = master_list_df_reconstituted_again.groupby(['year'])['domestic_box_office'].rank(ascending=False)

In [376]:
#master_list_df_reconstituted_no.loc[(master_list_df_reconstituted_no['released_in_india_2nd_check'] == 'yes')]

master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['domestic_box_office_ranked'] == 1]

number  year                                 title  domestic_box_office  \
762        5  2013       The Hunger Games: Catching Fire            424668047   
900     5117  2018                         Black Panther            700059566   
1036    2887  2016          Rogue One: A Star Wars Story            532177324   
244      799  2014                       American Sniper            350126372   
311     3857  2017     Star Wars Ep. VIII: The Last Jedi            620181382   
432     1736  2015  Star Wars Ep. VII: The Force Awakens            936662225   

      international_box_office  production_budget domestic_release_date  \
762                  424668047          130000000            2013-11-22   
900                  700059566          200000000            2018-02-16   
1036                 532177324          200000000            2016-12-16   
244                  350126372           58000000            2014-01-16   
311                  620181382          317000000            2017-12-15   
432                  936662225          306000000            2015-12-18   

     domestic_distributor mpaa_rating                  franchise  \
762             Lionsgate       PG-13               Hunger Games   
900           Walt Disney       PG-13  Marvel Cinematic Universe   
1036          Walt Disney       PG-13                  Star Wars   
244          Warner Bros.           R                        NaN   
311           Walt Disney       PG-13                  Star Wars   
432           Walt Disney       PG-13                  Star Wars   

                ...             released_in_india_2nd_check_match_8  \
762             ...                                             yes   
900             ...                                             yes   
1036            ...                                             yes   
244             ...                                             yes   
311             ...                                              no   
432             ...                                              no   

     released_in_india_2nd_check_match_1_bms_csv_text  \
762                                                     
900                                                     
1036                                                    
244                               An American Promise   
311                                                     
432                                                     

     released_in_india_2nd_check_match_2_bms_csv_text  \
762                                                     
900                                                     
1036                                                    
244                                   American Hustle   
311                                                     
432                                                     

     released_in_india_2nd_check_match_3_bms_csv_text  \
762                                                     
900                                                     
1036                                                    
244                                   American Sniper   
311                                                     
432                                                     

     released_in_india_2nd_check_match_4_bms_csv_text  \
762                                                     
900                                                     
1036                                                    
244                                    American Ultra   
311                                                     
432                                                     

     released_in_india_2nd_check_match_5_bms_csv_text  \
762                                                     
900                                                     
1036                                                    
244                                 American Pastoral   
311                                                 

In [386]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v4', index = False)

In [387]:
master_list_df_reconstituted_again_no = master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes']

In [389]:
stop_words

['i',
 'me',
 'my',
 'myself',
 'we',
 'our',
 'ours',
 'ourselves',
 'you',
 "you're",
 "you've",
 "you'll",
 "you'd",
 'your',
 'yours',
 'yourself',
 'yourselves',
 'he',
 'him',
 'his',
 'himself',
 'she',
 "she's",
 'her',
 'hers',
 'herself',
 'it',
 "it's",
 'its',
 'itself',
 'they',
 'them',
 'their',
 'theirs',
 'themselves',
 'what',
 'which',
 'who',
 'whom',
 'this',
 'that',
 "that'll",
 'these',
 'those',
 'am',
 'is',
 'are',
 'was',
 'were',
 'be',
 'been',
 'being',
 'have',
 'has',
 'had',
 'having',
 'do',
 'does',
 'did',
 'doing',
 'a',
 'an',
 'the',
 'and',
 'but',
 'if',
 'or',
 'because',
 'as',
 'until',
 'while',
 'of',
 'at',
 'by',
 'for',
 'with',
 'about',
 'against',
 'between',
 'into',
 'through',
 'during',
 'before',
 'after',
 'above',
 'below',
 'to',
 'from',
 'up',
 'down',
 'in',
 'out',
 'on',
 'off',
 'over',
 'under',
 'again',
 'further',
 'then',
 'once',
 'here',
 'there',
 'when',
 'where',
 'why',
 'how',
 'all',
 'any',
 'both',
 'each

In [390]:
#doing one more check, just this time I'm checking if all the words from the bookmyshow title are there in the official US title to get us matches

import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in master_list_df_reconstituted_again_no.iterrows():
    
#     print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ")
    
    for indexx,rowx in bms_release_list.iterrows():

        bms_title = simplify_title(rowx['title'])

        bms_title_words = bms_title.split(' ')

        if all(word in scraped_title_words for word in bms_title_words): #the order for this was reversed in my earlier searches

            print('This title from BookMyShow india release list -- {} -- could be a match for this official US title -- {}. The index number for official US title in master_list_xxx_dataframe is {}'\
                  .format(rowx['title'],row['title'],index))

            break

        else:

            continue
        
print("DONE AND DONE")

This title from BookMyShow india release list -- Spy -- could be a match for this official US title -- The Catcher Was A Spy. The index number for official US title in master_list_xxx_dataframe is 1
This title from BookMyShow india release list -- Room -- could be a match for this official US title -- War Room. The index number for official US title in master_list_xxx_dataframe is 27
This title from BookMyShow india release list -- Pete's Dragon -- could be a match for this official US title -- Pete's Dragon. The index number for official US title in master_list_xxx_dataframe is 44
This title from BookMyShow india release list -- All the Money in the World -- could be a match for this official US title -- All the Money in the World. The index number for official US title in master_list_xxx_dataframe is 45
This title from BookMyShow india release list -- Fifty Shades Darker -- could be a match for this official US title -- Fifty Shades Darker. The index number for official US title in m

In [391]:
#not taking into account multiple matches

#doing one more check, just this time I'm checking if all the words from the bookmyshow title are there in the official US title to get us matches

import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in master_list_df_reconstituted_again_no.iterrows():
    
#     print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ")
    
#     scraped_title_words = [word for word in scraped_title_words if word not in stop_words]
    
    
    for indexx,rowx in bms_release_list.iterrows():

        bms_title = simplify_title(rowx['title'])

        bms_title_words = bms_title.split(' ')

        if set(scraped_title_words) == set(bms_title_words): #the order for this was reversed in my earlier searches

            print('This title from BookMyShow india release list -- {} -- could be a match for this official US title -- {}. The index number for official US title in master_list_xxx_dataframe is {}'\
                  .format(rowx['title'],row['title'],index))

            break

        else:

            continue
        
print("DONE AND DONE")


This title from BookMyShow india release list -- Pete's Dragon -- could be a match for this official US title -- Pete's Dragon. The index number for official US title in master_list_xxx_dataframe is 44
This title from BookMyShow india release list -- All the Money in the World -- could be a match for this official US title -- All the Money in the World. The index number for official US title in master_list_xxx_dataframe is 45
This title from BookMyShow india release list -- Fifty Shades Darker -- could be a match for this official US title -- Fifty Shades Darker. The index number for official US title in master_list_xxx_dataframe is 73
This title from BookMyShow india release list -- Live By Night -- could be a match for this official US title -- Live by Night. The index number for official US title in master_list_xxx_dataframe is 249
This title from BookMyShow india release list -- Patriots Day -- could be a match for this official US title -- Patriots Day. The index number for offici

In [392]:
#doing one more check, just this time I'm checking if all the words from the bookmyshow title are there in the official US title to get us matches

import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in master_list_df_reconstituted_again_no.iterrows():
    
#     print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ")
    
    for indexx,rowx in bms_release_list.iterrows():

        bms_title = simplify_title(rowx['title'])

        bms_title_words = bms_title.split(' ')

        if all(word in bms_title_words for word in scraped_title_words):

            print('This title from BookMyShow india release list -- {} -- could be a match for this official US title -- {}. The index number for official US title in master_list_xxx_dataframe is {}'\
                  .format(rowx['title'],row['title'],index))

            break

        else:

            continue
        
print("DONE AND DONE")

This title from BookMyShow india release list -- Pete's Dragon -- could be a match for this official US title -- Pete's Dragon. The index number for official US title in master_list_xxx_dataframe is 44
This title from BookMyShow india release list -- All the Money in the World -- could be a match for this official US title -- All the Money in the World. The index number for official US title in master_list_xxx_dataframe is 45
This title from BookMyShow india release list -- Fifty Shades Darker -- could be a match for this official US title -- Fifty Shades Darker. The index number for official US title in master_list_xxx_dataframe is 73
This title from BookMyShow india release list -- Beauty and the Beast -- could be a match for this official US title -- Beast. The index number for official US title in master_list_xxx_dataframe is 97
This title from BookMyShow india release list -- Beyond All Boundaries -- could be a match for this official US title -- Boundaries. The index number for o

In [396]:
master_list_df_reconstituted_again_no.loc[master_list_df_reconstituted_again_no['title'].str.contains("It")]

number  year           title  domestic_box_office  \
349     917  2014  And So It Goes             15160801   
381    5193  2018          Itzhak               618626   
408     994  2014     Life Itself               810454   

     international_box_office  production_budget domestic_release_date  \
349                  15160801           18000000            2014-07-25   
381                    618626                  0            2018-03-09   
408                    810454                  0            2014-07-04   

      domestic_distributor mpaa_rating franchise            ...              \
349  Clarius Entertainment       PG-13       NaN            ...               
381              Greenwich   Not Rated       NaN            ...               
408      Magnolia Pictures           R       NaN            ...               

    released_in_india_2nd_check_match_8  \
349                                  no   
381                                  no   
408                                  no   

    released_in_india_2nd_check_match_1_bms_csv_text  \
349                                                    
381                                                    
408                                             Life   

    released_in_india_2nd_check_match_2_bms_csv_text  \
349                                                    
381                                                    
408                                                    

    released_in_india_2nd_check_match_3_bms_csv_text  \
349                                                    
381                                                    
408                                                    

    released_in_india_2nd_check_match_4_bms_csv_text  \
349                                                    
381                                                    
408                                                    

    released_in_india_2nd_check_match_5_bms_csv_text  \
349                                                    
381                                                    
408                                                    

    released_in_india_2nd_check_match_6_bms_csv_text  \
349                                                    
381                                                    
408                                                    

    released_in_india_2nd_check_match_7_bms_csv_text  \
349                                                    
381                                                    
408                                                    

    released_in_india_2nd_check_match_8_bms_csv_text  \
349                                                    
381                                                    
408                                                    

    domestic_box_office_ranked  
349                      116.0  
381                       98.0  
408                      176.0  

[3 rows x 43 columns]

In [397]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['title'].str.contains("Life Itself")]

number  year        title  domestic_box_office  international_box_office  \
408     994  2014  Life Itself               810454                    810454   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
408                  0            2014-07-04    Magnolia Pictures           R   

    franchise            ...             released_in_india_2nd_check_match_8  \
408       NaN            ...                                              no   

    released_in_india_2nd_check_match_1_bms_csv_text  \
408                                             Life   

    released_in_india_2nd_check_match_2_bms_csv_text  \
408                                                    

    released_in_india_2nd_check_match_3_bms_csv_text  \
408                                                    

    released_in_india_2nd_check_match_4_bms_csv_text  \
408                                                    

    released_in_india_2nd_check_match_5_bms_csv_text  \
408                                                    

    released_in_india_2nd_check_match_6_bms_csv_text  \
408                                                    

    released_in_india_2nd_check_match_7_bms_csv_text  \
408                                                    

    released_in_india_2nd_check_match_8_bms_csv_text  \
408                                                    

    domestic_box_office_ranked  
408                      176.0  

[1 rows x 43 columns]

In [398]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text', 'released_in_india',
       'released_in_india_2nd_check', 'released_in_india_2nd_check_match_1',
       'released_in_india_2nd_check_match_2',
       'released_in_india_2nd_check_match_3',
       'released_in_india_2nd_check_match_4',
       'released_in_india_2nd_check_match_5',
       'released_in_india_2nd_check_match_6',
       'released_in_india_2nd_check_match_7',
       'released_in_india_2nd_check_match_8',
       'released_in_india_2nd_chec

In [399]:
correction_list_3 = [44,45,249,433, 85,382]

for index_number in correction_list_3:
    master_list_df_reconstituted_again.loc[index_number,'released_in_india_2nd_check'] = 'yes'

In [400]:
master_list_df_reconstituted_again_no = master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes']

In [401]:
import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in master_list_df_reconstituted_again_no.iterrows():
    
#     print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ")
    
    for indexx,rowx in bms_release_list.iterrows():

        bms_title = simplify_title(rowx['title'])

        bms_title_words = bms_title.split(' ')

        if set(scraped_title_words) == set(bms_title_words):

            print('This title from BookMyShow india release list -- {} -- could be a match for this official US title -- {}. The index number for official US title in master_list_xxx_dataframe is {}'\
                  .format(rowx['title'],row['title'],index))

            break

        else:

            continue
        
print("DONE AND DONE")

This title from BookMyShow india release list -- Fifty Shades Darker -- could be a match for this official US title -- Fifty Shades Darker. The index number for official US title in master_list_xxx_dataframe is 73
DONE AND DONE


In [12]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v5.csv', index = False)

In [62]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v5.csv')

In [63]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text', 'released_in_india',
       'released_in_india_2nd_check', 'released_in_india_2nd_check_match_1',
       'released_in_india_2nd_check_match_2',
       'released_in_india_2nd_check_match_3',
       'released_in_india_2nd_check_match_4',
       'released_in_india_2nd_check_match_5',
       'released_in_india_2nd_check_match_6',
       'released_in_india_2nd_check_match_7',
       'released_in_india_2nd_check_match_8',
       'released_in_india_2nd_chec

In [64]:
master_list_df_reconstituted_again['released_in_india_3rd_check'] = master_list_df_reconstituted_again['released_in_india_2nd_check']

In [65]:
master_list_df_reconstituted_again['released_in_india_3rd_check_match_1'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_2'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_3'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_4'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_5'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_6'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_7'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_8'] = ""

In [66]:
master_list_df_reconstituted_again['released_in_india_3rd_check_match_1_bms_csv_text'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_2_bms_csv_text'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_3_bms_csv_text'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_4_bms_csv_text'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_5_bms_csv_text'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_6_bms_csv_text'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_7_bms_csv_text'] = ""

master_list_df_reconstituted_again['released_in_india_3rd_check_match_8_bms_csv_text'] = ""

In [67]:
master_list_df_reconstituted_again_yes = master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_3rd_check'] == 'yes']

master_list_df_reconstituted_again_no = master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_3rd_check'] != 'yes']

In [68]:
bms_release_list = pd.read_csv("data/bookmyshow_list.csv")

In [69]:
bms_release_list.rename(columns={'Release_Year': 'release_year',
                                  'EventGroup_strTitle':'title',
                                  'Event_dtmReleaseDate':'release_date'}, inplace=True)

In [70]:
#this is the same check as I did above, just that i'm not using all the stopwords, just a minimal list

import unicodedata
import re
from lxml import html
from random import randint
import time
import itertools


def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&"]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    for before, after in (('ß', 'ss'), ('Æ', 'AE'), ('æ', 'ae'), ('Œ', 'OE'),\
                          ('œ', 'oe'),('ﬁ','fi'),('ﬂ','fl'),('ø','oe'),('Ð','D'),('Þ','TH')\
                          # put any more transformations here...
                          ):
        data = data.replace(before, after)
        
    data = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    data = str(data,'utf-8')

    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

for index,row in master_list_df_reconstituted_again_no.iterrows():
    
    print(index)
    
    scraped_title = simplify_title(row['title'])

    scraped_title_words = scraped_title.split(" ") #we get a list of words here
    
    minimal_stop_word_list = ['the','a','of','I','to','in']
    
    if any(elem in scraped_title_words for elem in minimal_stop_word_list):
        
        scraped_title_words = [x for x in scraped_title_words if x not in minimal_stop_word_list]
    
    len_scraped_title_words = len(scraped_title_words)
    
    if len_scraped_title_words == 0:
        
        print('no words to search for title -- {}'.format(row['title']))
        
        continue
        
    elif len_scraped_title_words == 1:
        
        for indexx,rowx in bms_release_list.iterrows():

            bms_title = simplify_title(rowx['title'])

            bms_title_words = bms_title.split(' ')
            
            if (set(bms_title_words) == set(scraped_title_words)):
                
                master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_1'] = 'yes'
                
                master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_1_bms_csv_text'] = rowx['title']
                
                break
            
            else:
                
                continue
            
        continue
        
    elif len_scraped_title_words > 1:
        
        scraped_title_words_combo_list = list(itertools.combinations(scraped_title_words, (len_scraped_title_words - 1))) #you get a list of tuples here
        
        #if you want to understand what's going on here, list(itertools.combinations([1,2,3], 2)) gives us [(1, 2), (1, 3), (2, 3)]
        
        iteratorx = 0
        
        #you have the pass statement available to you as well

        #what happens if we don't even get a 1st match?

        for indexx,rowx in bms_release_list.iterrows():

            bms_title = simplify_title(rowx['title'])

            bms_title_words = bms_title.split(' ')
            
            if iteratorx == 0:
            
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_1'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_1_bms_csv_text'] = rowx['title']

                        iteratorx = 1

                        break

                    else:

                        continue
                
                continue
            
            elif iteratorx == 1:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_2'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_2_bms_csv_text'] = rowx['title']

                        iteratorx = 2

                        break

                    else:

                        continue
                
                continue
            
            elif iteratorx == 2:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_3'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_3_bms_csv_text'] = rowx['title']

                        iteratorx = 3

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 3:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_4'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_4_bms_csv_text'] = rowx['title']

                        iteratorx = 4

                        break

                    else:

                        continue
                
                continue
                
                
            elif iteratorx == 4:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_5'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_5_bms_csv_text'] = rowx['title']

                        iteratorx = 5

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 5:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_6'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_6_bms_csv_text'] = rowx['title']

                        iteratorx = 6

                        break

                    else:

                        continue
                
                continue
                
            elif iteratorx == 6:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_7'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_7_bms_csv_text'] = rowx['title']

                        iteratorx = 7

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 7:
                
                for combo in scraped_title_words_combo_list:

                    if all(word in bms_title_words for word in combo):

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_8'] = 'yes'

                        master_list_df_reconstituted_again_no.loc[index,'released_in_india_3rd_check_match_8_bms_csv_text'] = rowx['title']

                        iteratorx = 8

                        break

                    else:

                        continue
                
                continue

            elif iteratorx == 8:

                break

        continue

print("DONE AND DONE")

634
635
636
637
639
640
641
642
643
644
645
648


/home/shijith/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:517: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


649
650
651
652
653
654
655
656
657
659
660
661
662
664
666
667
668
669
670
671
672
673
674
679
680
682
685
687
690
691
693
696
698
699
700
701
703
704
706
707
708
709
710
712
714
715
717
720
721
722
724
726
727
729
730
731
732
733
735
736
738
740
741
742
743
744
745
746
748
749
750
751
752
755
756
757
758
759
760
763
764
766
768
769
774
775
776
777
780
783
784
785
786
787
788
789
791
793
794
795
796
797
798
800
801
803
804
807
808
810
812
813
814
816
817
818
822
824
825
826
827
828
829
831
832
833
834
835
837
840
843
844
846
847
849
850
851
852
853
855
856
857
859
860
861
862
863
864
865
868
869
870
871
873
875
879
880
881
884
885
886
887
893
894
896
900
901
902
903
906
908
909
912
913
917
918
920
921
922
923
924
925
926
927
928
931
933
935
936
937
938
939
940
941
942
943
945
946
947
948
951
952
954
956
957
958
959
961
963
965
966
967
968
969
970
972
974
975
977
978
979
980
982
983
984
985
986
988
989
990
991
993
995
996
998
1001
1002
1005
1007
1008
1010
1011
1013
1014
1024
1025
1028


In [71]:
pd.set_option('display.max_rows', 500)

In [72]:
master_list_df_reconstituted_again_no_for_check = master_list_df_reconstituted_again_no.loc[(master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_1'] == 'yes') |
                                                 (master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_2'] == 'yes') |
                                                 (master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_3'] == 'yes') |
                                                 (master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_4'] == 'yes') |
                                                 (master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_5'] == 'yes') |
                                                 (master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_6'] == 'yes') |
                                                 (master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_7'] == 'yes') |
                                                 (master_list_df_reconstituted_again_no['released_in_india_3rd_check_match_8'] == 'yes') ]

In [73]:
master_list_df_reconstituted_again_no_for_check.loc[:, ['title',
                                                  'released_in_india_3rd_check_match_1_bms_csv_text',
                                                  'released_in_india_3rd_check_match_2_bms_csv_text',
                                                  'released_in_india_3rd_check_match_3_bms_csv_text',
                                                  'released_in_india_3rd_check_match_4_bms_csv_text',
                                                  'released_in_india_3rd_check_match_5_bms_csv_text',
                                                  'released_in_india_3rd_check_match_6_bms_csv_text',
                                                  'released_in_india_3rd_check_match_7_bms_csv_text',
                                                  'released_in_india_3rd_check_match_8_bms_csv_text']]

title  \
648                    Wind River   
649                  Love & Mercy   
650                    Girls Trip   
656            Fifty Shades Freed   
661                      War Room   
667                   Tulip Fever   
669            A Beautiful Planet   
670         Fifty Shades of Black   
671                      Range 15   
674              The Fluffy Movie   
690                 Obvious Child   
691                   Cartel Land   
696            The Eagle Huntress   
698                    All Saints   
701           The Spectacular Now   
706           Fifty Shades Darker   
712               Best of Enemies   
731                 A Ghost Story   
744                Irrational Man   
746                      99 Homes   
751                         56 Up   
758                   Filly Brown   
764               Beyond the Mask   
774              The Glass Castle   
775                    Lazer Team   
793                     Every Day   
795                 The Last Word   
801                  City of Gold   
807                      Red Army   
808                       50 to 1   
814             The Wrecking Crew   
818              Mistress America   
825                    Little Men   
826             Beyond the Lights   
827   Kumiko, The Treasure Hunter   
831                 Bad Samaritan   
833                     Black Sea   
843              Love the Coopers   
847                    L'attentat   
868               Unfinished Song   
884               A Haunted House   
896                 Dead Man Down   
901                      Top Five   
908        Magic in the Moonlight   
918             A Matter of Faith   
926                The One I Love   
933                 Born in China   
936             The Perfect Match   
937                  The Good Lie   
941                   The D Train   
946           The Lady in the Van   
959            The Miracle Season   
966                   St. Vincent   
967                Particle Fever   
980              American Animals   
990          The Belko Experiment   
1005          The End of the Tour   
1013                To the Wonder   
1024                     Home Run   
1025     Tyler Perry's Temptation   
1028            The Young Messiah   
1035               First Reformed   
1041                  Life Itself   
1044                    Show Dogs   
1045                Welcome to Me   
1046                       Fed Up   
1049                   Ride Along   
1051              Harry & Snowman   
1055                Old Fashioned   
1063            Captain Fantastic   

     released_in_india_3rd_check_match_1_bms_csv_text  \
648                              Brothers Of The Wind   
649                      All the Boys Love Mandy Lane   
650                                Asian School Girls   
656                              Fifty Shades of Grey   
661                                      World War Z    
667                                      Comedy Fever   
669                               Beautiful Creatures   
670                              Fifty Shades of Grey   
671                                The 15:17 to Paris   
674                                     Scary Movie 5   
690                                      Child Of God   
691                                     Promised Land   
696                                   Eddie The Eagle   
698                          All I Want Is Everything   
701                                    Now You See Me   
706                              Fifty Shades of Grey   
712                                     Best Man Down   
731          We Steal Secrets: The Story of Wikileaks   
744                                       Iron Man 3    
746                            Brawl in Cell Block 99   
751                                         Get On Up   
758       Snoopy and Charlie Brown: The Peanuts Movie   
764                        The Place Beyond the Pines   
774               Enchanted Cast

In [ ]:
#cool, have done another check, no corrections to be made, think we've got all the titles that have been released

In [74]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v5.csv')

In [79]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries', 'all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text', 'released_in_india',
       'released_in_india_2nd_check', 'released_in_india_2nd_check_match_1',
       'released_in_india_2nd_check_match_2',
       'released_in_india_2nd_check_match_3',
       'released_in_india_2nd_check_match_4',
       'released_in_india_2nd_check_match_5',
       'released_in_india_2nd_check_match_6',
       'released_in_india_2nd_check_match_7',
       'released_in_india_2nd_check_match_8',
       'released_in_india_2nd_chec

In [81]:
column_drop_list = ['all_words_there',
       'all_words_there_bms_csv_text', 'exact_match',
       'exact_match_bms_csv_text', 'after_stopwords_removed',
       'after_stopwords_removed_bms_csv_text', 'words_same',
       'words_same_bms_csv_text', 'released_in_india', 'released_in_india_2nd_check_match_1',
       'released_in_india_2nd_check_match_2',
       'released_in_india_2nd_check_match_3',
       'released_in_india_2nd_check_match_4',
       'released_in_india_2nd_check_match_5',
       'released_in_india_2nd_check_match_6',
       'released_in_india_2nd_check_match_7',
       'released_in_india_2nd_check_match_8',
       'released_in_india_2nd_check_match_1_bms_csv_text',
       'released_in_india_2nd_check_match_2_bms_csv_text',
       'released_in_india_2nd_check_match_3_bms_csv_text',
       'released_in_india_2nd_check_match_4_bms_csv_text',
       'released_in_india_2nd_check_match_5_bms_csv_text',
       'released_in_india_2nd_check_match_6_bms_csv_text',
       'released_in_india_2nd_check_match_7_bms_csv_text',
       'released_in_india_2nd_check_match_8_bms_csv_text']


In [ ]:
master_list_df_reconstituted_again.drop(column_drop_list, axis=1, inplace=True)

In [ ]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v6.csv', index=False)

In [1]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v6.csv')

In [2]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office',
       'international_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries',
       'released_in_india_2nd_check', 'domestic_box_office_ranked'],
      dtype='object')

In [3]:
master_list_df_reconstituted_again['source'].unique()

array(['Based on Theme Park Ride', 'Original Screenplay',
       'Based on Fiction Book/Short Story', 'Based on Real Life Events',
       'Based on Comic/Graphic Novel', 'Remake', 'Based on TV',
       'Based on Game', 'Based on Factual Book/Article', 'Based on Toy',
       'Based on Folk Tale/Legend/Fairytale', 'Based on Religious Text',
       'Based on Movie', 'Spin-Off', 'Based on Short Film',
       'Based on Play', 'Based on Web Series', 'Based on Musical Group',
       nan, 'Compilation', 'Based on Musical or Opera', 'Based on Song'], dtype=object)

In [4]:
master_list_df_reconstituted_again['genre'].unique()

array(['Adventure', 'Drama', 'Action', 'Thriller/Suspense', 'Horror',
       'Comedy', 'Concert/Performance', 'Romantic Comedy', 'Musical',
       'Black Comedy', 'Western', 'Documentary', 'Multiple Genres'], dtype=object)

In [5]:
master_list_df_reconstituted_again['production_method'].unique()

array(['Live Action', 'Animation/Live Action', 'Digital Animation',
       'Stop-Motion Animation', nan, 'Multiple Production Methods'], dtype=object)

In [6]:
master_list_df_reconstituted_again['creative_type'].unique()

array(['Fantasy', 'Contemporary Fiction', 'Science Fiction',
       'Dramatization', 'Super Hero', 'Kids Fiction', 'Factual',
       'Historical Fiction', 'Multiple Creative Types', nan], dtype=object)

In [18]:
master_list_df_reconstituted_again[master_list_df_reconstituted_again['domestic_box_office_ranked'] <= 50].groupby(['released_in_india_2nd_check', 'genre']).size()

released_in_india_2nd_check  genre            
no                           Comedy                4
                             Drama                 4
                             Romantic Comedy       2
                             Thriller/Suspense     2
yes                          Action               72
                             Adventure            80
                             Black Comedy          2
                             Comedy               44
                             Drama                35
                             Horror               18
                             Musical               9
                             Thriller/Suspense    26
                             Western               2
dtype: int64

In [29]:
top_number = 50

df = pd.DataFrame(columns=["genre", "total","yes","no","yes %","no %"])

for genre in master_list_df_reconstituted_again['genre'].unique():
    movies_in_genre = len(master_list_df_reconstituted_again[(master_list_df_reconstituted_again['genre'] == genre) &
                         (master_list_df_reconstituted_again['domestic_box_office_ranked'] <= top_number)])
    movies_in_genre_released_india_yes = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genre'] == genre) &
                                                                                    (master_list_df_reconstituted_again['domestic_box_office_ranked'] <= top_number) &
                                                                                    (master_list_df_reconstituted_again['released_in_india_2nd_check'] == 'yes') ])
    movies_in_genre_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genre'] == genre) &
                                                                                   (master_list_df_reconstituted_again['domestic_box_office_ranked'] <= top_number) &
                                                                                   (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') ])
    if movies_in_genre != 0:
        movies_in_genre_released_india_yes_percent = (movies_in_genre_released_india_yes/movies_in_genre)*100
        movies_in_genre_released_india_yes_percent = round(movies_in_genre_released_india_yes_percent,1)
        movies_in_genre_released_india_no_percent = (movies_in_genre_released_india_no/movies_in_genre)*100
        movies_in_genre_released_india_no_percent = round(movies_in_genre_released_india_no_percent,1)
    else:
        movies_in_genre_released_india_yes_percent = 0
        movies_in_genre_released_india_no_percent = 0
    
    df = df.append({"genre": genre,
                    "total": movies_in_genre,
                    "yes": movies_in_genre_released_india_yes,
                    "no": movies_in_genre_released_india_no,
                    "yes %": movies_in_genre_released_india_yes_percent,
                    "no %": movies_in_genre_released_india_no_percent
                    }, ignore_index=True)

#     print("if we look at the top {} movies in terms of US domestic gross, there were {} movies in the genre {}.".format(top_number, movies_in_genre,genre,))
#     print("{} movies were released in India, that is {} %. {} movies were not released in India, that is {} %.".format(movies_in_genre_released_india_yes,movies_in_genre_released_india_yes_percent,
#                                                                                                                       movies_in_genre_released_india_no,movies_in_genre_released_india_no_percent))
#     print("\n")
df
# print("### DONE AND DONE ###")    

genre total yes no  yes %   no %
0             Adventure    80  80  0  100.0    0.0
1                 Drama    39  35  4   89.7   10.3
2                Action    72  72  0  100.0    0.0
3     Thriller/Suspense    28  26  2   92.9    7.1
4                Horror    18  18  0  100.0    0.0
5                Comedy    48  44  4   91.7    8.3
6   Concert/Performance     0   0  0    0.0    0.0
7       Romantic Comedy     2   0  2    0.0  100.0
8               Musical     9   9  0  100.0    0.0
9          Black Comedy     2   2  0  100.0    0.0
10              Western     2   2  0  100.0    0.0
11          Documentary     0   0  0    0.0    0.0
12      Multiple Genres     0   0  0    0.0    0.0

In [22]:
#this gives us number of nan values in each column

master_list_df_reconstituted_again.isnull().sum()

number                           0
year                             0
title                            0
domestic_box_office              0
international_box_office         0
production_budget                0
domestic_release_date           15
domestic_distributor             9
mpaa_rating                      0
franchise                      836
source                           1
genre                            0
production_method                1
creative_type                    1
production_companies            54
production_countries             0
released_in_india_2nd_check      0
domestic_box_office_ranked       0
dtype: int64

In [23]:
#this gets us non-zero values in each column, note that Nan values are counted as non-zero

master_list_df_reconstituted_again.astype(bool).sum(axis=0)

number                         1078
year                           1078
title                          1078
domestic_box_office            1078
international_box_office       1078
production_budget               758
domestic_release_date          1078
domestic_distributor           1078
mpaa_rating                    1078
franchise                      1078
source                         1078
genre                          1078
production_method              1078
creative_type                  1078
production_companies           1078
production_countries           1078
released_in_india_2nd_check    1078
domestic_box_office_ranked     1078
dtype: int64

In [50]:
master_list_df_reconstituted_again.iloc[649]

number                                                                   1866
year                                                                     2015
title                                                            Love & Mercy
domestic_box_office                                                  12551031
international_box_office                                             12551031
production_budget                                                           0
domestic_release_date                                              2015-06-05
domestic_distributor                                     Roadside Attractions
mpaa_rating                                                             PG-13
franchise                                                                 NaN
source                                              Based on Real Life Events
genre                                                                   Drama
production_method                                               

In [ ]:
#just realised that the international box_office column is a duplicate of the domestic box office column, yikes, that must have happened during the scraping, after checking the pages, the domestic box office numbers
    #are ok, but the international box office numbers are wrong, don't need that column anyway, so am just going to drop it from the data frame
    


In [51]:
master_list_df_reconstituted_again.drop("international_box_office", axis=1, inplace=True)

In [52]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v7.csv', index=False)

In [73]:
#of all the movies where you have production budget information, find the ones with the biggest production budgets that weren't released in India


master_list_df_reconstituted_again['production_budget'].max()

330600000

In [104]:
import numpy

bins = numpy.arange(start=0,stop=350000000,step=25000000)
list(bins)


[0,
 25000000,
 50000000,
 75000000,
 100000000,
 125000000,
 150000000,
 175000000,
 200000000,
 225000000,
 250000000,
 275000000,
 300000000,
 325000000]

In [107]:
master_list_df_reconstituted_again[master_list_df_reconstituted_again['production_budget'] > 0]['production_budget'].min()

100000

In [108]:
master_list_df_reconstituted_again[master_list_df_reconstituted_again['production_budget'] > 0]['production_budget'].max()

330600000

In [141]:
bins =   [0,100000, 25000000,50000000, 75000000, 100000000, 125000000, 150000000, 175000000, 200000000, 225000000, 250000000, 275000000, 300000000, 325000000,350000000]

In [142]:
len(bins)

16

In [143]:
labels = ['no info','100k-25m','25m-50m','50m-75m','75m-100m','100m-125m','125m-150m','150m-175m','175m-200m','200m-225m','225m-250m','250m-275m', '275m-300m','300m-325m','325m-350m']

In [145]:
master_list_df_reconstituted_again['production_budget_bins'] = pd.cut(master_list_df_reconstituted_again['production_budget'], bins = bins, labels = labels, right = False, include_lowest = True)

In [146]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v8.csv', index=False)

In [159]:
master_list_df_reconstituted_again['domestic_box_office'].min()

500000

In [160]:
master_list_df_reconstituted_again['domestic_box_office'].max()

936662225

In [162]:
bins =   [500000, 50000000, 100000000, 150000000, 200000000, 250000000, 300000000, 350000000,400000000, 450000000,500000000, 550000000,600000000, 650000000,700000000, 750000000,800000000, 850000000,900000000, 950000000]

In [163]:
labels = ['50k-50m','50m-100m','100m-150m','150m-200m','200m-250m','250m-300m','300m-350m','350m-400m','400m-450m','450m-500m','500m-550m','550m-600m','600m-650m','650m-700m','700m-750m',
         '750m-800m','800m-850m','850m-900m','900m-950m']

In [166]:
master_list_df_reconstituted_again['domestic_box_office_bins'] = pd.cut(master_list_df_reconstituted_again['domestic_box_office'], bins = bins, labels = labels, right = False, include_lowest = True)

In [186]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v8.csv', index=False)

In [192]:
#just doing a check to see if we've got the year right, 

for index, row in master_list_df_reconstituted_again.iterrows():
    release_year = row['year']
    release_year = str(release_year)
    release_date = row['domestic_release_date']
    try:
        release_date[:4]
    except:
        print('no release date for {}'.format(row['number']))
    else:
        release_year_from_date = release_date[:4]
        if release_year != release_year_from_date:
            print('release year mismatch for {}'.format(row['number']))
            print(release_year)
            print(release_year_from_date)

print('done and done')

no release date for 148
no release date for 4054
no release date for 165
no release date for 3042
no release date for 4017
no release date for 3057
no release date for 4023
no release date for 1938
no release date for 3085
no release date for 3098
no release date for 5270
no release date for 3070
no release date for 4021
no release date for 4030
no release date for 927
done and done


In [79]:
#just adding a director column to help match titles better

import glob
from lxml import html

for index, row in master_list_df_reconstituted_again.iterrows():
    
    number = row['number']
    
    print(number)
    
    search_string = 'movie_pages/' + str(number).zfill(4) + '_*.html'

    for filename in glob.glob(search_string):

        with open(filename, encoding='utf-8') as filex:

            sourcex = filex.read()

            treex = html.document_fromstring(sourcex)

            try:
                treex.xpath("//td[@itemprop='director']//span[1]/text()")[0]
            except:
                print('no director for movie number {}'.format(number))
                director = ''
            else:
                director = treex.xpath("//td[@itemprop='director']//span[1]/text()")[0]
                
            try:
                treex.xpath("//td[@itemprop='director']//span[1]/text()")[1]
            except:
                pass
            else:
                director_two = treex.xpath("//td[@itemprop='director']//span[1]/text()")[1]
                director = director + ',' + director_two
                print('multiple directors for movie number {}'.format(number))

            master_list_df_reconstituted_again.loc[index,'director'] = director

print('done and done')

3867
multiple directors for movie number 3867
164
12
1834
851
3023
2895
3986
3074
217
3899
2927
837
3918
87
1786
2994
2903
1798
3104
2991
800
173
868
908
2896
5344
874
4015
5177
72
2987
1777
5503
5118
902
39
52
1753
69
2905
830
1877
40
2906
multiple directors for movie number 2906
22
833
18
3874
3014
103
130
160
2936
2956
129
3007
3100
797
multiple directors for movie number 797
176
3992
3858
3037
2977
3024
102
3907
1781
1737
2911
2935
2899
98
191
2909
1856
3953
68
3003
1754
1828
1787
1790
multiple directors for movie number 1790
64
2986
7
106
5434
3941
28
multiple directors for movie number 28
933
809
5062
848
5183
1772
63
3004
multiple directors for movie number 3004
3924
3022
3939
3047
2978
1766
1801
812
1760
1823
24
3131
182
875
790
834
multiple directors for movie number 834
872
1905
2941
889
126
3947
141
62
3875
131
3905
1768
23
793
multiple directors for movie number 793
869
1897
862
1807
3909
multiple directors for movie number 3909
2928
1784
132
60
2988
3029
1740
multiple dire

1762
5345
5348
1886
5437
97
2995
994
1821
4030
5342
1985
972
3933
1941
836
135
3134
17
3120
3072
1937
927
214
5429
867
multiple directors for movie number 867
921
104
850
3019
903
1736
2982
3943
4035
1835
156
2949
4008
3923
880
4042
197
4050
done and done


In [80]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v8.csv', index=False)

In [1]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v8.csv')

In [2]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries',
       'released_in_india_2nd_check', 'domestic_box_office_ranked',
       'production_budget_bins', 'domestic_box_office_bins', 'director'],
      dtype='object')

In [3]:
master_list_df_reconstituted_again.head()

number  year                                             title  \
0    3867  2017  Pirates of the Caribbean: Dead Men Tell No Tales   
1     164  2013                                          The East   
2      12  2013                                       World War Z   
3    1834  2015                               Ricki and the Flash   
4     851  2014                                     Transcendence   

   domestic_box_office  production_budget domestic_release_date  \
0            172558876          230000000            2017-05-26   
1              2274649            6500000            2013-05-31   
2            202359711          190000000            2013-06-21   
3             26839498           18000000            2015-08-07   
4             23022309          100000000            2014-04-18   

  domestic_distributor mpaa_rating                 franchise  \
0          Walt Disney       PG-13  Pirates of the Caribbean   
1      Fox Searchlight       PG-13                       NaN   
2   Paramount Pictures       PG-13               World War Z   
3        Sony Pictures       PG-13                       NaN   
4         Warner Bros.       PG-13                       NaN   

                              source              genre production_method  \
0           Based on Theme Park Ride          Adventure       Live Action   
1                Original Screenplay              Drama       Live Action   
2  Based on Fiction Book/Short Story             Action       Live Action   
3                Original Screenplay              Drama       Live Action   
4                Original Screenplay  Thriller/Suspense       Live Action   

          creative_type                               production_companies  \
0               Fantasy       Walt Disney Pictures,Jerry Bruckheimer Films   
1  Contemporary Fiction                                   Scott Free Films   
2       Science Fiction  Skydance Productions,Hemisphere Media Capital,...   
3  Contemporary Fiction  Marc Platt Productions,Badwill Entertainment ,...   
4       Science Fiction                Straight Up Films,DMG Entertainment   

  production_countries released_in_india_2nd_check  \
0        United States                         yes   
1        United States                         yes   
2        United States                         yes   
3        United States                         yes   
4        United States                         yes   

   domestic_box_office_ranked production_budget_bins domestic_box_office_bins  \
0                        19.0              225m-250m                150m-200m   
1                       157.0               100k-25m                  50k-50m   
2                        13.0              175m-200m                200m-250m   
3                        86.0               100k-25m                  50k-50m   
4                       105.0              100m-125m                  50k-50m   

                        director  
0  Joachim Ronnin,Espen Sandberg  
1                            NaN  
2                            NaN  
3                 Jonathan Demme  
4                            NaN

In [4]:
#taking the password from a text file
with open('passwords_ignore.txt') as f:
    password = f.readline()

In [5]:
login_string = 'postgresql://postgres:' + password + '@localhost/imdb2'

In [6]:
from imdb import IMDb

ia = IMDb('s3', login_string, adultSearch=False)

In [113]:
#REWORKED CODE

import unidecode
import re

def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&",","]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    data = unidecode.unidecode(data)
    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

master_list_df_reconstituted_again['genres_imdb'] = None

for index,row in master_list_df_reconstituted_again.iterrows():
# for index,row in master_list_df_reconstituted_again.iloc[74:75].iterrows():
    
#     print('\n')
#     print(index)
    number = row['number']
    
    title = row['title']
    title_simplified = simplify_title(title)
    title_simplified_words = title_simplified.split(' ')
#     print('this is title_simplified_words {}'.format(title_simplified_words))

    year = row['year']
    year = str(year)
#     print('this is year {}'.format(year))
    
    director = row['director']
    
    if str(director) != 'nan':
        director_simplified = simplify_title(director)
        director_simplified_words = director_simplified.split(' ')
    else:
        director_simplified_words = ['ZZZZZZ']
    
#     print('this is director_simplified_words {}'.format(director_simplified_words))
    
    results  = ia.search_movie(title,results = 200)

    for result in results:
        result_ID = result.movieID
        movie = ia.get_movie(result_ID)
        try:
            movie['kind']
        except:
            pass
        else:
            kindx = movie['kind']
            if kindx == 'movie': #it could be tv episode too, so filtering them out

                titlex = movie['title']
                titlex_string_simplified = simplify_title(titlex)
    #             print('this is titlex_string_simplified {}'.format(titlex_string_simplified))

                try:
                    movie['year']
                except:
                    yearx = '0000'
                else:
                    yearx = movie['year']
                    yearx = str(yearx)
    #             print('this is yearx {}'.format(yearx))

                try:
                    movie['director']
                except:
                    directors_string_simplified = 'XXXXXX'
                else:
                    director_list = movie['director']
                    director_name_list = []

                    for director_item in director_list:
                        director_id = director_item.personID
                        director_object = ia.get_person(director_id)
                        director_name = director_object['name']
                        director_name_list.append(director_name)

                    directors_string = ",".join(director_name_list)
                    directors_string_simplified = simplify_title(directors_string)

    #             print('this is directors_string_simplified {}'.format(directors_string_simplified))

                true_count = [(all(substring in directors_string_simplified for substring in director_simplified_words)),
                              (all(substring in titlex_string_simplified for substring in title_simplified_words)),
                              (yearx == year)].count(True)

                if true_count == 3:
                    genres_imdb_raw = movie['genres']
                    genres_imdb = ','.join(genres_imdb_raw)
                    master_list_df_reconstituted_again.loc[index,'genres_imdb'] = genres_imdb
                    break

                elif true_count == 2:
                    genres_imdb_raw = movie['genres']
                    genres_imdb = ','.join(genres_imdb_raw)
                    master_list_df_reconstituted_again.loc[index,'genres_imdb'] = genres_imdb
    #                     print('only 2 of 3 conditions true for title "{}" and number {}'.format(title,number))
    #                     print('\n')
                    break
    
    if pd.isnull(master_list_df_reconstituted_again.loc[index,'genres_imdb']):
        print('no genres listed for {}, the number for the movie is {}, the index is {}'.format(title, number, index))
        print('\n')
        
print('\n')
print('done and done')

no genres listed for Unfriended, the number for the movie is 1812, the index is 149


no genres listed for Ratchet and Clank, the number for the movie is 3030, the index is 620


no genres listed for Planes: Fire and Rescue, the number for the movie is 835, the index is 621


no genres listed for Norman: The Moderate Rise and Tragic Fall of a New York Fixer, the number for the movie is 4000, the index is 639


no genres listed for The Met: Live in HD - Aida, the number for the movie is 165, the index is 655


no genres listed for 2013 Oscar Shorts, the number for the movie is 178, the index is 657


no genres listed for 2014 Oscar Shorts, the number for the movie is 959, the index is 682


no genres listed for 2018 Oscar Shorts, the number for the movie is 5126, the index is 703


no genres listed for The Music of Strangers: Yo-Yo Ma and the Silk Road Ensemble, the number for the movie is 3103, the index is 745


no genres listed for 56 Up, the number for the movie is 208, the index is

In [138]:
#so for a number of these movies, i searched manually on the website and got their imdb IDs, i can use these imdb IDs with the local database to retrieve genre information
#there are some documentaries in this list too, will decide later on whether to keep them or not
#will use this dict later on to input genres into the main dataframe

manual_genres_input = {
'1812':{'title':"Unfriended",'imdbID':"1691917",'genres':''},
'3030':{'title':"Ratchet and Clank",'imdbID':"2865120",'genres':''},
'0835':{'title':"Planes: Fire and Rescue",'imdbID':"2980706",'genres':''},
'4000':{'title':"Norman: The Moderate Rise and Tragic Fall of a New York Fixer",'imdbID':"4191702",'genres':''},
'3103':{'title':"The Music of Strangers: Yo-Yo Ma and the Silk Road Ensemble",'imdbID':"3549206",'genres':''},
'0208':{'title':"56 Up",'imdbID':"2147134",'genres':''},
'0920':{'title':"Tyler Perry's The Single Moms Club",'imdbID':"2465140",'genres':''},
'0184':{'title':"L'attentat",'imdbID':"0787442",'genres':''},
'1994':{'title':"Deli Man: The Movie",'imdbID':"4239548",'genres':''},
'0035':{'title':"Disney Planes",'imdbID':"1691917",'genres':''},
'0968':{'title':"Men, Women and Children",'imdbID':"3179568",'genres':''},
'0927':{'title':"Island of Lemurs: Madagascar",'imdbID':"3231010",'genres':''}
}

In [140]:
for key, value in manual_genres_input.items():
    imdb_id = manual_genres_input[key]['imdbID']
    moviex = ia.get_movie(imdb_id)
    moviex_genres_raw = moviex['genres']
    moviex_genres = ','.join(moviex_genres_raw)
    manual_genres_input[key]['genres'] = moviex_genres
    
print('done and done')

done and done


In [141]:
manual_genres_input

{'0035': {'genres': 'adventure,animation,comedy',
  'imdbID': '1691917',
  'title': 'Disney Planes'},
 '0184': {'genres': 'drama', 'imdbID': '0787442', 'title': "L'attentat"},
 '0208': {'genres': 'documentary', 'imdbID': '2147134', 'title': '56 Up'},
 '0835': {'genres': 'adventure,animation,comedy',
  'imdbID': '2980706',
  'title': 'Planes: Fire and Rescue'},
 '0920': {'genres': 'comedy,drama',
  'imdbID': '2465140',
  'title': "Tyler Perry's The Single Moms Club"},
 '0927': {'genres': 'adventure,biography,documentary',
  'imdbID': '3231010',
  'title': 'Island of Lemurs: Madagascar'},
 '0968': {'genres': 'comedy,drama',
  'imdbID': '3179568',
  'title': 'Men, Women and Children'},
 '1812': {'genres': 'adventure,animation,comedy',
  'imdbID': '1691917',
  'title': 'Unfriended'},
 '1994': {'genres': 'documentary',
  'imdbID': '4239548',
  'title': 'Deli Man: The Movie'},
 '3030': {'genres': 'action,adventure,animation',
  'imdbID': '2865120',
  'title': 'Ratchet and Clank'},
 '3103': {

In [142]:
master_list_df_reconstituted_again.dtypes

number                           int64
year                             int64
title                           object
domestic_box_office              int64
production_budget                int64
domestic_release_date           object
domestic_distributor            object
mpaa_rating                     object
franchise                       object
source                          object
genre                           object
production_method               object
creative_type                   object
production_companies            object
production_countries            object
released_in_india_2nd_check     object
domestic_box_office_ranked     float64
production_budget_bins          object
domestic_box_office_bins        object
director                        object
genres_imdb                     object
dtype: object

In [143]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v8.csv', index=False)

In [147]:
for key, value in manual_genres_input.items():
    genres_imdb = manual_genres_input[key]['genres']
    number = int(key)
    master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb'] = genres_imdb

print('done and done')

done and done


In [148]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == 968]['genres_imdb']

1033    comedy,drama
Name: genres_imdb, dtype: object

In [149]:
#deleting rows from dataframe which cant possibly be movies

delete_row_dict = {
'0165':{'title':"The Met: Live in HD - Aida"},
'0178':{'title':"2013 Oscar Shorts"},
'0959':{'title':"2014 Oscar Shorts"},
'5126':{'title':"2018 Oscar Shorts"},
'1917':{'title':"2015 Oscar Shorts"},
'4023':{'title':"Mayweather vs. McGregor"},
'1938':{'title':"Game of Thrones: The IMAX Experience"},
'4027':{'title':"2017 Oscar Shorts"},
'3085':{'title':"The Met: Live in HD - Madama Butterfly"},
'3098':{'title':"The Harry Potter IMAX Marathon"},
'1947':{'title':"The Met: Live in HD - Tannhauser"},
'3086':{'title':"The Met: Live in HD - Manon Lescaut"}
}

In [150]:
delete_row_list = [165,178,959,5126,1917,4023,1938,4027,3085,3098,1947,3086]

In [151]:
master_list_df_reconstituted_again = master_list_df_reconstituted_again[~(master_list_df_reconstituted_again['number'].isin(delete_row_list))]

In [152]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v9.csv', index=False)

In [153]:
genres_imdb_list = list(master_list_df_reconstituted_again['genres_imdb'].unique())
print(len(genres_imdb_list))
genres_imdb_list = [x for x in genres_imdb_list if str(x) != 'nan']
final_list = []
for genres_imdb in genres_imdb_list:
    list_to_add = [x.strip() for x in genres_imdb.split(",")]
    final_list.extend(list_to_add)
    
final_list = list(set(final_list))
print(len(final_list))

197
23


In [154]:
final_list

['',
 'musical',
 'action',
 'sci-fi',
 'war',
 'documentary',
 'news',
 'music',
 'adventure',
 'sport',
 'horror',
 'drama',
 'history',
 'fantasy',
 'thriller',
 'family',
 'western',
 'animation',
 'biography',
 'comedy',
 'romance',
 'mystery',
 'crime']

In [167]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['genres_imdb']=='']

number  year       title  domestic_box_office  production_budget  \
354     975  2014      Tracks               509815                  0   
804    5443  2018  Boundaries               701828                  0   

    domestic_release_date    domestic_distributor mpaa_rating franchise  \
354            2014-09-19           Weinstein Co.       PG-13       NaN   
804            2018-06-22  Sony Pictures Classics           R       NaN   

                        source     ...     production_method  \
354  Based on Real Life Events     ...           Live Action   
804        Original Screenplay     ...           Live Action   

            creative_type                               production_companies  \
354         Dramatization                                      See-Saw Films   
804  Contemporary Fiction  Automatik,Oddfellows Entertainment,Stage 6 Fil...   

     production_countries released_in_india_2nd_check  \
354         United States                         yes   
804  Canada,United States                          no   

    domestic_box_office_ranked  production_budget_bins  \
354                      188.0                 no info   
804                       97.0                 no info   

    domestic_box_office_bins     director genres_imdb  
354                  50k-50m  John Curran              
804                  50k-50m  Shana Feste              

[2 rows x 21 columns]

In [168]:
manual_genres_input = {
'0975':{'title':"Tracks",'imdbID':"2167266",'genres':''},
'5443':{'title':"Boundaries",'imdbID':"5686062",'genres':''}
}

for key, value in manual_genres_input.items():
    imdb_id = manual_genres_input[key]['imdbID']
    moviex = ia.get_movie(imdb_id)
    moviex_genres_raw = moviex['genres']
    moviex_genres = ','.join(moviex_genres_raw)
    manual_genres_input[key]['genres'] = moviex_genres

for key, value in manual_genres_input.items():
    genres_imdb = manual_genres_input[key]['genres']
    number = int(key)
    master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb'] = genres_imdb

print('done and done')

done and done


In [165]:
len_df = len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['genres_imdb'] == None])
len_df

0

In [180]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v9.csv', index=False)

In [183]:
#3080 stands for a row in the dataframe for '2016 Oscar Shorts' , am guessing it's a compilation of shorts nominated for the oscar and they're shown together as one package
#not counting this as a movie

delete_row_list_2 = [3080]

master_list_df_reconstituted_again = master_list_df_reconstituted_again[~(master_list_df_reconstituted_again['number'].isin(delete_row_list_2))]

master_list_df_reconstituted_again.to_csv('data/india_release_check_v9.csv', index=False)

In [209]:
#RUN THIS AT NIGHT

from imdb import IMDb

import unidecode
import re
from random import randint
import time

ib = IMDb(accessSystem='http', adultSearch=False)

def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&",","]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    data = unidecode.unidecode(data)
    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

master_list_df_reconstituted_again['genres_imdb_check'] = None

for index,row in master_list_df_reconstituted_again.iterrows():
    number = row['number']
    print('page number is {}'.format(number))
    
    title = row['title']
    title_simplified = simplify_title(title)
    title_simplified_words = title_simplified.split(' ')

    year = row['year']
    year = str(year)
    
    title_year = title + " " + year
    
    director = row['director']
    
    if str(director) != 'nan':
        director_simplified = simplify_title(director)
        director_simplified_words = director_simplified.split(' ')
    else:
        director_simplified_words = ['ZZZZZZ']
    
    results  = ib.search_movie(title_year)

    delay = 5
    time.sleep(delay)

    for result in results:
        result_ID = result.movieID
        movie = ia.get_movie(result_ID)  #using ia, the local postgres db instead

        try:
            movie['kind']
        except:
            pass
        else:
            kindx = movie['kind']
            if kindx == 'movie': #it could be tv episode too, so filtering them out

                titlex = movie['title']
                titlex_string_simplified = simplify_title(titlex)

                try:
                    movie['year']
                except:
                    yearx = '0000'
                else:
                    yearx = movie['year']
                    yearx = str(yearx)

                try:
                    movie['director']
                except:
                    directors_string_simplified = 'XXXXXX'
                else:
                    director_list = movie['director']
                    director_name_list = []

                    for director_item in director_list:
                        director_id = director_item.personID
                        director_object = ia.get_person(director_id)   #using ia instead of ib, that is local db instead of website

                        director_name = director_object['name']
                        director_name_list.append(director_name)

                    directors_string = ",".join(director_name_list)
                    directors_string_simplified = simplify_title(directors_string)

                true_count = [(all(substring in directors_string_simplified for substring in director_simplified_words)),
                              (all(substring in titlex_string_simplified for substring in title_simplified_words)),
                              (yearx == year)].count(True)

                if true_count == 3:
                    genres_imdb_raw = movie['genres']
                    genres_imdb = ','.join(genres_imdb_raw)
                    master_list_df_reconstituted_again.loc[index,'genres_imdb_check'] = genres_imdb
                    break

                elif true_count == 2:
                    genres_imdb_raw = movie['genres']
                    genres_imdb = ','.join(genres_imdb_raw)
                    master_list_df_reconstituted_again.loc[index,'genres_imdb_check'] = genres_imdb
                    break
    
    if pd.isnull(master_list_df_reconstituted_again.loc[index,'genres_imdb_check']):
        print('no genres listed for {}, the number for the movie is {}, the index is {}'.format(title, number, index))
        print('\n')
        
print('\n')
print('done and done')

master_list_df_reconstituted_again.to_csv('data/india_release_check_v10.csv', index=False)

page number is 3867
page number is 164
page number is 12
page number is 1834
page number is 851
page number is 3023
page number is 2895
page number is 3986
page number is 3074
no genres listed for Green Room, the number for the movie is 3074, the index is 8


page number is 217
page number is 3899
page number is 2927
page number is 837
page number is 3918
page number is 87
page number is 1786
page number is 2994
page number is 2903
page number is 1798
page number is 3104
page number is 2991
page number is 800
page number is 173
page number is 868
no genres listed for Begin Again, the number for the movie is 868, the index is 23


page number is 908
page number is 2896
page number is 5344
page number is 874
page number is 4015
no genres listed for Sleight, the number for the movie is 4015, the index is 28


page number is 5177
page number is 72
page number is 2987
page number is 1777
page number is 5503
page number is 5118
page number is 902
page number is 39
page number is 52
page numb

page number is 57
page number is 3964
page number is 2904
page number is 2951
page number is 5268
page number is 88
page number is 3969
page number is 865
page number is 81
page number is 56
page number is 918
page number is 1802
page number is 3944
page number is 11
page number is 112
page number is 864
page number is 1775
page number is 3910
page number is 871
page number is 1792
page number is 5439
page number is 20
page number is 824
page number is 2890
page number is 3976
page number is 5176
page number is 1747
page number is 110
page number is 5338
page number is 3066
page number is 185
page number is 5181
page number is 876
page number is 893
page number is 5507
page number is 1902
page number is 3977
page number is 5173
page number is 78
page number is 82
page number is 1859
page number is 1750
page number is 2968
page number is 3861
page number is 117
page number is 1806
page number is 3970
page number is 2892
page number is 905
page number is 5515
page number is 1758
page num

page number is 1837
page number is 924
page number is 5272
page number is 49
page number is 4081
page number is 2917
page number is 4065
page number is 5189
page number is 4060
page number is 3035
page number is 1850
page number is 3103
no genres listed for The Music of Strangers: Yo-Yo Ma and the Silk Road Ensemble, the number for the movie is 3103, the index is 745


page number is 1932
no genres listed for 99 Homes, the number for the movie is 1932, the index is 746


page number is 3949
page number is 194
page number is 5185
page number is 1939
page number is 208
no genres listed for 56 Up, the number for the movie is 208, the index is 751


page number is 5347
page number is 900
page number is 2973
page number is 4053
page number is 1005
page number is 174
page number is 166
no genres listed for Filly Brown, the number for the movie is 166, the index is 758


page number is 74
page number is 3967
page number is 3039
page number is 142
no genres listed for Frances Ha, the number fo

page number is 135
page number is 3134
page number is 17
page number is 3120
page number is 3072
page number is 1937
page number is 927
no genres listed for Island of Lemurs: Madagascar, the number for the movie is 927, the index is 1056


page number is 214
page number is 5429
page number is 867
page number is 921
page number is 104
page number is 850
page number is 3019
page number is 903
page number is 1736
no genres listed for Star Wars Ep. VII: The Force Awakens, the number for the movie is 1736, the index is 1065


page number is 2982
page number is 3943
page number is 4035
page number is 1835
page number is 156
no genres listed for No, the number for the movie is 156, the index is 1070


page number is 2949
page number is 4008
page number is 3923
page number is 880
page number is 4042
page number is 197
page number is 4050


done and done


In [223]:
#just filling in the genres that haven't been got
#went to the imdb website directly to deal with this

#below are the page numbers and the imdb urls
#will be using the imdb id contained within the url to get the genre information

correction_dict_again = {
'3074':"https://www.imdb.com/title/tt4062536/?ref_=nv_sr_1",
'868':"https://www.imdb.com/title/tt1980929/?ref_=nv_sr_1",
'4015':"https://www.imdb.com/title/tt4573516/?ref_=nv_sr_1",
'160':"https://www.imdb.com/title/tt1491044/?ref_=nv_sr_1",
'933':"https://www.imdb.com/title/tt2170299/?ref_=nv_sr_1",
'1812':"https://www.imdb.com/title/tt3713166/?ref_=nv_sr_2",
'119':"https://www.imdb.com/title/tt1853739/?ref_=nv_sr_1",
'5259':"https://www.imdb.com/title/tt2231461/?ref_=nv_sr_1",
'883':"https://www.imdb.com/title/tt1798709/?ref_=nv_sr_1",
'3058':"https://www.imdb.com/title/tt4501454/?ref_=nv_sr_1",
'963':"https://www.imdb.com/title/tt2692904/?ref_=nv_sr_1",
'885':"https://www.imdb.com/title/tt2388715/?ref_=nv_sr_1",
'1855':"https://www.imdb.com/title/tt3235888/?ref_=nv_sr_1",
'114':"https://www.imdb.com/title/tt1935179/?ref_=nv_sr_1",
'1832':"https://www.imdb.com/title/tt3316960/?ref_=nv_sr_1",
'916':"https://www.imdb.com/title/tt2458776/?ref_=nv_sr_7",
'835':"https://www.imdb.com/title/tt2980706/?ref_=nv_sr_1",
'3062':"https://www.imdb.com/title/tt0790770/?ref_=nv_sr_1",
'3145':"https://www.imdb.com/title/tt3139764/?ref_=nv_sr_1",
'4000':"https://www.imdb.com/title/tt4191702/?ref_=nv_sr_1",
'3137':"https://www.imdb.com/title/tt3859304/?ref_=nv_sr_3",
'1866':"https://www.imdb.com/title/tt0903657/?ref_=nv_sr_1",
'977':"https://www.imdb.com/title/tt2012665/?ref_=nv_sr_1",
'153':"https://www.imdb.com/title/tt1389096/?ref_=nv_sr_1",
'3140':"https://www.imdb.com/title/tt4632316/?ref_=nv_sr_5",
'1961':"https://www.imdb.com/title/tt3518012/?ref_=nv_sr_2",
'3103':"https://www.imdb.com/title/tt3549206/?ref_=nv_sr_1",
'1932':"https://www.imdb.com/title/tt2891174/?ref_=nv_sr_1",
'208':"https://www.imdb.com/title/tt2147134/?ref_=nv_sr_1",
'166':"https://www.imdb.com/title/tt1869425/?ref_=nv_sr_1",
'142':"https://www.imdb.com/title/tt2347569/?ref_=nv_sr_1",
'3057':"https://www.imdb.com/title/tt2401878/?ref_=nv_sr_1",
'1946':"https://www.imdb.com/title/tt4157220/?ref_=nv_sr_1",
'3136':"https://www.imdb.com/title/tt4113346/?ref_=nv_sr_4",
'1971':"https://www.imdb.com/title/tt3264102/?ref_=nv_sr_2",
'920':"https://www.imdb.com/title/tt2465140/?ref_=nv_sr_1",
'184':"https://www.imdb.com/title/tt0787442/?ref_=fn_al_tt_1",
'4031':"https://www.imdb.com/title/tt4778988/?ref_=nv_sr_1",
'1910':"https://www.imdb.com/title/tt2933544/?ref_=nv_sr_1",
'4011':"https://www.imdb.com/title/tt4420704/?ref_=nv_sr_2",
'3857':"https://www.imdb.com/title/tt2527336/?ref_=nv_sr_1",
'1841':"https://www.imdb.com/title/tt3774114/?ref_=nv_sr_1",
'980':"https://www.imdb.com/title/tt2479800/?ref_=nv_sr_1",
'1994':"https://www.imdb.com/title/tt4239548/?ref_=nv_sr_1",
'3902':"https://www.imdb.com/title/tt4425200/?ref_=nv_sr_2",
'925':"https://www.imdb.com/title/tt1967545/?ref_=nv_sr_1",
'186':"https://www.imdb.com/title/tt1595656/?ref_=nv_sr_1",
'5193':"https://www.imdb.com/title/tt6186232/?ref_=nv_sr_2",
'163':"https://www.imdb.com/title/tt2294677/?ref_=nv_sr_6",
'1985':"https://www.imdb.com/title/tt2788716/?ref_=nv_sr_1",
'1941':"https://www.imdb.com/title/tt1445208/?ref_=nv_sr_1",
'927':"https://www.imdb.com/title/tt3231010/?ref_=fn_al_tt_1",
'1736':"https://www.imdb.com/title/tt2488496/?ref_=nv_sr_1",
'156':"https://www.imdb.com/title/tt2059255/?ref_=nm_flmg_prd_11"
}

In [224]:
import re

for key, value in correction_dict_again.items():
    number = int(key)
    imdb_id = re.findall(r"https:\/\/www\.imdb\.com\/title\/tt(.*)\/\?ref.*", value)[0]
    moviex = ia.get_movie(imdb_id)
    genres_imdb_raw = moviex['genres']
    genres_imdb_check = ','.join(genres_imdb_raw)
    
    master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb_check'] = genres_imdb_check

print('done and done')

done and done


In [227]:
for index,row in master_list_df_reconstituted_again.iterrows():
    genres_imdb = row['genres_imdb']
    genres_imdb_check = row['genres_imdb_check']
    
    number = row['number']
    title = row['title']
    
    if genres_imdb != genres_imdb_check:
        print('Genres mismatch. The page number is {},title is "{}" and the index number is {}'.format(number,title,index))
        
print('done and done')

Genres mismatch. The page number is 2991,title is "The Witch" and the index number is 20
Genres mismatch. The page number is 98,title is "Homefront" and the index number is 72
Genres mismatch. The page number is 1754,title is "Home" and the index number is 79
Genres mismatch. The page number is 1787,title is "Sisters" and the index number is 81
Genres mismatch. The page number is 5434,title is "Adrift" and the index number is 87
Genres mismatch. The page number is 60,title is "Last Vegas" and the index number is 136
Genres mismatch. The page number is 1812,title is "Unfriended" and the index number is 149
Genres mismatch. The page number is 5262,title is "Truth or Dare" and the index number is 182
Genres mismatch. The page number is 3033,title is "The Darkness" and the index number is 192
Genres mismatch. The page number is 3866,title is "Coco" and the index number is 195
Genres mismatch. The page number is 3887,title is "Split" and the index number is 199
Genres mismatch. The page num

In [229]:
correction_dict_v3 = {
'2991':{'title':"The Witch", 'imdb_url':'https://www.imdb.com/title/tt4263482/?ref_=fn_al_tt_1'},
'98':{'title':"Homefront", 'imdb_url':'https://www.imdb.com/title/tt2312718/?ref_=nv_sr_1'},
'1754':{'title':"Home", 'imdb_url':'https://www.imdb.com/title/tt2224026/?ref_=fn_al_tt_2'},
'1787':{'title':"Sisters", 'imdb_url':'https://www.imdb.com/title/tt6258050/?ref_=nv_sr_2'},
'5434':{'title':"Adrift", 'imdb_url':'https://www.imdb.com/title/tt6306064/?ref_=nv_sr_1'},
'60':{'title':"Last Vegas", 'imdb_url':'https://www.imdb.com/title/tt1204975/?ref_=nv_sr_1'},
'1812':{'title':"Unfriended", 'imdb_url':'https://www.imdb.com/title/tt3713166/?ref_=nv_sr_2'},
'5262':{'title':"Truth or Dare", 'imdb_url':'https://www.imdb.com/title/tt6772950/?ref_=nv_sr_1'},
'3033':{'title':"The Darkness", 'imdb_url':'https://www.imdb.com/title/tt1878841/?ref_=nv_sr_1'},
'3866':{'title':"Coco", 'imdb_url':'https://www.imdb.com/title/tt2380307/?ref_=nv_sr_1'},
'3887':{'title':"Split", 'imdb_url':'https://www.imdb.com/title/tt4972582/?ref_=nv_sr_1'},
'8':{'title':"Gravity", 'imdb_url':'https://www.imdb.com/title/tt1454468/?ref_=nv_sr_2'},
'1836':{'title':"Ex Machina", 'imdb_url':'https://www.imdb.com/title/tt0470752/?ref_=nv_sr_1'},
'2939':{'title':"Lights Out", 'imdb_url':'https://www.imdb.com/title/tt4786282/?ref_=nv_sr_1'},
'820':{'title':"Hercules", 'imdb_url':'https://www.imdb.com/title/tt1267297/?ref_=nv_sr_1'},
'1751':{'title':"San Andreas", 'imdb_url':'https://www.imdb.com/title/tt2126355/?ref_=nv_sr_1'},
'85':{'title':"The Call", 'imdb_url':'https://www.imdb.com/title/tt1911644/?ref_=nv_sr_2'},
'3952':{'title':"Sleepless", 'imdb_url':'https://www.imdb.com/title/tt2072233/?ref_=nv_sr_2'},
'975':{'title':"Tracks", 'imdb_url':'https://www.imdb.com/title/tt2167266/?ref_=nv_sr_1'},
'202':{'title':"Generation Iron", 'imdb_url':'https://www.imdb.com/title/tt2205904/?ref_=nv_sr_2'},
'918':{'title':"Addicted", 'imdb_url':'https://www.imdb.com/title/tt2205401/?ref_=nv_sr_1'},
'3944':{'title':"The Circle", 'imdb_url':'https://www.imdb.com/title/tt4287320/?ref_=nv_sr_2'},
'3976':{'title':"Gold", 'imdb_url':'https://www.imdb.com/title/tt1800302/?ref_=nv_sr_4'},
'1747':{'title':"Cinderella", 'imdb_url':'https://www.imdb.com/title/tt1661199/?ref_=nv_sr_1'},
'1825':{'title':"Max", 'imdb_url':'https://www.imdb.com/title/tt3369806/?ref_=nv_sr_3'},
'4080':{'title':"Wilson", 'imdb_url':'https://www.imdb.com/title/tt1781058/?ref_=nv_sr_1'},
'3071':{'title':"Demolition", 'imdb_url':'https://www.imdb.com/title/tt1172049/?ref_=nv_sr_2'},
'1793':{'title':"The Visit", 'imdb_url':'https://www.imdb.com/title/tt3567288/?ref_=nv_sr_1'},
'2990':{'title':"The Forest", 'imdb_url':'https://www.imdb.com/title/tt3387542/?ref_=nv_sr_1'},
'4054':{'title':"Inhumans", 'imdb_url':'https://www.imdb.com/title/tt4154858/?ref_=nv_sr_1'},
'4070':{'title':"Landline", 'imdb_url':'https://www.imdb.com/title/tt5737862/?ref_=nv_sr_1'},
'1796':{'title':"Spotlight", 'imdb_url':'https://www.imdb.com/title/tt1895587/?ref_=nv_sr_1'},
'1926':{'title':"Cake", 'imdb_url':'https://www.imdb.com/title/tt3442006/?ref_=nv_sr_2'},
'5349':{'title':"Beast", 'imdb_url':'https://www.imdb.com/title/tt5628302/?ref_=nv_sr_3'},
'5272':{'title':"The Rider", 'imdb_url':'https://www.imdb.com/title/tt6217608/?ref_=nv_sr_2'},
'3991':{'title':"Let There Be Light", 'imdb_url':'https://www.imdb.com/title/tt5804314/?ref_=nv_sr_1'},
'3107':{'title':"Lazer Team", 'imdb_url':'https://www.imdb.com/title/tt3864024/?ref_=nv_sr_1'},
'3136':{'title':"City of Gold", 'imdb_url':'https://www.imdb.com/title/tt4113346/?ref_=nv_sr_4'},
'818':{'title':"Paddington", 'imdb_url':'https://www.imdb.com/title/tt1109624/?ref_=nv_sr_2'},
'3988':{'title':"Stronger", 'imdb_url':'https://www.imdb.com/title/tt3881784/?ref_=nv_sr_1'},
'3998':{'title':"Lowriders", 'imdb_url':'https://www.imdb.com/title/tt1366338/?ref_=nv_sr_1'},
'1944':{'title':"Black Sea", 'imdb_url':'https://www.imdb.com/title/tt2261331/?ref_=nv_sr_1'},
'1820':{'title':"The Night Before", 'imdb_url':'https://www.imdb.com/title/tt3530002/?ref_=nv_sr_1'},
'1940':{'title':"Meet the Patels", 'imdb_url':'https://www.imdb.com/title/tt2378401/?ref_=nv_sr_1'},
'3025':{'title':"Unforgettable", 'imdb_url':'https://www.imdb.com/title/tt3462710/?ref_=nv_sr_2'},
'985':{'title':"The Song", 'imdb_url':'https://www.imdb.com/title/tt2517044/?ref_=nv_sr_4'},
'4063':{'title':"Step", 'imdb_url':'https://www.imdb.com/title/tt5758404/?ref_=nv_sr_3'},
'4051':{'title':"The Comedian", 'imdb_url':'https://www.imdb.com/title/tt1967614/?ref_=nv_sr_1'},
'99':{'title':"The Family", 'imdb_url':'https://www.imdb.com/title/tt2404311/?ref_=nv_sr_2'},
'1887':{'title':"True Story", 'imdb_url':'https://www.imdb.com/title/tt2273657/?ref_=nv_sr_4'},
'189':{'title':"Disconnect", 'imdb_url':'https://www.imdb.com/title/tt1433811/?ref_=nv_sr_1'},
'5348':{'title':"The Seagull", 'imdb_url':'https://www.imdb.com/title/tt4682136/?ref_=nv_sr_1'},
'836':{'title':"Ride Along", 'imdb_url':'https://www.imdb.com/title/tt1408253/?ref_=nv_sr_2'},
'135':{'title':"Emperor", 'imdb_url':'https://www.imdb.com/title/tt2103264/?ref_=nv_sr_7'},
'903':{'title':"Big Eyes", 'imdb_url':'https://www.imdb.com/title/tt1126590/?ref_=nv_sr_1'},
'1835':{'title':"Criminal", 'imdb_url':'https://www.imdb.com/title/tt3014866/?ref_=nv_sr_4'},
'4008':{'title':"The Wall", 'imdb_url':'https://www.imdb.com/title/tt4218696/?ref_=nv_sr_1'},
'3923':{'title':"The Star", 'imdb_url':'https://www.imdb.com/title/tt4587656/?ref_=nv_sr_1'},
'880':{'title':"Wild", 'imdb_url':'https://www.imdb.com/title/tt2305051/?ref_=nv_sr_6'},
'197':{'title':"Phantom", 'imdb_url':'https://www.imdb.com/title/tt1922685/?ref_=nm_flmg_wr_2'},
'4050':{'title':"Lucky", 'imdb_url':'https://www.imdb.com/title/tt5859238/?ref_=nv_sr_3'}
}

In [230]:
import re

for key, value in correction_dict_v3.items():
    number = int(key)
    imdb_url = correction_dict_v3[key]['imdb_url']
    imdb_id = re.findall(r"https:\/\/www\.imdb\.com\/title\/tt(.*)\/\?ref.*", imdb_url)[0]
    moviex = ia.get_movie(imdb_id)
    genres_imdb_raw = moviex['genres']
    genres_imdb_check = ','.join(genres_imdb_raw)
    
    master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb_check'] = genres_imdb_check
    master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb'] = genres_imdb_check

print('done and done')

done and done


In [231]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v10.csv', index=False)

In [232]:
for index,row in master_list_df_reconstituted_again.iterrows():
    genres_imdb = row['genres_imdb']
    genres_imdb_check = row['genres_imdb_check']
    
    number = row['number']
    title = row['title']
    
    if genres_imdb != genres_imdb_check:
        print('Genres mismatch. The page number is {},title is "{}" and the index number is {}'.format(number,title,index))
        
print('done and done')

done and done


In [233]:
#deleting some foreign movies that have crept into the list
#and also movies that are actually just promotional releases in theatres for tv shows, such as inhumans

# 5127	2017	Una mujer fantástica -- spanish
# 4019	2017	Una mujer fantástica -- spanish 
# 125	2013	La Vie d'Adèle – Chapitres 1 & 2 
# 184	2013	L'attentat
# 4054	2017	Inhumans

delete_row_list_2 = [5127, 4019,125,184,4054]

master_list_df_reconstituted_again = master_list_df_reconstituted_again[~(master_list_df_reconstituted_again['number'].isin(delete_row_list_2))]

master_list_df_reconstituted_again.to_csv('data/india_release_check_v10.csv', index=False)

In [236]:
#just checking if any titles are duplicates

titles = master_list_df_reconstituted_again['title']
master_list_df_reconstituted_again[titles.isin(titles[titles.duplicated()])]

number  year                       title  domestic_box_office  \
805    5271  2017  You Were Never Really Here              2523610   
949    3990  2017  You Were Never Really Here              2523610   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
805                  0            2017-04-06       Amazon Studios           R   
949                  0            2017-04-06       Amazon Studios           R   

    franchise                             source           ...            \
805       NaN  Based on Fiction Book/Short Story           ...             
949       NaN  Based on Fiction Book/Short Story           ...             

            creative_type production_companies  \
805  Contemporary Fiction                  NaN   
949  Contemporary Fiction                  NaN   

                    production_countries released_in_india_2nd_check  \
805  France,United Kingdom,United States                         yes   
949  France,United Kingdom,United States                         yes   

    domestic_box_office_ranked production_budget_bins  \
805                      148.5                no info   
949                      148.5                no info   

     domestic_box_office_bins      director             genres_imdb  \
805                   50k-50m  Lynne Ramsay  drama,mystery,thriller   
949                   50k-50m  Lynne Ramsay  drama,mystery,thriller   

          genres_imdb_check  
805  drama,mystery,thriller  
949  drama,mystery,thriller  

[2 rows x 22 columns]

In [237]:
delete_row_list_3 = [5271]

master_list_df_reconstituted_again = master_list_df_reconstituted_again[~(master_list_df_reconstituted_again['number'].isin(delete_row_list_3))]

master_list_df_reconstituted_again.to_csv('data/india_release_check_v10.csv', index=False)

In [1]:
#START HERE

correction_dict_4 = {
'3074':"https://www.imdb.com/title/tt4062536/?ref_=nv_sr_1",
'868':"https://www.imdb.com/title/tt1980929/?ref_=nv_sr_1",
'4015':"https://www.imdb.com/title/tt4573516/?ref_=nv_sr_1",
'160':"https://www.imdb.com/title/tt1491044/?ref_=nv_sr_1",
'933':"https://www.imdb.com/title/tt2170299/?ref_=nv_sr_1",
'1812':"https://www.imdb.com/title/tt3713166/?ref_=nv_sr_2",
'119':"https://www.imdb.com/title/tt1853739/?ref_=nv_sr_1",
'5259':"https://www.imdb.com/title/tt2231461/?ref_=nv_sr_1",
'883':"https://www.imdb.com/title/tt1798709/?ref_=nv_sr_1",
'3058':"https://www.imdb.com/title/tt4501454/?ref_=nv_sr_1",
'963':"https://www.imdb.com/title/tt2692904/?ref_=nv_sr_1",
'885':"https://www.imdb.com/title/tt2388715/?ref_=nv_sr_1",
'1855':"https://www.imdb.com/title/tt3235888/?ref_=nv_sr_1",
'114':"https://www.imdb.com/title/tt1935179/?ref_=nv_sr_1",
'1832':"https://www.imdb.com/title/tt3316960/?ref_=nv_sr_1",
'916':"https://www.imdb.com/title/tt2458776/?ref_=nv_sr_7",
'835':"https://www.imdb.com/title/tt2980706/?ref_=nv_sr_1",
'3062':"https://www.imdb.com/title/tt0790770/?ref_=nv_sr_1",
'3145':"https://www.imdb.com/title/tt3139764/?ref_=nv_sr_1",
'4000':"https://www.imdb.com/title/tt4191702/?ref_=nv_sr_1",
'3137':"https://www.imdb.com/title/tt3859304/?ref_=nv_sr_3",
'1866':"https://www.imdb.com/title/tt0903657/?ref_=nv_sr_1",
'977':"https://www.imdb.com/title/tt2012665/?ref_=nv_sr_1",
'153':"https://www.imdb.com/title/tt1389096/?ref_=nv_sr_1",
'3140':"https://www.imdb.com/title/tt4632316/?ref_=nv_sr_5",
'1961':"https://www.imdb.com/title/tt3518012/?ref_=nv_sr_2",
'3103':"https://www.imdb.com/title/tt3549206/?ref_=nv_sr_1",
'1932':"https://www.imdb.com/title/tt2891174/?ref_=nv_sr_1",
'208':"https://www.imdb.com/title/tt2147134/?ref_=nv_sr_1",
'166':"https://www.imdb.com/title/tt1869425/?ref_=nv_sr_1",
'142':"https://www.imdb.com/title/tt2347569/?ref_=nv_sr_1",
'3057':"https://www.imdb.com/title/tt2401878/?ref_=nv_sr_1",
'1946':"https://www.imdb.com/title/tt4157220/?ref_=nv_sr_1",
'3136':"https://www.imdb.com/title/tt4113346/?ref_=nv_sr_4",
'1971':"https://www.imdb.com/title/tt3264102/?ref_=nv_sr_2",
'920':"https://www.imdb.com/title/tt2465140/?ref_=nv_sr_1",
'184':"https://www.imdb.com/title/tt0787442/?ref_=fn_al_tt_1",
'4031':"https://www.imdb.com/title/tt4778988/?ref_=nv_sr_1",
'1910':"https://www.imdb.com/title/tt2933544/?ref_=nv_sr_1",
'4011':"https://www.imdb.com/title/tt4420704/?ref_=nv_sr_2",
'3857':"https://www.imdb.com/title/tt2527336/?ref_=nv_sr_1",
'1841':"https://www.imdb.com/title/tt3774114/?ref_=nv_sr_1",
'980':"https://www.imdb.com/title/tt2479800/?ref_=nv_sr_1",
'1994':"https://www.imdb.com/title/tt4239548/?ref_=nv_sr_1",
'3902':"https://www.imdb.com/title/tt4425200/?ref_=nv_sr_2",
'925':"https://www.imdb.com/title/tt1967545/?ref_=nv_sr_1",
'186':"https://www.imdb.com/title/tt1595656/?ref_=nv_sr_1",
'5193':"https://www.imdb.com/title/tt6186232/?ref_=nv_sr_2",
'163':"https://www.imdb.com/title/tt2294677/?ref_=nv_sr_6",
'1985':"https://www.imdb.com/title/tt2788716/?ref_=nv_sr_1",
'1941':"https://www.imdb.com/title/tt1445208/?ref_=nv_sr_1",
'927':"https://www.imdb.com/title/tt3231010/?ref_=fn_al_tt_1",
'1736':"https://www.imdb.com/title/tt2488496/?ref_=nv_sr_1",
'156':"https://www.imdb.com/title/tt2059255/?ref_=nm_flmg_prd_11",
'2991':"https://www.imdb.com/title/tt4263482/?ref_=fn_al_tt_1",
'98':"https://www.imdb.com/title/tt2312718/?ref_=nv_sr_1",
'1754':"https://www.imdb.com/title/tt2224026/?ref_=fn_al_tt_2",
'1787':"https://www.imdb.com/title/tt6258050/?ref_=nv_sr_2",
'5434':"https://www.imdb.com/title/tt6306064/?ref_=nv_sr_1",
'60':"https://www.imdb.com/title/tt1204975/?ref_=nv_sr_1",
'1812':"https://www.imdb.com/title/tt3713166/?ref_=nv_sr_2",
'5262':"https://www.imdb.com/title/tt6772950/?ref_=nv_sr_1",
'3033':"https://www.imdb.com/title/tt1878841/?ref_=nv_sr_1",
'3866':"https://www.imdb.com/title/tt2380307/?ref_=nv_sr_1",
'3887':"https://www.imdb.com/title/tt4972582/?ref_=nv_sr_1",
'8':"https://www.imdb.com/title/tt1454468/?ref_=nv_sr_2",
'1836':"https://www.imdb.com/title/tt0470752/?ref_=nv_sr_1",
'2939':"https://www.imdb.com/title/tt4786282/?ref_=nv_sr_1",
'820':"https://www.imdb.com/title/tt1267297/?ref_=nv_sr_1",
'1751':"https://www.imdb.com/title/tt2126355/?ref_=nv_sr_1",
'85':"https://www.imdb.com/title/tt1911644/?ref_=nv_sr_2",
'3952':"https://www.imdb.com/title/tt2072233/?ref_=nv_sr_2",
'975':"https://www.imdb.com/title/tt2167266/?ref_=nv_sr_1",
'202':"https://www.imdb.com/title/tt2205904/?ref_=nv_sr_2",
'918':"https://www.imdb.com/title/tt2205401/?ref_=nv_sr_1",
'3944':"https://www.imdb.com/title/tt4287320/?ref_=nv_sr_2",
'3976':"https://www.imdb.com/title/tt1800302/?ref_=nv_sr_4",
'1747':"https://www.imdb.com/title/tt1661199/?ref_=nv_sr_1",
'1825':"https://www.imdb.com/title/tt3369806/?ref_=nv_sr_3",
'4080':"https://www.imdb.com/title/tt1781058/?ref_=nv_sr_1",
'3071':"https://www.imdb.com/title/tt1172049/?ref_=nv_sr_2",
'1793':"https://www.imdb.com/title/tt3567288/?ref_=nv_sr_1",
'2990':"https://www.imdb.com/title/tt3387542/?ref_=nv_sr_1",
'4054':"https://www.imdb.com/title/tt4154858/?ref_=nv_sr_1",
'4070':"https://www.imdb.com/title/tt5737862/?ref_=nv_sr_1",
'1796':"https://www.imdb.com/title/tt1895587/?ref_=nv_sr_1",
'1926':"https://www.imdb.com/title/tt3442006/?ref_=nv_sr_2",
'5349':"https://www.imdb.com/title/tt5628302/?ref_=nv_sr_3",
'5272':"https://www.imdb.com/title/tt6217608/?ref_=nv_sr_2",
'3991':"https://www.imdb.com/title/tt5804314/?ref_=nv_sr_1",
'3107':"https://www.imdb.com/title/tt3864024/?ref_=nv_sr_1",
'3136':"https://www.imdb.com/title/tt4113346/?ref_=nv_sr_4",
'818':"https://www.imdb.com/title/tt1109624/?ref_=nv_sr_2",
'3988':"https://www.imdb.com/title/tt3881784/?ref_=nv_sr_1",
'3998':"https://www.imdb.com/title/tt1366338/?ref_=nv_sr_1",
'1944':"https://www.imdb.com/title/tt2261331/?ref_=nv_sr_1",
'1820':"https://www.imdb.com/title/tt3530002/?ref_=nv_sr_1",
'1940':"https://www.imdb.com/title/tt2378401/?ref_=nv_sr_1",
'3025':"https://www.imdb.com/title/tt3462710/?ref_=nv_sr_2",
'985':"https://www.imdb.com/title/tt2517044/?ref_=nv_sr_4",
'4063':"https://www.imdb.com/title/tt5758404/?ref_=nv_sr_3",
'4051':"https://www.imdb.com/title/tt1967614/?ref_=nv_sr_1",
'99':"https://www.imdb.com/title/tt2404311/?ref_=nv_sr_2",
'1887':"https://www.imdb.com/title/tt2273657/?ref_=nv_sr_4",
'189':"https://www.imdb.com/title/tt1433811/?ref_=nv_sr_1",
'5348':"https://www.imdb.com/title/tt4682136/?ref_=nv_sr_1",
'836':"https://www.imdb.com/title/tt1408253/?ref_=nv_sr_2",
'135':"https://www.imdb.com/title/tt2103264/?ref_=nv_sr_7",
'903':"https://www.imdb.com/title/tt1126590/?ref_=nv_sr_1",
'1835':"https://www.imdb.com/title/tt3014866/?ref_=nv_sr_4",
'4008':"https://www.imdb.com/title/tt4218696/?ref_=nv_sr_1",
'3923':"https://www.imdb.com/title/tt4587656/?ref_=nv_sr_1",
'880':"https://www.imdb.com/title/tt2305051/?ref_=nv_sr_6",
'197':"https://www.imdb.com/title/tt1922685/?ref_=nm_flmg_wr_2",
'4050':"https://www.imdb.com/title/tt5859238/?ref_=nv_sr_3"
}

In [2]:
correction_dict_4_keys = list(correction_dict_4.keys())

In [3]:
from imdb import IMDb

with open('passwords_ignore.txt') as f:
    password = f.readline()

login_string = 'postgresql://postgres:' + password + '@localhost/imdb2'

ia = IMDb('s3', login_string, adultSearch=False)

In [4]:
ib = IMDb(accessSystem='http', adultSearch=False)

In [5]:
from imdb import IMDb
import unidecode
import re
from random import randint
import time

def simplify_title(data):

    separator_list = ["/","-","–","—",")","(","\\",":","[","]","&",","]

    for separator in separator_list:
        if separator in data:
            data = data.replace(separator," ")

    data = unidecode.unidecode(data)
    data = re.sub(r'[^a-zA-Z0-9]', ' ', data)
    data = re.sub(r'\s+', ' ', data)
    data = data.strip()
    data = data.lower()

    return data

# master_list_df_reconstituted_again['id_imdb'] = None
# master_list_df_reconstituted_again['languages_imdb'] = None
# master_list_df_reconstituted_again['genres_imdb_3'] = None

for index,row in master_list_df_reconstituted_again.iterrows():
#     print('\n')
    number = row['number']
    print('\n')
    print('page number is {}'.format(number))
    number_string = str(number)
    
    title = row['title']
    
    
    try:

        if number_string in correction_dict_4_keys:

            url_imdb = correction_dict_4[number_string]
            id_imdb = re.findall(r"https:\/\/www\.imdb\.com\/title\/tt(.*)\/\?ref.*", url_imdb)[0]

            movie_http = ib.get_movie(id_imdb)
            
            delay = randint(5,9)
            time.sleep(delay)


            languages_imdb_raw = movie_http['languages']
            languages_imdb = ','.join(languages_imdb_raw)
            if 'English' not in languages_imdb_raw:
                print('movie for page number {} and title "{}" not in English'.format(number,title))
            elif 'English' != languages_imdb_raw[0]:
                print('movie for page number {} and title "{}" does not have English listed as first language'.format(number,title))

    #         master_list_df_reconstituted_again.loc[index,'languages_imdb'] = languages_imdb
    #         master_list_df_reconstituted_again.loc[index,'id_imdb'] = id_imdb
    #         movie = ia.get_movie(id_imdb)
    #         genres_imdb_raw = movie['genres']
    #         genres_imdb = ','.join(genres_imdb_raw)
    #         master_list_df_reconstituted_again.loc[index,'genres_imdb_3'] = genres_imdb

        else:

            title_simplified = simplify_title(title)
            title_simplified_words = title_simplified.split(' ')

            year = row['year']
            year = str(year)

            title_year = title + " " + year

            director = row['director']

            if str(director) != 'nan':
                director_simplified = simplify_title(director)
                director_simplified_words = director_simplified.split(' ')
            else:
                director_simplified_words = ['ZZZZZZ']

            results  = ib.search_movie(title_year)

            for result in results:

                result_ID = result.movieID
                movie = ia.get_movie(result_ID)  #using ia, the local postgres db instead

                try:
                    movie['kind']
                except:
                    pass
                else:
                    kindx = movie['kind']

                    if kindx == 'movie': #it could be tv episode too, so filtering them out

                        titlex = movie['title']
                        titlex_string_simplified = simplify_title(titlex)

                        try:
                            movie['year']
                        except:
                            yearx = '0000'
                        else:
                            yearx = movie['year']
                            yearx = str(yearx)

                        try:
                            movie['director']
                        except:
                            directors_string_simplified = 'XXXXXX'
                        else:
                            director_list = movie['director']
                            director_name_list = []

                            for director_item in director_list:
                                director_id = director_item.personID
                                director_object = ia.get_person(director_id)   #using ia instead of ib, that is local db instead of website

                                director_name = director_object['name']
                                director_name_list.append(director_name)

                            directors_string = ",".join(director_name_list)
                            directors_string_simplified = simplify_title(directors_string)

                        true_count = [(all(substring in directors_string_simplified for substring in director_simplified_words)),
                                    (all(substring in titlex_string_simplified for substring in title_simplified_words)),
                                    (yearx == year)].count(True)

                        if true_count >= 2:

                            movie_http = ib.get_movie(result_ID)

                            languages_imdb_raw = movie_http['languages']
                            if 'English' not in languages_imdb_raw:
                                print('movie for page number {} and title "{}" not in English'.format(number,title))
                            elif 'English' != languages_imdb_raw[0]:
                                print('movie for page number {} and title "{}" does not have English listed as first language'.format(number,title))
    #                         languages_imdb = ','.join(languages_imdb_raw)
    #                         master_list_df_reconstituted_again.loc[index,'languages_imdb'] = languages_imdb

    #                         master_list_df_reconstituted_again.loc[index,'id_imdb'] = result_ID

    #                         genres_imdb_raw = movie['genres']
    #                         genres_imdb = ','.join(genres_imdb_raw)
    #                         master_list_df_reconstituted_again.loc[index,'genres_imdb_3'] = genres_imdb

                            break

    #                     elif true_count == 2:

    #                         movie_http = ib.get_movie(result_ID)

    #                         languages_imdb_raw = movie_http['languages']
    #                         languages_imdb = ','.join(languages_imdb_raw)
    #                         master_list_df_reconstituted_again.loc[index,'languages_imdb'] = languages_imdb

    #                         master_list_df_reconstituted_again.loc[index,'id_imdb'] = result_ID

    #                         genres_imdb_raw = movie['genres']
    #                         genres_imdb = ','.join(genres_imdb_raw)
    #                         master_list_df_reconstituted_again.loc[index,'genres_imdb_3'] = genres_imdb

    #                         break
    except:
        print('error for movie of page number {} and title "{}"'.format(number,title))
        continue
        
#     if pd.isnull(master_list_df_reconstituted_again.loc[index,'languages_imdb']):
#         print('no languages listed for {}, the number for the movie is {}, the index is {}'.format(title, number, index))

#     if pd.isnull(master_list_df_reconstituted_again.loc[index,'id_imdb']):
#         print('no imdb id listed for {}, the number for the movie is {}, the index is {}'.format(title, number, index))

#     if pd.isnull(master_list_df_reconstituted_again.loc[index,'genres_imdb_3']):
#         print('no imdb id listed for {}, the number for the movie is {}, the index is {}'.format(title, number, index))

print('\n')
print('done and done')

# master_list_df_reconstituted_again.to_csv('data/india_release_check_v11.csv', index=False)

NameError: name 'master_list_df_reconstituted_again' is not defined

In [64]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v11.csv', index=False)

In [2]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v11.csv')

master_list_df_reconstituted_again.head()

number  year                                             title  \
0    3867  2017  Pirates of the Caribbean: Dead Men Tell No Tales   
1     164  2013                                          The East   
2      12  2013                                       World War Z   
3    1834  2015                               Ricki and the Flash   
4     851  2014                                     Transcendence   

   domestic_box_office  production_budget domestic_release_date  \
0            172558876          230000000            2017-05-26   
1              2274649            6500000            2013-05-31   
2            202359711          190000000            2013-06-21   
3             26839498           18000000            2015-08-07   
4             23022309          100000000            2014-04-18   

  domestic_distributor mpaa_rating                 franchise  \
0          Walt Disney       PG-13  Pirates of the Caribbean   
1      Fox Searchlight       PG-13                       NaN   
2   Paramount Pictures       PG-13               World War Z   
3        Sony Pictures       PG-13                       NaN   
4         Warner Bros.       PG-13                       NaN   

                              source            ...             \
0           Based on Theme Park Ride            ...              
1                Original Screenplay            ...              
2  Based on Fiction Book/Short Story            ...              
3                Original Screenplay            ...              
4                Original Screenplay            ...              

          creative_type                               production_companies  \
0               Fantasy             Walt Disney Pictures,Jerry Bruckheimer   
1  Contemporary Fiction                                   Scott Free Films   
2       Science Fiction  Skydance Productions,Hemisphere Media Capital,...   
3  Contemporary Fiction  Marc Platt Productions,Badwill Entertainment ,...   
4       Science Fiction                Straight Up Films,DMG Entertainment   

  production_countries released_in_india_2nd_check domestic_box_office_ranked  \
0        United States                         yes                       19.0   
1        United States                         yes                      157.0   
2        United States                         yes                       13.0   
3        United States                         yes                       86.0   
4        United States                         yes                      105.0   

  production_budget_bins  domestic_box_office_bins  \
0              225m-250m                 150m-200m   
1               100k-25m                   50k-50m   
2              175m-200m                 200m-250m   
3               100k-25m                   50k-50m   
4              100m-125m                   50k-50m   

                        director               genres_imdb  \
0  Joachim Ronnin,Espen Sandberg  action,adventure,fantasy   
1                 Zal Batmanglij  adventure,drama,thriller   
2                   Marc Forster   action,adventure,horror   
3                 Jonathan Demme        comedy,drama,music   
4                  Wally Pfister     drama,mystery,romance   

          genres_imdb_check  
0  action,adventure,fantasy  
1  adventure,drama,thriller  
2   action,adventure,horror  
3        comedy,drama,music  
4     drama,mystery,romance  

[5 rows x 22 columns]

In [ ]:
#do it again looking at whether english is the first language in the list, if it isn't, make it known

In [3]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries',
       'released_in_india_2nd_check', 'domestic_box_office_ranked',
       'production_budget_bins', 'domestic_box_office_bins', 'director',
       'genres_imdb', 'genres_imdb_check'],
      dtype='object')

In [4]:
master_list_df_reconstituted_again.drop(['domestic_box_office_ranked','genres_imdb'], axis=1, inplace=True)

In [5]:
master_list_df_reconstituted_again.columns

Index(['number', 'year', 'title', 'domestic_box_office', 'production_budget',
       'domestic_release_date', 'domestic_distributor', 'mpaa_rating',
       'franchise', 'source', 'genre', 'production_method', 'creative_type',
       'production_companies', 'production_countries',
       'released_in_india_2nd_check', 'production_budget_bins',
       'domestic_box_office_bins', 'director', 'genres_imdb_check'],
      dtype='object')

In [6]:
master_list_df_reconstituted_again.shape

(1059, 20)

In [7]:
master_list_df_reconstituted_again.dtypes

number                          int64
year                            int64
title                          object
domestic_box_office             int64
production_budget               int64
domestic_release_date          object
domestic_distributor           object
mpaa_rating                    object
franchise                      object
source                         object
genre                          object
production_method              object
creative_type                  object
production_companies           object
production_countries           object
released_in_india_2nd_check    object
production_budget_bins         object
domestic_box_office_bins       object
director                       object
genres_imdb_check              object
dtype: object

In [8]:
just_august_df = pd.read_csv('data/india_release_just_aug.csv')

In [9]:
just_august_df.dtypes

number                           int64
year                             int64
title                           object
domestic_box_office              int64
production_budget                int64
domestic_release_date           object
domestic_distributor            object
mpaa_rating                     object
franchise                      float64
source                          object
genre                           object
production_method               object
creative_type                   object
production_companies            object
production_countries            object
released_in_india_2nd_check     object
production_budget_bins          object
domestic_box_office_bins        object
director                        object
genres_imdb_check               object
dtype: object

In [10]:
just_august_df['franchise']

0    NaN
1    NaN
2    NaN
3    NaN
4    NaN
5    NaN
6    NaN
7    NaN
8    NaN
9    NaN
10   NaN
11   NaN
12   NaN
13   NaN
14   NaN
15   NaN
16   NaN
17   NaN
18   NaN
19   NaN
20   NaN
21   NaN
22   NaN
Name: franchise, dtype: float64

In [11]:
master_list_df_reconstituted_again = pd.concat([master_list_df_reconstituted_again, just_august_df], ignore_index=True)

In [12]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v11.csv', index=False)

In [ ]:
#ok so having english not listed first doesnt mean that the movie's primary language isnt english, case in point - operation finale from 2018 is an english movie but has french listed first
#but put that check in anyway

In [6]:
#START HERE

correction_dict_4 = {
'3074':"https://www.imdb.com/title/tt4062536/?ref_=nv_sr_1",
'868':"https://www.imdb.com/title/tt1980929/?ref_=nv_sr_1",
'4015':"https://www.imdb.com/title/tt4573516/?ref_=nv_sr_1",
'160':"https://www.imdb.com/title/tt1491044/?ref_=nv_sr_1",
'933':"https://www.imdb.com/title/tt2170299/?ref_=nv_sr_1",
'1812':"https://www.imdb.com/title/tt3713166/?ref_=nv_sr_2",
'119':"https://www.imdb.com/title/tt1853739/?ref_=nv_sr_1",
'5259':"https://www.imdb.com/title/tt2231461/?ref_=nv_sr_1",
'883':"https://www.imdb.com/title/tt1798709/?ref_=nv_sr_1",
'3058':"https://www.imdb.com/title/tt4501454/?ref_=nv_sr_1",
'963':"https://www.imdb.com/title/tt2692904/?ref_=nv_sr_1",
'885':"https://www.imdb.com/title/tt2388715/?ref_=nv_sr_1",
'1855':"https://www.imdb.com/title/tt3235888/?ref_=nv_sr_1",
'114':"https://www.imdb.com/title/tt1935179/?ref_=nv_sr_1",
'1832':"https://www.imdb.com/title/tt3316960/?ref_=nv_sr_1",
'916':"https://www.imdb.com/title/tt2458776/?ref_=nv_sr_7",
'835':"https://www.imdb.com/title/tt2980706/?ref_=nv_sr_1",
'3062':"https://www.imdb.com/title/tt0790770/?ref_=nv_sr_1",
'3145':"https://www.imdb.com/title/tt3139764/?ref_=nv_sr_1",
'4000':"https://www.imdb.com/title/tt4191702/?ref_=nv_sr_1",
'3137':"https://www.imdb.com/title/tt3859304/?ref_=nv_sr_3",
'1866':"https://www.imdb.com/title/tt0903657/?ref_=nv_sr_1",
'977':"https://www.imdb.com/title/tt2012665/?ref_=nv_sr_1",
'153':"https://www.imdb.com/title/tt1389096/?ref_=nv_sr_1",
'3140':"https://www.imdb.com/title/tt4632316/?ref_=nv_sr_5",
'1961':"https://www.imdb.com/title/tt3518012/?ref_=nv_sr_2",
'3103':"https://www.imdb.com/title/tt3549206/?ref_=nv_sr_1",
'1932':"https://www.imdb.com/title/tt2891174/?ref_=nv_sr_1",
'208':"https://www.imdb.com/title/tt2147134/?ref_=nv_sr_1",
'166':"https://www.imdb.com/title/tt1869425/?ref_=nv_sr_1",
'142':"https://www.imdb.com/title/tt2347569/?ref_=nv_sr_1",
'3057':"https://www.imdb.com/title/tt2401878/?ref_=nv_sr_1",
'1946':"https://www.imdb.com/title/tt4157220/?ref_=nv_sr_1",
'3136':"https://www.imdb.com/title/tt4113346/?ref_=nv_sr_4",
'1971':"https://www.imdb.com/title/tt3264102/?ref_=nv_sr_2",
'920':"https://www.imdb.com/title/tt2465140/?ref_=nv_sr_1",
'184':"https://www.imdb.com/title/tt0787442/?ref_=fn_al_tt_1",
'4031':"https://www.imdb.com/title/tt4778988/?ref_=nv_sr_1",
'1910':"https://www.imdb.com/title/tt2933544/?ref_=nv_sr_1",
'4011':"https://www.imdb.com/title/tt4420704/?ref_=nv_sr_2",
'3857':"https://www.imdb.com/title/tt2527336/?ref_=nv_sr_1",
'1841':"https://www.imdb.com/title/tt3774114/?ref_=nv_sr_1",
'980':"https://www.imdb.com/title/tt2479800/?ref_=nv_sr_1",
'1994':"https://www.imdb.com/title/tt4239548/?ref_=nv_sr_1",
'3902':"https://www.imdb.com/title/tt4425200/?ref_=nv_sr_2",
'925':"https://www.imdb.com/title/tt1967545/?ref_=nv_sr_1",
'186':"https://www.imdb.com/title/tt1595656/?ref_=nv_sr_1",
'5193':"https://www.imdb.com/title/tt6186232/?ref_=nv_sr_2",
'163':"https://www.imdb.com/title/tt2294677/?ref_=nv_sr_6",
'1985':"https://www.imdb.com/title/tt2788716/?ref_=nv_sr_1",
'1941':"https://www.imdb.com/title/tt1445208/?ref_=nv_sr_1",
'927':"https://www.imdb.com/title/tt3231010/?ref_=fn_al_tt_1",
'1736':"https://www.imdb.com/title/tt2488496/?ref_=nv_sr_1",
'156':"https://www.imdb.com/title/tt2059255/?ref_=nm_flmg_prd_11",
'2991':"https://www.imdb.com/title/tt4263482/?ref_=fn_al_tt_1",
'98':"https://www.imdb.com/title/tt2312718/?ref_=nv_sr_1",
'1754':"https://www.imdb.com/title/tt2224026/?ref_=fn_al_tt_2",
'1787':"https://www.imdb.com/title/tt6258050/?ref_=nv_sr_2",
'5434':"https://www.imdb.com/title/tt6306064/?ref_=nv_sr_1",
'60':"https://www.imdb.com/title/tt1204975/?ref_=nv_sr_1",
'1812':"https://www.imdb.com/title/tt3713166/?ref_=nv_sr_2",
'5262':"https://www.imdb.com/title/tt6772950/?ref_=nv_sr_1",
'3033':"https://www.imdb.com/title/tt1878841/?ref_=nv_sr_1",
'3866':"https://www.imdb.com/title/tt2380307/?ref_=nv_sr_1",
'3887':"https://www.imdb.com/title/tt4972582/?ref_=nv_sr_1",
'8':"https://www.imdb.com/title/tt1454468/?ref_=nv_sr_2",
'1836':"https://www.imdb.com/title/tt0470752/?ref_=nv_sr_1",
'2939':"https://www.imdb.com/title/tt4786282/?ref_=nv_sr_1",
'820':"https://www.imdb.com/title/tt1267297/?ref_=nv_sr_1",
'1751':"https://www.imdb.com/title/tt2126355/?ref_=nv_sr_1",
'85':"https://www.imdb.com/title/tt1911644/?ref_=nv_sr_2",
'3952':"https://www.imdb.com/title/tt2072233/?ref_=nv_sr_2",
'975':"https://www.imdb.com/title/tt2167266/?ref_=nv_sr_1",
'202':"https://www.imdb.com/title/tt2205904/?ref_=nv_sr_2",
'918':"https://www.imdb.com/title/tt2205401/?ref_=nv_sr_1",
'3944':"https://www.imdb.com/title/tt4287320/?ref_=nv_sr_2",
'3976':"https://www.imdb.com/title/tt1800302/?ref_=nv_sr_4",
'1747':"https://www.imdb.com/title/tt1661199/?ref_=nv_sr_1",
'1825':"https://www.imdb.com/title/tt3369806/?ref_=nv_sr_3",
'4080':"https://www.imdb.com/title/tt1781058/?ref_=nv_sr_1",
'3071':"https://www.imdb.com/title/tt1172049/?ref_=nv_sr_2",
'1793':"https://www.imdb.com/title/tt3567288/?ref_=nv_sr_1",
'2990':"https://www.imdb.com/title/tt3387542/?ref_=nv_sr_1",
'4054':"https://www.imdb.com/title/tt4154858/?ref_=nv_sr_1",
'4070':"https://www.imdb.com/title/tt5737862/?ref_=nv_sr_1",
'1796':"https://www.imdb.com/title/tt1895587/?ref_=nv_sr_1",
'1926':"https://www.imdb.com/title/tt3442006/?ref_=nv_sr_2",
'5349':"https://www.imdb.com/title/tt5628302/?ref_=nv_sr_3",
'5272':"https://www.imdb.com/title/tt6217608/?ref_=nv_sr_2",
'3991':"https://www.imdb.com/title/tt5804314/?ref_=nv_sr_1",
'3107':"https://www.imdb.com/title/tt3864024/?ref_=nv_sr_1",
'3136':"https://www.imdb.com/title/tt4113346/?ref_=nv_sr_4",
'818':"https://www.imdb.com/title/tt1109624/?ref_=nv_sr_2",
'3988':"https://www.imdb.com/title/tt3881784/?ref_=nv_sr_1",
'3998':"https://www.imdb.com/title/tt1366338/?ref_=nv_sr_1",
'1944':"https://www.imdb.com/title/tt2261331/?ref_=nv_sr_1",
'1820':"https://www.imdb.com/title/tt3530002/?ref_=nv_sr_1",
'1940':"https://www.imdb.com/title/tt2378401/?ref_=nv_sr_1",
'3025':"https://www.imdb.com/title/tt3462710/?ref_=nv_sr_2",
'985':"https://www.imdb.com/title/tt2517044/?ref_=nv_sr_4",
'4063':"https://www.imdb.com/title/tt5758404/?ref_=nv_sr_3",
'4051':"https://www.imdb.com/title/tt1967614/?ref_=nv_sr_1",
'99':"https://www.imdb.com/title/tt2404311/?ref_=nv_sr_2",
'1887':"https://www.imdb.com/title/tt2273657/?ref_=nv_sr_4",
'189':"https://www.imdb.com/title/tt1433811/?ref_=nv_sr_1",
'5348':"https://www.imdb.com/title/tt4682136/?ref_=nv_sr_1",
'836':"https://www.imdb.com/title/tt1408253/?ref_=nv_sr_2",
'135':"https://www.imdb.com/title/tt2103264/?ref_=nv_sr_7",
'903':"https://www.imdb.com/title/tt1126590/?ref_=nv_sr_1",
'1835':"https://www.imdb.com/title/tt3014866/?ref_=nv_sr_4",
'4008':"https://www.imdb.com/title/tt4218696/?ref_=nv_sr_1",
'3923':"https://www.imdb.com/title/tt4587656/?ref_=nv_sr_1",
'880':"https://www.imdb.com/title/tt2305051/?ref_=nv_sr_6",
'197':"https://www.imdb.com/title/tt1922685/?ref_=nm_flmg_wr_2",
'4050':"https://www.imdb.com/title/tt5859238/?ref_=nv_sr_3"
}

In [7]:
correction_dict_4_keys = list(correction_dict_4.keys())

In [8]:
#delete the movies that don't have english listed


In [9]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv("data/india_release_check_v11.csv")

In [10]:
from imdb import IMDb

with open('passwords_ignore.txt') as f:
    password = f.readline()

login_string = 'postgresql://postgres:' + password + '@localhost/imdb2'

ia = IMDb('s3', login_string, adultSearch=False)

In [11]:
ib = IMDb(accessSystem='http', adultSearch=False)

In [ ]:

master_list_df_reconstituted_again['genres_imdb_final'] = None
master_list_df_reconstituted_again['languages_imdb'] = None
master_list_df_reconstituted_again['id_imdb'] = None

for index,row in master_list_df_reconstituted_again.iterrows():

    number = row['number']
    print('\n')
    print('page number is {}'.format(number))
    number_string = str(number)

    title = row['title']

    try:
        if number_string in correction_dict_4_keys:

            url_imdb = correction_dict_4[number_string]
            # print('got here')
            id_imdb = re.findall(r"https:\/\/www\.imdb\.com\/title\/tt(.*)\/\?ref.*", url_imdb)[0]

            movie_http = ib.get_movie(id_imdb)

            delay = randint(5,9)
            time.sleep(delay)

            languages_imdb_raw = movie_http['languages']
            languages_imdb = ','.join(languages_imdb_raw)

            master_list_df_reconstituted_again.loc[index,'languages_imdb'] = languages_imdb

            master_list_df_reconstituted_again.loc[index,'id_imdb'] = id_imdb

            movie = ia.get_movie(id_imdb)
            genres_imdb_raw = movie['genres']
            genres_imdb = ','.join(genres_imdb_raw)
            master_list_df_reconstituted_again.loc[index,'genres_imdb_final'] = genres_imdb

        else:
            # print('am here now')

            year = row['year']
            year = str(year)

            director = row['director']

            if ',' in director:
                director = re.findall(r"(.*)\,.*",director)[0]
            elif str(director) == 'nan':
                director = 'ZZZZZZ'

            results  = ib.search_movie(title,results = 20)

            delay = randint(5,9)
            time.sleep(delay)

            title_director_year = []
            title_director = []
            title_year = []
            director_year = []

            result_counter = -1

            for result in results:
                result_counter += 1

                result_ID = result.movieID
                movie = ia.get_movie(result_ID)  #using ia, the local postgres db here instead of the main website

                try:
                    movie['kind']
                except:
                    pass
                else:
                    kindx = movie['kind']

                    if kindx == 'movie': #it could be tv episode too, so filtering them out

                        titlex = movie['title']

                        try:
                            movie['year']
                        except:
                            yearx = '0000'
                        else:
                            yearx = movie['year']
                            yearx = str(yearx)

                        try:
                            movie['director']
                        except:
                            directorx = 'XXXXXX'
                        else:
                            director_list = movie['director']
                            director_item = director_list[0]
                            director_id = director_item.personID
                            director_object = ia.get_person(director_id)
                            directorx = director_object['name']

                        if ((fuzz.token_sort_ratio(director,directorx) >= 85) and (fuzz.token_sort_ratio(title,titlex) >= 85) and
                        (yearx == year)):
                            title_director_year.append(result_counter)
                        elif ((fuzz.token_sort_ratio(director,directorx) >= 85) and (fuzz.token_sort_ratio(title,titlex) >= 85)):
                            title_director.append(result_counter)
                        elif ((fuzz.token_sort_ratio(title,titlex) >= 85) and (yearx == year)):
                            title_year.append(result_counter)
                        # elif ((fuzz.token_sort_ratio(director,directorx) >= 85) and (yearx == year)):
                        #     director_year.append(result_counter)

                continue

            def fillin_data(listx):

                index_number = listx[0]

                result_ID = results[index_number].movieID

                master_list_df_reconstituted_again.loc[index,'id_imdb'] = result_ID

                movie_http = ib.get_movie(result_ID)

                delay = randint(5,9)
                time.sleep(delay)

                languages_imdb_raw = movie_http['languages']
                languages_imdb = ','.join(languages_imdb_raw)
                master_list_df_reconstituted_again.loc[index,'languages_imdb'] = languages_imdb

                movie = ia.get_movie(result_ID)

                genres_imdb_raw = movie['genres']
                genres_imdb = ','.join(genres_imdb_raw)
                master_list_df_reconstituted_again.loc[index,'genres_imdb_final'] = genres_imdb


            if len(title_director_year) > 0:
                fillin_data(title_director_year)
            else:
                if len(title_director) > 0:
                    fillin_data(title_director)
                else:
                    if len(title_year) > 0:
                        fillin_data(title_year)
                    # else:
                    #     if len(director_year) > 0:
                    #         fillin_data(director_year)

    except:
        print('error for movie of page number {} and title "{}"'.format(number,title))
        continue

print('\n')
print('done and done')

master_list_df_reconstituted_again.to_csv('data/india_release_check_v12.csv', index=False)



page number is 3867
error for movie of page number 3867 and title "Pirates of the Caribbean: Dead Men Tell No Tales"


page number is 164
error for movie of page number 164 and title "The East"


page number is 12
error for movie of page number 12 and title "World War Z"


page number is 1834
error for movie of page number 1834 and title "Ricki and the Flash"


page number is 851
error for movie of page number 851 and title "Transcendence"


page number is 3023
error for movie of page number 3023 and title "The Birth of a Nation"


page number is 2895
error for movie of page number 2895 and title "Suicide Squad"


page number is 3986
error for movie of page number 3986 and title "My Cousin Rachel"


page number is 3074
got here


page number is 217
error for movie of page number 217 and title "The Reluctant Fundamentalist"


page number is 3899
error for movie of page number 3899 and title "Baywatch"


page number is 2927
error for movie of page number 2927 and title "The BFG"


page

2018-10-18 00:17:53,883 CRITICAL [imdbpy] /home/shijith/anaconda3/lib/python3.6/site-packages/imdb/_exceptions.py:34: IMDbDataAccessError exception raised; args: ({'errcode': 104, 'errmsg': 'Connection reset by peer', 'url': 'http://www.imdb.com/title/tt6306064/plotsummary', 'proxy': '', 'exception type': 'IOError', 'original exception': ConnectionResetError(104, 'Connection reset by peer')},); kwds: {}
Traceback (most recent call last):
  File "/home/shijith/anaconda3/lib/python3.6/site-packages/imdb/parser/http/__init__.py", line 231, in retrieve_unicode
    response = uopener.open(url)
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py", line 526, in open
    response = self._open(req, data)
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py", line 544, in _open
    '_open', req)
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py", line 504, in _call_chain
    result = func(*args)
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py"



page number is 3941
error for movie of page number 3941 and title "Logan Lucky"


page number is 28
error for movie of page number 28 and title "Cloudy with a Chance of Meatballs 2"


page number is 933
got here


page number is 809
error for movie of page number 809 and title "Noah"


page number is 5062
error for movie of page number 5062 and title "Insidious: The Last Key"


page number is 848
error for movie of page number 848 and title "Horrible Bosses 2"


page number is 5183
error for movie of page number 5183 and title "Isle of Dogs"


page number is 1772
error for movie of page number 1772 and title "Creed"


page number is 63
error for movie of page number 63 and title "Escape Plan"


page number is 3004
error for movie of page number 3004 and title "Whiskey Tango Foxtrot"


page number is 3924
error for movie of page number 3924 and title "The Mountain Between Us"


page number is 3022
error for movie of page number 3022 and title "The Edge of Seventeen"


page number is 3



page number is 2919
error for movie of page number 2919 and title "Sully"


page number is 1843
error for movie of page number 1843 and title "Victor Frankenstein"


page number is 3866
got here


page number is 53
error for movie of page number 53 and title "2 Guns"


page number is 892
error for movie of page number 892 and title "3 Days to Kill"


page number is 3903
error for movie of page number 3903 and title "Ghost in the Shell"


page number is 3887
got here


In [ ]:
#dont know why but the browser started hanging , just copied the whole thing into a python script and ran it on the command line


In [1]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v12.csv')

In [11]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['genres_imdb_final'].isnull()]['number']

155     1811
209     2970
388      112
504     2921
590     2932
630     4004
632      108
670      952
736     3035
789      170
830      911
835     3936
844       65
850       48
855     1759
861     2913
956      995
996     2969
999       35
1006      96
1020      97
1034    3120
1039    5429
Name: number, dtype: int64

In [3]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['id_imdb'].isnull()]

number  year                                      title  \
155     1811  2015                           The Longest Ride   
209     2970  2016  13 Hours: The Secret Soldiers of Benghazi   
388      112  2013                 Kevin Hart: Let Me Explain   
504     2921  2016                               Ghostbusters   
590     2932  2016            The Divergent Series: Allegiant   
630     4004  2017                     An Inconvenient Sequel   
632      108  2013                                21 and Over   
670      952  2014                           The Fluffy Movie   
736     3035  2016             The Beatles: Eight Days a Week   
789      170  2013                           Girl Most Likely   
830      911  2014            Legends of Oz: Dorothy's Return   
835     3936  2017     Tyler Perry's Boo 2! A Madea Halloween   
844       65  2013                 No se Aceptan Devoluciones   
850       48  2013              Jackass Presents: Bad Grandpa   
855     1759  2015            The Divergent Series: Insurgent   
861     2913  2016   The Conjuring 2: The Enfield Poltergeist   
956      995  2014                        Alone Yet Not Alone   
996     2969  2016       Tyler Perry's Boo! A Madea Halloween   
999       35  2013                              Disney Planes   
1006      96  2013                   Tyler Perry's Temptation   
1020      97  2013            Tyler Perry's A Madea Christmas   
1039    5429  2018                                  Ocean's 8   

      domestic_box_office  production_budget domestic_release_date  \
155              37446117           34000000            2015-04-10   
209              52853219           50000000            2016-01-15   
388              32244051            2500000            2013-07-03   
504             128350574          144000000            2016-07-15   
590              66184051          110000000            2016-03-18   
630               3496795            1000000            2017-07-28   
632              25682380           13000000            2013-03-01   
670               2827393                  0            2014-07-25   
736               2934445                  0            2016-09-16   
789               1378591                  0            2013-07-19   
830               8462347           70000000            2014-05-09   
835              47319572           20000000            2017-10-20   
844              44467206            5000000            2013-08-30   
850             102003019           15000000            2013-10-25   
855             130179072          110000000            2015-03-20   
861             102470008           40000000            2016-06-10   
956                795755                  0            2014-06-13   
996              73206343           20000000            2016-10-21   
999              90282580           50000000            2013-08-09   
1006             51975354                  0            2013-03-29   
1020             52543354           25000000            2013-12-13   
1039            139377762           70000000            2018-06-08   

       domestic_distributor mpaa_rating              franchise  \
155        20th Century Fox       PG-13                    NaN   
209      Paramount Pictures           R                    NaN   
388               Lionsgate           R                    NaN   
504           Sony Pictures       PG-13           Ghostbusters   
590               Lionsgate       PG-13   The Divergent Series   
630       Paramount Vantage          PG  An Inconvenient Truth   
632              Relativity           R                    NaN   
670               Open Road       PG-13                    NaN   
736        Abramorama Films   Not Rated                    NaN   
789    Roadside Attractions       PG-13                    NaN   
830   Clarius Entertainment          PG                    NaN   
835               Lionsgate       PG-13                  Madea   
844               Lionsgate       PG-13  

In [4]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['languages_imdb'].isnull()]

number  year                                      title  \
155     1811  2015                           The Longest Ride   
209     2970  2016  13 Hours: The Secret Soldiers of Benghazi   
388      112  2013                 Kevin Hart: Let Me Explain   
504     2921  2016                               Ghostbusters   
590     2932  2016            The Divergent Series: Allegiant   
630     4004  2017                     An Inconvenient Sequel   
632      108  2013                                21 and Over   
670      952  2014                           The Fluffy Movie   
736     3035  2016             The Beatles: Eight Days a Week   
789      170  2013                           Girl Most Likely   
830      911  2014            Legends of Oz: Dorothy's Return   
835     3936  2017     Tyler Perry's Boo 2! A Madea Halloween   
844       65  2013                 No se Aceptan Devoluciones   
850       48  2013              Jackass Presents: Bad Grandpa   
855     1759  2015            The Divergent Series: Insurgent   
861     2913  2016   The Conjuring 2: The Enfield Poltergeist   
956      995  2014                        Alone Yet Not Alone   
996     2969  2016       Tyler Perry's Boo! A Madea Halloween   
999       35  2013                              Disney Planes   
1006      96  2013                   Tyler Perry's Temptation   
1020      97  2013            Tyler Perry's A Madea Christmas   
1034    3120  2016                                    Believe   
1039    5429  2018                                  Ocean's 8   

      domestic_box_office  production_budget domestic_release_date  \
155              37446117           34000000            2015-04-10   
209              52853219           50000000            2016-01-15   
388              32244051            2500000            2013-07-03   
504             128350574          144000000            2016-07-15   
590              66184051          110000000            2016-03-18   
630               3496795            1000000            2017-07-28   
632              25682380           13000000            2013-03-01   
670               2827393                  0            2014-07-25   
736               2934445                  0            2016-09-16   
789               1378591                  0            2013-07-19   
830               8462347           70000000            2014-05-09   
835              47319572           20000000            2017-10-20   
844              44467206            5000000            2013-08-30   
850             102003019           15000000            2013-10-25   
855             130179072          110000000            2015-03-20   
861             102470008           40000000            2016-06-10   
956                795755                  0            2014-06-13   
996              73206343           20000000            2016-10-21   
999              90282580           50000000            2013-08-09   
1006             51975354                  0            2013-03-29   
1020             52543354           25000000            2013-12-13   
1034               890303            3500000            2016-12-02   
1039            139377762           70000000            2018-06-08   

       domestic_distributor mpaa_rating              franchise  \
155        20th Century Fox       PG-13                    NaN   
209      Paramount Pictures           R                    NaN   
388               Lionsgate           R                    NaN   
504           Sony Pictures       PG-13           Ghostbusters   
590               Lionsgate       PG-13   The Divergent Series   
630       Paramount Vantage          PG  An Inconvenient Truth   
632              Relativity           R                    NaN   
670               Open Road       PG-13                    NaN   
736        Abramorama Films   Not Rated                    NaN   
789    Roadside Attractions       PG-13                    NaN   
830   Clarius Entertainment          P

In [5]:
master_list_df_reconstituted_again.dtypes

number                           int64
year                             int64
title                           object
domestic_box_office              int64
production_budget                int64
domestic_release_date           object
domestic_distributor            object
mpaa_rating                     object
franchise                       object
source                          object
genre                           object
production_method               object
creative_type                   object
production_companies            object
production_countries            object
released_in_india_2nd_check     object
production_budget_bins          object
domestic_box_office_bins        object
director                        object
genres_imdb_check               object
genres_imdb_final               object
languages_imdb                  object
id_imdb                        float64
dtype: object

In [14]:
fill_dict = {
"1811":"https://www.imdb.com/title/tt2726560/?ref_=nv_sr_1",
"2970":"https://www.imdb.com/title/tt4172430/?ref_=nv_sr_1",
"112":"https://www.imdb.com/title/tt2609912/?ref_=nv_sr_1",
"2921":"https://www.imdb.com/title/tt1289401/?ref_=nv_sr_2",
"2932":"https://www.imdb.com/title/tt3410834/?ref_=nv_sr_2",
"4004":"https://www.imdb.com/title/tt6322922/?ref_=nv_sr_1",
"108":"https://www.imdb.com/title/tt1711425/?ref_=nv_sr_1",
"952":"https://www.imdb.com/title/tt3532608/?ref_=nv_sr_1",
"3035":"https://www.imdb.com/title/tt2531318/?ref_=nv_sr_1",
"170":"https://www.imdb.com/title/tt1698648/?ref_=nv_sr_1",
"911":"https://www.imdb.com/title/tt0884726/?ref_=nv_sr_1",
"3936":"https://www.imdb.com/title/tt6217804/?ref_=nv_sr_1",
"65":"https://www.imdb.com/title/tt2378281/?ref_=nv_sr_1",
"48":"https://www.imdb.com/title/tt3063516/?ref_=nv_sr_1",
"1759":"https://www.imdb.com/title/tt2908446/?ref_=nv_sr_1",
"2913":"https://www.imdb.com/title/tt3065204/?ref_=nv_sr_1",
"995":"https://www.imdb.com/title/tt1986769/?ref_=nv_sr_1",
"2969":"https://www.imdb.com/title/tt5325452/?ref_=nv_sr_2",
"35":"https://www.imdb.com/title/tt1691917/?ref_=nv_sr_1",
"96":"https://www.imdb.com/title/tt2070862/?ref_=ttfc_fc_tt",
"97":"https://www.imdb.com/title/tt2609758/?ref_=nv_sr_1",
"3120":"https://www.imdb.com/title/tt4700756/?ref_=nm_flmg_cin_3",
"5429":"https://www.imdb.com/title/tt5164214/?ref_=nv_sr_1"
}

In [15]:
from imdb import IMDb

with open('passwords_ignore.txt') as f:
    password = f.readline()

login_string = 'postgresql://postgres:' + password + '@localhost/imdb2'

ia = IMDb('s3', login_string, adultSearch = False)

ib = IMDb(accessSystem = 'http', adultSearch = False)

In [17]:
import re
from random import randint
import time

for key, value in fill_dict.items():
    
    print(key)
    number = int(key)
    id_imdb = re.findall(r"https:\/\/www\.imdb\.com\/title\/tt(.*)\/\?ref.*", value)[0]

    try:
        movie_http = ib.get_movie(id_imdb)

        delay = randint(5,9)
        time.sleep(delay)

        languages_imdb_raw = movie_http['languages']
        languages_imdb = ','.join(languages_imdb_raw)

        master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'languages_imdb'] = languages_imdb

        master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'id_imdb'] = id_imdb

        movie = ia.get_movie(id_imdb)
        genres_imdb_raw = movie['genres']
        genres_imdb = ','.join(genres_imdb_raw)
        master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb_final'] = genres_imdb
    
    except:
        print('error for page number {}'.format(key))
        
print('done and done')

1811
2970
112
2921
2932
4004
108
952
3035
170
911
3936
65
48
1759
2913
995
2969
35
96
97
3120
error for page number 3120
5429
done and done


In [18]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v12.csv', index=False)

In [19]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['genres_imdb_final'].isnull()]

number  year    title  domestic_box_office  production_budget  \
1034    3120  2016  Believe               890303            3500000   

     domestic_release_date domestic_distributor mpaa_rating franchise  \
1034            2016-12-02   Smith Global Media          PG       NaN   

                   source     ...                     production_companies  \
1034  Original Screenplay     ...       Power of 3,Smith Global Management   

     production_countries released_in_india_2nd_check production_budget_bins  \
1034        United States                          no               100k-25m   

     domestic_box_office_bins       director genres_imdb_check  \
1034                  50k-50m  Billy Dickson             drama   

     genres_imdb_final languages_imdb      id_imdb  
1034               NaN            NaN  4.70076e+06  

[1 rows x 23 columns]

In [20]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['id_imdb'].isnull()]

Empty DataFrame
Columns: [number, year, title, domestic_box_office, production_budget, domestic_release_date, domestic_distributor, mpaa_rating, franchise, source, genre, production_method, creative_type, production_companies, production_countries, released_in_india_2nd_check, production_budget_bins, domestic_box_office_bins, director, genres_imdb_check, genres_imdb_final, languages_imdb, id_imdb]
Index: []

[0 rows x 23 columns]

In [21]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['languages_imdb'].isnull()]

number  year    title  domestic_box_office  production_budget  \
1034    3120  2016  Believe               890303            3500000   

     domestic_release_date domestic_distributor mpaa_rating franchise  \
1034            2016-12-02   Smith Global Media          PG       NaN   

                   source     ...                     production_companies  \
1034  Original Screenplay     ...       Power of 3,Smith Global Management   

     production_countries released_in_india_2nd_check production_budget_bins  \
1034        United States                          no               100k-25m   

     domestic_box_office_bins       director genres_imdb_check  \
1034                  50k-50m  Billy Dickson             drama   

     genres_imdb_final languages_imdb      id_imdb  
1034               NaN            NaN  4.70076e+06  

[1 rows x 23 columns]

In [27]:
movie_http = ib.get_movie('4700756') 

master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == 3120,'languages_imdb'] = 'English'
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == 3120,'id_imdb'] = '4700756'
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == 3120,'genres_imdb_final'] = movie_http['genres']

print('done and done')

done and done


In [28]:
master_list_df_reconstituted_again['id_imdb'] = master_list_df_reconstituted_again['id_imdb'].astype(int)

In [29]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['genres_imdb_final'].isnull()]

Empty DataFrame
Columns: [number, year, title, domestic_box_office, production_budget, domestic_release_date, domestic_distributor, mpaa_rating, franchise, source, genre, production_method, creative_type, production_companies, production_countries, released_in_india_2nd_check, production_budget_bins, domestic_box_office_bins, director, genres_imdb_check, genres_imdb_final, languages_imdb, id_imdb]
Index: []

[0 rows x 23 columns]

In [30]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['languages_imdb'].isnull()]

Empty DataFrame
Columns: [number, year, title, domestic_box_office, production_budget, domestic_release_date, domestic_distributor, mpaa_rating, franchise, source, genre, production_method, creative_type, production_companies, production_countries, released_in_india_2nd_check, production_budget_bins, domestic_box_office_bins, director, genres_imdb_check, genres_imdb_final, languages_imdb, id_imdb]
Index: []

[0 rows x 23 columns]

In [31]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v12.csv', index=False)

In [32]:
master_list_df_reconstituted_again.loc[~(master_list_df_reconstituted_again['languages_imdb'].str.contains('English', na=False, regex=False))]

number  year                             title  domestic_box_office  \
691     3069  2016                The Eagle Huntress              3168664   
695     3133  2016       A Tale of Love and Darkness               572212   
787     3012  2016                  No Manches Frida             11528613   
839     1001  2014  A Girl Walks Home Alone at Night               544032   
920     4011  2017                              KEDi              2834262   
1051     156  2013                                No              2341226   

      production_budget domestic_release_date    domestic_distributor  \
691                   0            2016-11-02  Sony Pictures Classics   
695                   0            2016-08-19             Focus World   
787                   0            2016-09-02               Lionsgate   
839                   0            2014-11-21             Kino Lorber   
920                   0            2017-02-10   Oscilloscope Pictures   
1051                  0            2013-02-15  Sony Pictures Classics   

     mpaa_rating franchise                         source   ...     \
691            G       NaN      Based on Real Life Events   ...      
695        PG-13       NaN  Based on Factual Book/Article   ...      
787        PG-13       NaN                         Remake   ...      
839    Not Rated       NaN            Original Screenplay   ...      
920    Not Rated       NaN      Based on Real Life Events   ...      
1051           R       NaN      Based on Real Life Events   ...      

                                   production_companies  \
691   Sony Pictures Classics,19340 Productions,Artem...   
695   Movie Plus,Ram Bergman Productions,Keshet,Avi ...   
787   Pantelion Films,Lionsgate,Alcon Entertainment,...   
839   Say Ahh Productions,Black Light District,Logan...   
920                                                 NaN   
1051            Fabula,Participant Media,Funny Balloons   

                       production_countries released_in_india_2nd_check  \
691   Mongolia,United Kingdom,United States                          no   
695                    Israel,United States                          no   
787                           United States                          no   
839                           United States                          no   
920                    Turkey,United States                          no   
1051             Chile,France,United States                          no   

     production_budget_bins domestic_box_office_bins           director  \
691                 no info                  50k-50m          Otto Bell   
695                 no info                  50k-50m    Natalie Portman   
787                 no info                  50k-50m   Nacho G. Velilla   
839                 no info                  50k-50m  Ana Lily Amirpour   
920                 no info                  50k-50m        Ceyda Torun   
1051                no info                  50k-50m      Pablo Larrain   

                genres_imdb_check            genres_imdb_final languages_imdb  \
691   adventure,documentary,sport  adventure,documentary,sport         Kazakh   
695       biography,drama,history      biography,drama,history         Hebrew   
787                        comedy                       comedy        Spanish   
839                  drama,horror                 drama,horror        Persian   
920                   documentary                  documentary        Turkish   
1051                        drama                        drama        Spanish   

      id_imdb  
691   3882074  
695   1135989  
787   5259966  
839   2326554  
920   4420704  
1051  2059255  

[6 rows x 23 columns]

In [33]:
#removing the movies which aren't in English

master_list_df_reconstituted_again = master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['languages_imdb'].str.contains('English', na=False, regex=False)]

In [34]:
#went through the list of titles, deleting two titles which are confirmed Spanish-lanaguage movies-- 'Ladrones' and 'No se Aceptan Devoluciones'-- even if english is listed in the imdb languages

master_list_df_reconstituted_again = master_list_df_reconstituted_again.loc[~((master_list_df_reconstituted_again['number'] == 65) | (master_list_df_reconstituted_again['number'] == 1906))]

In [35]:
master_list_df_reconstituted_again.shape

(1074, 23)

In [36]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v13.csv', index=False)

In [37]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['genres_imdb_final'] != master_list_df_reconstituted_again['genres_imdb_check']]

number  year               title  domestic_box_office  \
315     3980  2017         The Promise              8224288   
637       19  2013      The Hangover 3            112200072   
976     4021  2017  Jeepers Creepers 3              2235162   
1034    3120  2016             Believe               890303   
1070    5582  2018              A.X.L.              6500473   

      production_budget domestic_release_date domestic_distributor  \
315            90000000            2017-04-21            Open Road   
637           103000000            2013-05-23         Warner Bros.   
976                   0                   NaN        Weinstein Co.   
1034            3500000            2016-12-02   Smith Global Media   
1070                  0            2018-08-24          Global Road   

     mpaa_rating         franchise               source   ...     \
315        PG-13               NaN  Original Screenplay   ...      
637            R          Hangover  Original Screenplay   ...      
976    Not Rated  Jeepers Creepers  Original Screenplay   ...      
1034          PG               NaN  Original Screenplay   ...      
1070          PG               NaN  Based on Short Film   ...      

                                   production_companies production_countries  \
315          Survival Pictures,Mike Medavoy Productions  Spain,United States   
637   Warner Bros.,Legendary Pictures,Green Hat Film...        United States   
976          American Zoetrope,Odyssey Media,The Cartel        United States   
1034                 Power of 3,Smith Global Management        United States   
1070  Global Road Entertainment,Lakeshore Entertainm...        United States   

     released_in_india_2nd_check production_budget_bins  \
315                          yes               75m-100m   
637                          yes              100m-125m   
976                           no                no info   
1034                          no               100k-25m   
1070                          no                no info   

     domestic_box_office_bins       director      genres_imdb_check  \
315                   50k-50m   Terry George  drama,horror,thriller   
637                 100m-150m  Todd Phillips           comedy,crime   
976                   50k-50m   Victor Salva  action,horror,mystery   
1034                  50k-50m  Billy Dickson                  drama   
1070                  50k-50m    Oliver Daly                    NaN   

            genres_imdb_final                          languages_imdb  id_imdb  
315             drama,history  English,Armenian,German,French,Turkish  4776998  
637                    comedy                                 English  1119646  
976            horror,mystery                                 English   263488  
1034                    Drama                                 English  4700756  
1070  adventure,family,sci-fi                                 English  5709188  

[5 rows x 23 columns]

In [38]:
master_list_df_reconstituted_again.drop(['genres_imdb_check'], axis = 1, inplace = True)

In [2]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == 3120,'genres_imdb_final'] = 'drama'

In [52]:
production_company_list = list(master_list_df_reconstituted_again['production_companies'].unique())
production_company_list = [x for x in production_company_list if str(x) != 'nan']
final_list = []
for production_company in production_company_list:
    list_to_add = [x.strip() for x in production_company.split(",")]
    final_list.extend(list_to_add)
    
final_list = list(set(final_list))

for production_company_A in final_list:
    for production_company_B in final_list:
        if production_company_B in production_company_A:
            if production_company_A != production_company_B:
                print('this item in list "{}" as a string contains another item "{}"'.format(production_company_A,production_company_B))    

this item in list "LLC Primeredian Entertainment" as a string contains another item "LLC"
this item in list "Park Pictures Features" as a string contains another item "Park Pictures"
this item in list "Peak Distribution Partners LLC" as a string contains another item "LLC"
this item in list "Film 44" as a string contains another item "Film 4"
this item in list "KGB Media" as a string contains another item "KG"
this item in list "Jellyfish Bloom" as a string contains another item "Bloom"
this item in list "PalmStar Media Capital" as a string contains another item "PalmStar Media"
this item in list "Sony Pictures Animation" as a string contains another item "Sony Pictures"
this item in list "Scholastic Entertainment Inc." as a string contains another item "Inc."
this item in list "Dentsu Inc." as a string contains another item "Inc."
this item in list "Riche-Ludwig" as a string contains another item "Riche"
this item in list "3DTK Inc." as a string contains another item "Inc."
this item 

In [55]:
value_replace_dict = {
"Park Pictures Features":"Park Pictures",
"PalmStar Media Capital":"PalmStar Media",
"Jerry Bruckheimer Films":"Jerry Bruckheimer",
"Rat Pack Film Produktion":"Rat Pack",
"Spring Creek Prod":"Spring Creek",
"Constantin Film International":"Constantin Film",
"Pathe Distribution":"Pathe",
"Image Nation Abu Dhabi":"Image Nation",
"Hasbro Studios":"Hasbro"
}

master_list_df_reconstituted_again['production_companies'].replace(value_replace_dict, inplace=True, regex=True)

In [56]:
production_company_list = list(master_list_df_reconstituted_again['production_companies'].unique())
production_company_list = [x for x in production_company_list if str(x) != 'nan']
final_list = []
for production_company in production_company_list:
    list_to_add = [x.strip() for x in production_company.split(",")]
    final_list.extend(list_to_add)
    
final_list = list(set(final_list))

for production_company_A in final_list:
    for production_company_B in final_list:
        if production_company_B in production_company_A:
            if production_company_A != production_company_B:
                print('this item in list "{}" as a string contains another item "{}"'.format(production_company_A,production_company_B))    

this item in list "LLC Primeredian Entertainment" as a string contains another item "LLC"
this item in list "Peak Distribution Partners LLC" as a string contains another item "LLC"
this item in list "Film 44" as a string contains another item "Film 4"
this item in list "KGB Media" as a string contains another item "KG"
this item in list "Jellyfish Bloom" as a string contains another item "Bloom"
this item in list "Sony Pictures Animation" as a string contains another item "Sony Pictures"
this item in list "Scholastic Entertainment Inc." as a string contains another item "Inc."
this item in list "Dentsu Inc." as a string contains another item "Inc."
this item in list "Riche-Ludwig" as a string contains another item "Riche"
this item in list "3DTK Inc." as a string contains another item "Inc."
this item in list "20th Century Fox Animation" as a string contains another item "20th Century Fox"
this item in list "87Eleven Inc." as a string contains another item "Inc."
this item in list "Son

In [9]:
production_company_list = list(master_list_df_reconstituted_again['production_companies'].unique())
production_company_list = [x for x in production_company_list if str(x) != 'nan']
final_list = []
for production_company in production_company_list:
    list_to_add = [x.strip() for x in production_company.split(",")]
    final_list.extend(list_to_add)
    
final_list = list(set(final_list))
final_list = [x for x in final_list if x != 'LLC']
final_list = [x for x in final_list if x != 'Inc.']

with open('data/production_company_list.txt', 'w') as f:
    for item in final_list:
        f.write("%s\n" % item)
# final_list

In [17]:
#removing releases of stand-up performances such as that of Kevin Hart

master_list_df_reconstituted_again = master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['genre'] != 'Concert/Performance']

In [45]:
#1746 - fifty shades grey, don't know why but bookmyshow list says that it was released in India. All news reports from the time say it was banned

correction_list = [1746]

In [46]:
for numberx in correction_list:
    master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == numberx, 'released_in_india_2nd_check'] = 'no'

print('done and done')

done and done


In [47]:
master_list_df_reconstituted_again.to_csv('data/india_release_check_v15.csv', index=False)

In [16]:
# import pandas as pd

# master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v14.csv')

In [61]:
master_list_df_reconstituted_again.dtypes

number                          int64
year                            int64
title                          object
domestic_box_office             int64
production_budget               int64
domestic_release_date          object
domestic_distributor           object
mpaa_rating                    object
franchise                      object
source                         object
genre                          object
production_method              object
creative_type                  object
production_companies           object
production_countries           object
released_in_india_2nd_check    object
production_budget_bins         object
domestic_box_office_bins       object
director                       object
genres_imdb_final              object
languages_imdb                 object
id_imdb                         int64
dtype: object

In [64]:
master_list_df_reconstituted_again.shape

(1069, 22)

In [67]:
master_list_df_reconstituted_again_yes_documentaries = master_list_df_reconstituted_again[(master_list_df_reconstituted_again['genre'] == 'Documentary') |
                                                                                        (master_list_df_reconstituted_again['genres_imdb_final'].str.contains('documentary', na=False, regex=False))]

In [68]:
master_list_df_reconstituted_again_yes_documentaries.shape

(64, 22)

In [69]:
master_list_df_reconstituted_again_no_documentaries = master_list_df_reconstituted_again[~((master_list_df_reconstituted_again['genre'] == 'Documentary') |
                                                                                        (master_list_df_reconstituted_again['genres_imdb_final'].str.contains('documentary', na=False, regex=False)))]

In [70]:
master_list_df_reconstituted_again_no_documentaries.shape

(1005, 22)

In [71]:
master_list_df_reconstituted_again_no_documentaries.to_csv('data/india_release_check_v16.csv', index=False)

In [72]:
master_list_df_reconstituted_again_yes_documentaries.to_csv('data/india_release_check_v16_documentaries.csv', index=False)

In [1]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v16.csv')

In [2]:
master_list_df_reconstituted_again.shape

(1005, 22)

In [5]:
category = 'genre' #this is the genre categorisation from the-numbers.com

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

category_name_list = master_list_df_reconstituted_again[category].unique()
category_name_list = [x for x in category_name_list if str(x) != 'nan']

for category_name in category_name_list:
    
    df = df.append({"category": category_name,
                    '2013':None,
                    '2014':None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) & 
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again[category] == category_name])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)
    
    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)  &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                                       (master_list_df_reconstituted_again['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
df.sort_values('total not',ascending=False)

category  2013 2014  2015  2016 2017  2018 total not total  \
1               Drama    13   17    23    13   28    26       120   328   
5              Comedy     8    8    10     8   10     5        49   161   
3   Thriller/Suspense     5    1     1     2    2     8        19   121   
6     Romantic Comedy     1    5     1     1    0     3        11    34   
4              Horror     1    2     0     0    3     0         6    65   
0           Adventure     1    1     0     2    0     1         5   123   
2              Action     1    0     1     1    0     1         4   132   
8        Black Comedy     1    0     0     1    1     1         4    18   
7             Musical     0    0     0     1    0     0         1    12   
9             Western     0    1     0     0    0  None         1     9   
10    Multiple Genres  None    0  None  None    1  None         1     2   

   2013 % 2014 % 2015 % 2016 % 2017 % 2018 % total not %  
1    28.9   27.9   36.5   20.3   46.7   74.3        36.6  
5    27.6     32   30.3   23.5     40   33.3        30.4  
3    18.5    5.9      5     10     10   47.1        15.7  
6    12.5   55.6     25     20      0     75        32.4  
4    12.5     20      0      0   21.4      0         9.2  
0     4.8    4.2      0    7.4      0    9.1         4.1  
2       4      0      5    4.5      0    4.5           3  
8      25      0      0   33.3   16.7     50        22.2  
7       0      0      0   33.3      0      0         8.3  
9       0    100      0      0      0   None        11.1  
10   None      0   None   None    100   None          50

In [6]:
category = 'creative_type'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

category_name_list = master_list_df_reconstituted_again[category].unique()
category_name_list = [x for x in category_name_list if str(x) != 'nan']

for category_name in category_name_list:
    
    df = df.append({"category": category_name,
                    '2013':None,
                    '2014':None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) & 
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again[category] == category_name])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)
    
    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)  &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                                       (master_list_df_reconstituted_again['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
df.sort_values('total not',ascending=False)

category 2013  2014  2015  2016  2017  2018 total not total  \
1     Contemporary Fiction   24    24    20    14    30    29       141   487   
3            Dramatization    1     3    10     9    10    11        44   139   
6       Historical Fiction    2     4     4     1     4     2        17    88   
0                  Fantasy    1     2     2     1     0     1         7    83   
2          Science Fiction    1     2     0     2     0     2         7   101   
5             Kids Fiction    1     0     0     1     0     0         2    72   
4               Super Hero    0     0     0     1     0     0         1    31   
7  Multiple Creative Types    1     0  None  None  None  None         1     2   
8                  Factual    0  None  None  None     1  None         1     2   

  2013 % 2014 % 2015 % 2016 % 2017 % 2018 % total not %  
1   26.7   30.4     23   18.4   34.5   42.6          29  
3    6.2   17.6   35.7     30   32.3   64.7        31.7  
6   16.7     25     25    4.2     25     50        19.3  
0    5.9    8.3   13.3      5      0     50         8.4  
2    6.2   11.8      0   10.5      0   16.7         6.9  
5    7.7      0      0    6.2      0      0         2.8  
4      0      0      0   12.5      0      0         3.2  
7    100      0   None   None   None   None          50  
8      0   None   None   None    100   None          50

In [7]:
category = 'source'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

category_name_list = master_list_df_reconstituted_again[category].unique()
category_name_list = [x for x in category_name_list if str(x) != 'nan']

for category_name in category_name_list:
    
#     print(category_name)
    
    df = df.append({"category": category_name,
                    '2013':None,
                    '2014':None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) & 
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again[category] == category_name])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)
    
    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)  &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                                       (master_list_df_reconstituted_again['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
df.sort_values('total not',ascending=False)

category  2013  2014  2015  2016  2017  2018  \
1                   Original Screenplay    20    27    23    16    27    27   
3             Based on Real Life Events     1     1     4     4     7     7   
2     Based on Fiction Book/Short Story     4     3     2     1     7     5   
8         Based on Factual Book/Article     1     3     4     3     4     1   
15                        Based on Play     3     0     2     0  None  None   
14                  Based on Short Film     0     1     1     1  None     1   
4          Based on Comic/Graphic Novel     2     0     0     2     0     0   
11              Based on Religious Text  None     0  None     0     0     2   
18                        Based on Song  None  None  None  None  None     1   
5                                Remake     0     0     0     0     0     1   
17            Based on Musical or Opera  None  None  None     1  None  None   
12                       Based on Movie     0  None     0     1     0  None   
16                  Based on Web Series  None  None  None     0  None  None   
0              Based on Theme Park Ride  None  None  None  None     0  None   
13                             Spin-Off     0     0     0     0  None     0   
10  Based on Folk Tale/Legend/Fairytale     0     0     0     0     0     0   
7                         Based on Game  None     0     0     0  None     0   
6                           Based on TV     0     0     0     0     0     0   
9                          Based on Toy     0     0     0     0     0  None   

   total not total 2013 % 2014 % 2015 % 2016 % 2017 % 2018 % total not %  
1        140   522   22.2     31   22.8   16.7   30.3   45.8        26.8  
3         24    89    5.9   12.5   28.6     19   38.9   63.6          27  
2         22   157   16.7     10      8    3.1   26.9     25          14  
8         16    62   14.3     25   26.7     30   28.6     25        25.8  
15         5    12     60      0   66.7      0   None   None        41.7  
14         4     7      0    100     50     50   None    100        57.1  
4          4    51   15.4      0      0   22.2      0      0         7.8  
11         2     7   None      0   None      0      0    100        28.6  
18         1     1   None   None   None   None   None    100         100  
5          1    26      0      0      0      0      0     25         3.8  
17         1     1   None   None   None    100   None   None         100  
12         1     4      0   None      0    100      0   None          25  
16         0     1   None   None   None      0   None   None           0  
0          0     1   None   None   None   None      0   None           0  
13         0     9      0      0      0      0   None      0           0  
10         0    13      0      0      0      0      0      0           0  
7          0    11   None      0      0      0   None      0           0  
6          0    23      0      0      0      0      0      0           0  
9          0     8      0      0      0      0      0   None           0

In [8]:
category = 'mpaa_rating'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

category_name_list = master_list_df_reconstituted_again[category].unique()

for category_name in category_name_list:
    
    df = df.append({"category": category_name,
                    '2013':None,
                    '2014':None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) & #should I change this to str.contains()
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again[category] == category_name])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)  &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                                       (master_list_df_reconstituted_again['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
df.sort_values('total not',ascending=False)

category  2013  2014 2015  2016 2017  2018 total not total 2013 % 2014 %  \
1          R    19    15   17    18   26    23       118   445   23.8   21.7   
0      PG-13    11    17   12     5    7    12        64   406   15.9   22.4   
2         PG     1     3    6     5    9     9        33   144      5   11.1   
4  Not Rated  None  None    1     1    3     1         6     6   None   None   
3          G     0     0    0  None    0  None         0     4      0      0   

  2015 % 2016 % 2017 % 2018 % total not %  
1     21   20.9   32.9     46        26.5  
0   16.9    6.4   10.6   26.1        15.8  
2     24   17.9   33.3   52.9        22.9  
4    100    100    100    100         100  
3      0   None      0   None           0

In [9]:
labels = ['50k-50m','50m-100m','100m-150m','150m-200m','200m-250m','250m-300m','300m-350m','350m-400m','400m-450m','450m-500m','500m-550m','550m-600m','600m-650m','650m-700m','700m-750m',
         '750m-800m','800m-850m','850m-900m','900m-950m']

category = 'domestic_box_office_bins'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

for category_name in labels:
    
    df = df.append({"category": category_name,
                    '2013': None,
                    '2014': None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)])
    
    if movies_in_category_name_total != 0:

        movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
        movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

        df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
        df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
        df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

        for year in range(2013,2019):

            year_string = str(year)

            year_percent_string = str(year) + ' %'

            movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)  &
                                                                                (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                                (master_list_df_reconstituted_again['year'] == year)])

            movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                                           (master_list_df_reconstituted_again['year'] == year) ])
            if movies_in_category_name != 0:
                movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
                movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)

                df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
                df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent

df

category  2013  2014  2015  2016  2017  2018 total not total 2013 %  \
0     50k-50m    29    33    34    28    43    42       209   662   28.4   
1    50m-100m     2     1     1     1     0     2         7   164    6.1   
2   100m-150m     0     1     0     0     2     1         4    69      0   
3   150m-200m     0     0     1     0     0     0         1    40      0   
4   200m-250m     0     0     0     0     0     0         0    25      0   
5   250m-300m     0     0     0     0     0  None         0    10      0   
6   300m-350m  None     0     0     0     0     0         0    10   None   
7   350m-400m     0     0     0     0     0  None         0     8      0   
8   400m-450m     0  None  None     0     0     0         0     7      0   
9   450m-500m  None  None     0     0  None  None         0     2   None   
10  500m-550m  None  None  None     0     0  None         0     2   None   
11  550m-600m  None  None  None  None  None  None      None  None   None   
12  600m-650m  None  None  None  None     0     0         0     2   None   
13  650m-700m  None  None     0  None  None     0         0     2   None   
14  700m-750m  None  None  None  None  None     0         0     1   None   
15  750m-800m  None  None  None  None  None  None      None  None   None   
16  800m-850m  None  None  None  None  None  None      None  None   None   
17  850m-900m  None  None  None  None  None  None      None  None   None   
18  900m-950m  None  None     0  None  None  None         0     1   None   

   2014 % 2015 % 2016 % 2017 % 2018 % total not %  
0    30.8   27.4   21.9   35.2   53.2        31.6  
1       3    3.8    2.9      0   12.5         4.3  
2     7.7      0      0   16.7   12.5         5.8  
3       0    8.3      0      0      0         2.5  
4       0      0      0      0      0           0  
5       0      0      0      0   None           0  
6       0      0      0      0      0           0  
7       0      0      0      0   None           0  
8    None   None      0      0      0           0  
9    None      0      0   None   None           0  
10   None   None      0      0   None           0  
11   None   None   None   None   None        None  
12   None   None   None      0      0           0  
13   None      0   None   None      0           0  
14   None   None   None   None      0           0  
15   None   None   None   None   None        None  
16   None   None   None   None   None        None  
17   None   None   None   None   None        None  
18   None      0   None   None   None           0

In [82]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                      (master_list_df_reconstituted_again['domestic_box_office_bins'] == '50m-100m')]

number  year                            title  domestic_box_office  \
657     1805  2015                         War Room             67790117   
796     5175  2018               I Can Only Imagine             83482352   
827     2952  2016     Neighbors 2: Sorority Rising             55340730   
922     5340  2018                        Overboard             50316123   
999       96  2013         Tyler Perry's Temptation             51975354   
1013      97  2013  Tyler Perry's A Madea Christmas             52543354   
1033     867  2014             Think Like a Man Too             65028687   

      production_budget domestic_release_date  domestic_distributor  \
657             3000000            2015-08-28         Sony Pictures   
796             7000000            2018-03-16  Roadside Attractions   
827            35000000            2016-05-20             Universal   
922            12000000            2018-05-04             Lionsgate   
999                   0            2013-03-29             Lionsgate   
1013           25000000            2013-12-13             Lionsgate   
1033           24000000            2014-06-20         Sony Pictures   

     mpaa_rating         franchise                         source   ...     \
657           PG               NaN            Original Screenplay   ...      
796           PG               NaN                  Based on Song   ...      
827            R         Neighbors            Original Screenplay   ...      
922        PG-13               NaN                         Remake   ...      
999        PG-13               NaN                  Based on Play   ...      
1013       PG-13             Madea                  Based on Play   ...      
1033       PG-13  Think Like a Man  Based on Factual Book/Article   ...      

             creative_type                               production_companies  \
657   Contemporary Fiction  Tri-Star Pictures,Faithstep Films,Provident Fi...   
796          Dramatization  Lionsgate,Erwin Brothers Entertainment,South W...   
827   Contemporary Fiction  Point Grey,Good Universe,Universal Pictures,Pe...   
922   Contemporary Fiction  Pantelion Films,Metro-Goldwyn-Mayer Pictures,3...   
999   Contemporary Fiction                              Lionsgate,TPS Company   
1013  Contemporary Fiction                      Lionsgate,Tyler Perry Studios   
1033  Contemporary Fiction  Screen Gems,LStar Capital,Will Packer Productions   

     production_countries released_in_india_2nd_check production_budget_bins  \
657         United States                          no               100k-25m   
796         United States                          no               100k-25m   
827         United States                          no                25m-50m   
922         United States                          no               100k-25m   
999         United States                          no                no info   
1013        United States                          no                25m-50m   
1033        United States                          no               100k-25m   

     domestic_box_office_bins                  director  \
657                  50m-100m             Alex Kendrick   
796                  50m-100m    Andrew Erwin,Jon Erwin   
827                  50m-100m          Nicholas Stoller   
922                  50m-100m             Rob Greenberg   
999                  50m-100m               Tyler Perry   
1013                 50m-100m               Tyler Perry   
1033                 50m-100m  Tim Story,Keith Merryman   

           genres_imdb_final                    languages_imdb  id_imdb  
657                    drama                           English  3832914  
796   biography,drama,family                           English  6450186  
827                   comedy                           English  4438848  
922           comedy,romance  English,Norwegian,Spanish,French  1563742  
999           drama,thriller                           English  207086

In [4]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                      (master_list_df_reconstituted_again['domestic_box_office_bins'] == '100m-150m')]

number  year                title  domestic_box_office  \
636    3906  2017           Girls Trip            115108515   
641    5119  2018   Fifty Shades Freed            100407760   
677    3880  2017  Fifty Shades Darker            114434010   
959     836  2014           Ride Along            134202565   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
636           28000000            2017-07-21            Universal           R   
641           55000000            2018-02-09            Universal           R   
677           55000000            2017-02-10            Universal           R   
959           25000000            2014-01-17            Universal       PG-13   

                franchise                             source   ...     \
636                   NaN                Original Screenplay   ...      
641  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      
677  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      
959            Ride Along                Original Screenplay   ...      

            creative_type                               production_companies  \
636  Contemporary Fiction  Will Packer Productions,Universal Pictures,Per...   
641  Contemporary Fiction  Michael De Luca,Universal Pictures,Perfect Wor...   
677  Contemporary Fiction  Universal Pictures,Perfect World Pictures,Mich...   
959  Contemporary Fiction      Cube Vision,Rainforest Films,Relativity Media   

    production_countries released_in_india_2nd_check production_budget_bins  \
636        United States                          no                25m-50m   
641        United States                          no                50m-75m   
677        United States                          no                50m-75m   
959        United States                          no                25m-50m   

    domestic_box_office_bins        director       genres_imdb_final  \
636                100m-150m  Malcolm D. Lee            comedy,drama   
641                100m-150m     James Foley  drama,romance,thriller   
677                100m-150m     James Foley           drama,romance   
959                100m-150m       Tim Story     action,comedy,crime   

        languages_imdb  id_imdb  
636            English  3564472  
641            English  4477536  
677            English  4465564  
959  English,Ukrainian  1408253  

[4 rows x 22 columns]

In [5]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                      (master_list_df_reconstituted_again['domestic_box_office_bins'] == '150m-200m')]

number  year                 title  domestic_box_office  \
466    1746  2015  Fifty Shades of Grey            166167230   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
466           40000000            2015-02-13            Universal           R   

                franchise                             source   ...     \
466  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      

            creative_type                               production_companies  \
466  Contemporary Fiction  Focus Features,Michael De Luca,Trigger Street ...   

    production_countries released_in_india_2nd_check production_budget_bins  \
466        United States                          no                25m-50m   

    domestic_box_office_bins            director       genres_imdb_final  \
466                150m-200m  Sam Taylor-Johnson  drama,romance,thriller   

    languages_imdb  id_imdb  
466        English  2322441  

[1 rows x 22 columns]

In [84]:
#of all the movies where you have production budget information, find the ones with the biggest production budgets that weren't released in India

labels = ['no info','100k-25m','25m-50m','50m-75m','75m-100m','100m-125m','125m-150m','150m-175m','175m-200m','200m-225m','225m-250m','250m-275m', '275m-300m','300m-325m','325m-350m']

category = 'production_budget_bins'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

labels_culled = [x for x in labels if x != 'no info']

for category_name in labels_culled:
    
    df = df.append({"category": category_name,
                    '2013': None,
                    '2014': None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)  &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                                       (master_list_df_reconstituted_again['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent

df            
# df.sort_values('total not',ascending=False)

#you should have a caveat that these are all the movies that earned at least $500,000 at the US box office

category  2013  2014  2015  2016  2017  2018 total not total 2013 %  \
0    100k-25m    12    17     9    14     9     7        68   311   20.3   
1     25m-50m     5     1     1     2     2     1        12   162   14.3   
2     50m-75m     0     0     0     0     1     1         2    93      0   
3    75m-100m     0     0     0     0     0     0         0    36      0   
4   100m-125m     0     0     0     0     0     0         0    35      0   
5   125m-150m     0     0     0     0     0     0         0    30      0   
6   150m-175m     0     0     0     0     0     0         0    32      0   
7   175m-200m     0     0     0     0     0  None         0    26      0   
8   200m-225m     0     0     0     0     0     0         0    13      0   
9   225m-250m     0  None  None  None     0  None         0     2      0   
10  250m-275m     0     0  None     0     0     0         0     6      0   
11  275m-300m     0  None  None  None  None  None         0     1      0   
12  300m-325m  None  None     0  None     0     0         0     5   None   
13  325m-350m  None  None     0  None  None  None         0     1   None   

   2014 % 2015 % 2016 % 2017 % 2018 % total not %  
0    26.6     17   18.9     22     35        21.9  
1       4    2.9    6.5    8.7    7.7         7.4  
2       0      0      0    8.3   12.5         2.2  
3       0      0      0      0      0           0  
4       0      0      0      0      0           0  
5       0      0      0      0      0           0  
6       0      0      0      0      0           0  
7       0      0      0      0   None           0  
8       0      0      0      0      0           0  
9    None   None   None      0   None           0  
10      0   None      0      0      0           0  
11   None   None   None   None   None           0  
12   None      0   None      0      0           0  
13   None      0   None   None   None           0

In [85]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                      (master_list_df_reconstituted_again['production_budget_bins'] == '25m-50m')]

number  year                            title  domestic_box_office  \
474     1746  2015             Fifty Shades of Grey            166167230   
649     3906  2017                       Girls Trip            115108515   
663     3996  2017                      Tulip Fever              2455635   
688     5261  2018                    I Feel Pretty             48795601   
702      133  2013                         Paranoia              7388654   
750       74  2013                      Snowpiercer              4563029   
827     2952  2016     Neighbors 2: Sorority Rising             55340730   
836     3021  2016                  The Infiltrator             15436808   
872      128  2013                    Dead Man Down             10895295   
921       99  2013                       The Family             36918811   
1013      97  2013  Tyler Perry's A Madea Christmas             52543354   
1023     836  2014                       Ride Along            134202565   

      production_budget domestic_release_date  domestic_distributor  \
474            40000000            2015-02-13             Universal   
649            28000000            2017-07-21             Universal   
663            25000000            2017-09-01         Weinstein Co.   
688            32000000            2018-04-20     STX Entertainment   
702            40000000            2013-08-16            Relativity   
750            40000000            2013-06-27            RADiUS-TWC   
827            35000000            2016-05-20             Universal   
836            47500000            2016-07-13  Broad Green Pictures   
872            30000000            2013-03-08          FilmDistrict   
921            30000000            2013-09-13            Relativity   
1013           25000000            2013-12-13             Lionsgate   
1023           25000000            2014-01-17             Universal   

     mpaa_rating             franchise                             source  \
474            R  Fifty Shades of Grey  Based on Fiction Book/Short Story   
649            R                   NaN                Original Screenplay   
663            R                   NaN  Based on Fiction Book/Short Story   
688        PG-13                   NaN                Original Screenplay   
702        PG-13                   NaN                Original Screenplay   
750            R                   NaN       Based on Comic/Graphic Novel   
827            R             Neighbors                Original Screenplay   
836            R                   NaN      Based on Factual Book/Article   
872            R                   NaN                Original Screenplay   
921            R                   NaN  Based on Fiction Book/Short Story   
1013       PG-13                 Madea                      Based on Play   
1023       PG-13            Ride Along                Original Screenplay   

       ...            creative_type  \
474    ...     Contemporary Fiction   
649    ...     Contemporary Fiction   
663    ...       Historical Fiction   
688    ...     Contemporary Fiction   
702    ...     Contemporary Fiction   
750    ...          Science Fiction   
827    ...     Contemporary Fiction   
836    ...            Dramatization   
872    ...     Contemporary Fiction   
921    ...     Contemporary Fiction   
1013   ...     Contemporary Fiction   
1023   ...     Contemporary Fiction   

                                   production_companies  \
474   Focus Features,Michael De Luca,Trigger Street ...   
649   Will Packer Productions,Universal Pictures,Per...   
663   Worldview Entertainment,Weinstein Company,Ruby...   
688   Voltage Pictures,Wonderland Sound and Vision,H...   
702                                                 NaN   
750                             Moho Films,Opus Picture   
827   Point Grey,Good Universe,Universal Pictures,Pe...   
836           Bank Leumi,Lipsync Productions,Good Films   
872   FilmDistrict,IM Global,WWE Studios,Original Fi

In [86]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                      (master_list_df_reconstituted_again['production_budget_bins'] == '50m-75m')]

number  year                title  domestic_box_office  \
654    5119  2018   Fifty Shades Freed            100407760   
698    3880  2017  Fifty Shades Darker            114434010   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
654           55000000            2018-02-09            Universal           R   
698           55000000            2017-02-10            Universal           R   

                franchise                             source   ...     \
654  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      
698  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      

            creative_type                               production_companies  \
654  Contemporary Fiction  Michael De Luca,Universal Pictures,Perfect Wor...   
698  Contemporary Fiction  Universal Pictures,Perfect World Pictures,Mich...   

    production_countries released_in_india_2nd_check production_budget_bins  \
654        United States                          no                50m-75m   
698        United States                          no                50m-75m   

    domestic_box_office_bins     director       genres_imdb_final  \
654                100m-150m  James Foley  drama,romance,thriller   
698                100m-150m  James Foley           drama,romance   

    languages_imdb  id_imdb  
654        English  4477536  
698        English  4465564  

[2 rows x 22 columns]

In [197]:
pd.set_option('display.max_rows', 500)

In [87]:
category = 'domestic_distributor'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

category_name_list = master_list_df_reconstituted_again[category].unique()
category_name_list = [x for x in category_name_list if str(x) != 'nan']

for category_name in category_name_list:
    
    df = df.append({"category": category_name,
                    '2013':None,
                    '2014':None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) & #.str.contains(category_name, na=False, regex=False) 
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again[category] == category_name])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name)  &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category] == category_name) &
                                                                                       (master_list_df_reconstituted_again['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
df.sort_values('total not',ascending=False)

category  2013  2014  2015  2016  2017  2018  \
9                    Roadside Attractions     5     3     2     3     5     5   
18                 Sony Pictures Classics     0     2     4     4     4     4   
7                               Lionsgate     3     0     1     3     3     5   
5                                     A24     2     1     1     1     3     3   
30                Pure Flix Entertainment  None     0     2     1     2     2   
8                               Universal     0     1     1     1     2     2   
11                          Weinstein Co.     2     1     1     0     3  None   
41                    Freestyle Releasing     1     1     3     1  None  None   
3                           Sony Pictures     0     3     1     0     1     1   
12                         Focus Features     0     1     2     1     0     2   
6                               IFC Films     1     0     2     1  None     1   
67                            The Orchard  None  None     1  None     2     1   
63                      Magnolia Pictures     1  None     1     1     1  None   
37                             RADiUS-TWC     1     2     0     1  None  None   
21                        Bleecker Street  None  None     0     1     1     2   
1                         Fox Searchlight     2     0     1     0     1     0   
45                     Annapurna Pictures  None  None  None  None     3     1   
28                   Samuel Goldwyn Films     1     1     1  None  None  None   
77                       LD Entertainment     1  None  None  None  None     2   
29                    Purdie Distribution     0  None     1     1     1  None   
24                             Relativity     2     1     0     0  None  None   
26                         Amazon Studios  None  None  None  None     2     1   
15                              Open Road     1     1     0     1     0  None   
2                      Paramount Pictures     0     2     1     0     0     0   
14                   Broad Green Pictures  None  None     2     1     0  None   
32                           FilmDistrict     2     0  None  None  None  None   
40                            Global Road  None  None  None  None  None     2   
58                     Atlas Distribution  None     1  None  None     1  None   
65                 Electric Entertainment  None  None  None  None     1     1   
48         Lionsgate/Roadside Attractions  None     2  None  None  None  None   
..                                    ...   ...   ...   ...   ...   ...   ...   
22                      Cinelou Releasing  None  None     1     0  None  None   
84                     Smith Global Media  None  None  None     1  None  None   
25                              CBS Films     0  None     1  None  None     0   
83                               Cinedigm     1  None  None  None  None  None   
82                           Unison Films  None     1  None  None  None  None   
81                          TriBeca Films  None     1  None  None  None  None   
34                                    MGM  None  None  None  None  None     1   
80                         One Media, LLC  None     1  None  None  None  None   
79                              Riverrain  None  None  None  None     1  None   
78            Fun Academy Motion Pictures  None  None  None  None  None     1   
39  Entertainment Studios Motion Pictures  None  None  None  None     0     1   
44                        Gunpowder & Sky  None  None  None  None     0     1   
46                       Indican Pictures  None  None  None     1  None  None   
47       Pure Flix / Samuel Goldwyn Films  None  None     1  None  None  None   
49                                   Neon  None  None  None  None     1  None   
50                                   Tugg  None  None  None     1  None  None   
74                    Five & Two Pictures  None     1  None  None  None  None   
75                          OTL Releasing  None  None  None  Non

In [88]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['domestic_distributor'] == 'Roadside Attractions')&
                                  (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                            title  domestic_box_office  \
648     1866  2015                     Love & Mercy             12551031   
664     4026  2017                     Wonderstruck              1033632   
675      153  2013                    Stand Up Guys              3310031   
721     5349  2018                            Beast               800365   
756     1951  2015                 Where Hope Grows              1156000   
778      947  2014               Words and Pictures              2171257   
785      170  2013                 Girl Most Likely              1378591   
796     5175  2018               I Can Only Imagine             83482352   
810     3988  2017                         Stronger              4211129   
830      157  2013           Much Ado About Nothing              4328850   
848     5192  2018                Finding Your Feet              1418682   
852     4075  2017                   Tommy's Honour               569306   
870     4046  2017  The Only Living Boy in New York               624332   
885      974  2014                    Gimme Shelter              1359910   
900     3050  2016                           Genius              1361045   
917     3989  2017                Beatriz at Dinner              7115854   
939     3027  2016          Hello, My Name is Doris             14444999   
953     5068  2018                  Forever My Girl             16376066   
967     3051  2016               Southside with You              6304223   
976      932  2014                     The Homesman              2429989   
1005     163  2013                    In a World...              2963271   
1024     135  2013                          Emperor              3346264   
1054    5586  2018                    Juliet, Naked              3423155   

      production_budget domestic_release_date  domestic_distributor  \
648                   0            2015-06-05  Roadside Attractions   
664                   0            2017-10-20  Roadside Attractions   
675                   0            2013-02-01  Roadside Attractions   
721                   0            2018-05-11  Roadside Attractions   
756                   0            2015-05-15  Roadside Attractions   
778                   0            2014-05-23  Roadside Attractions   
785                   0            2013-07-19  Roadside Attractions   
796             7000000            2018-03-16  Roadside Attractions   
810                   0            2017-09-22  Roadside Attractions   
830                   0            2013-06-07  Roadside Attractions   
848                   0            2018-03-30  Roadside Attractions   
852                   0            2017-04-14  Roadside Attractions   
870                   0            2017-08-11  Roadside Attractions   
885                   0            2014-01-24  Roadside Attractions   
900            17000000            2016-06-10  Roadside Attractions   
917                   0            2017-06-09  Roadside Attractions   
939                   0            2016-03-11  Roadside Attractions   
953             3500000            2018-01-19  Roadside Attractions   
967                   0            2016-08-26  Roadside Attractions   
976            16000000            2014-11-14  Roadside Attractions   
1005                  0            2013-08-09  Roadside Attractions   
1024                  0            2013-03-08  Roadside Attractions   
1054                  0            2018-08-17  Roadside Attractions   

     mpaa_rating franchise                             source   ...     \
648        PG-13       NaN          Based on Real Life Events   ...      
664           PG       NaN  Based on Fiction Book/Short Story   ...      
675            R       NaN                Original Screenplay   ...      
721            R       NaN                Original Screenplay   ...      
756        PG-13       NaN                Original Screenplay   ...      
778        PG-13       NaN      

In [89]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['domestic_distributor'] == 'Sony Pictures Classics')&
                                  (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                                              title  \
635     3062  2016                                        Miles Ahead   
638     4000  2017  Norman: The Moderate Rise and Tragic Fall of a...   
643     3137  2016                                         The Bronze   
693      958  2014                                    Love is Strange   
727     5272  2018                                          The Rider   
729     4081  2017                                       Brigsby Bear   
735     1850  2015                                     Irrational Man   
766     1879  2015                                            Grandma   
789     5443  2018                                         Boundaries   
805     1929  2015                              Infinitely Polar Bear   
884      898  2014                             Magic in the Moonlight   
904     4091  2017                                          Novitiate   
911     4051  2017                                       The Comedian   
920     1833  2015                                The Lady in the Van   
926     3049  2016                                      Maggie's Plan   
928     3096  2016                                    I Saw the Light   
1010    5348  2018                                        The Seagull   
1057    5580  2018                                           The Wife   

      domestic_box_office  production_budget domestic_release_date  \
635               2610896                  0            2016-04-01   
638               3814868                  0            2017-04-14   
643                615816            3500000            2016-03-18   
693               2262555                  0            2014-08-22   
727               2389150                  0            2018-04-13   
729                515765                  0            2017-07-28   
735               4030360                  0            2015-07-17   
766               6980524                  0            2015-08-21   
789                701828                  0            2018-06-22   
805               1430655                  0            2015-06-19   
884              10534510                  0            2014-07-25   
904                580346                  0            2017-10-27   
911               1658706                  0            2017-02-03   
920              10021175                  0            2015-01-15   
926               3351735                  0            2016-05-20   
928               1646788                  0            2016-03-25   
1010              1252960                  0            2018-05-11   
1057              7241977                  0            2018-08-17   

        domestic_distributor mpaa_rating franchise  \
635   Sony Pictures Classics           R       NaN   
638   Sony Pictures Classics           R       NaN   
643   Sony Pictures Classics           R       NaN   
693   Sony Pictures Classics           R       NaN   
727   Sony Pictures Classics           R       NaN   
729   Sony Pictures Classics       PG-13       NaN   
735   Sony Pictures Classics           R       NaN   
766   Sony Pictures Classics           R       NaN   
789   Sony Pictures Classics           R       NaN   
805   Sony Pictures Classics           R       NaN   
884   Sony Pictures Classics       PG-13       NaN   
904   Sony Pictures Classics           R       NaN   
911   Sony Pictures Classics           R       NaN   
920   Sony Pictures Classics       PG-13       NaN   
926   Sony Pictures Classics           R       NaN   
928   Sony Pictures Classics           R       NaN   
1010  Sony Pictures Classics       PG-13       NaN   
1057  Sony Pictures Classics           R       NaN   

                             source   ...            creative_type  \
635       Based on Real Life Events   ...            Dramatization   
638             Original Screenplay   ...     Contemporary Fiction   
643             Original Screenplay   ...     Cont

In [90]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['domestic_distributor'] == 'Lionsgate')&
                                  (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                                      title  \
658     3045  2016                                  Compadres   
741     1939  2015                                   Freeheld   
749      166  2013                                Filly Brown   
764     3965  2017                           The Glass Castle   
780     5179  2018                                   Acrimony   
794     5266  2018                                    Traffik   
829     3925  2017                    How to Be a Latin Lover   
831     3936  2017     Tyler Perry's Boo 2! A Madea Halloween   
839     3013  2016  Middle School: The Worst Years of My Life   
912     3036  2016                          The Perfect Match   
922     5340  2018                                  Overboard   
957     5514  2018                              Blindspotting   
999       96  2013                   Tyler Perry's Temptation   
1013      97  2013            Tyler Perry's A Madea Christmas   
1068    5585  2018                              Blindspotting   

      domestic_box_office  production_budget domestic_release_date  \
658               3127773            3000000            2016-04-22   
741                546201            7000000            2015-10-02   
749               2850357            1250000            2013-04-19   
764              17273059                  0            2017-08-11   
780              43549096           20000000            2018-03-30   
794               9186156                  0            2018-04-20   
829              32149404           10000000            2017-04-28   
831              47319572           20000000            2017-10-20   
839              20007149            8500000            2016-10-07   
912               9669521            5000000            2016-03-11   
922              50316123           12000000            2018-05-04   
957               4333394                  0            2018-08-10   
999              51975354                  0            2013-03-29   
1013             52543354           25000000            2013-12-13   
1068              4333394                  0            2018-08-10   

     domestic_distributor mpaa_rating franchise  \
658             Lionsgate           R       NaN   
741             Lionsgate       PG-13       NaN   
749             Lionsgate           R       NaN   
764             Lionsgate       PG-13       NaN   
780             Lionsgate           R       NaN   
794             Lionsgate           R       NaN   
829             Lionsgate       PG-13       NaN   
831             Lionsgate       PG-13     Madea   
839             Lionsgate          PG       NaN   
912             Lionsgate           R       NaN   
922             Lionsgate       PG-13       NaN   
957             Lionsgate           R       NaN   
999             Lionsgate       PG-13       NaN   
1013            Lionsgate       PG-13     Madea   
1068            Lionsgate           R       NaN   

                                 source   ...            creative_type  \
658                 Original Screenplay   ...     Contemporary Fiction   
741                 Based on Short Film   ...            Dramatization   
749                 Original Screenplay   ...     Contemporary Fiction   
764       Based on Factual Book/Article   ...            Dramatization   
780                 Original Screenplay   ...     Contemporary Fiction   
794                 Original Screenplay   ...     Contemporary Fiction   
829                 Original Screenplay   ...     Contemporary Fiction   
831                 Original Screenplay   ...     Contemporary Fiction   
839   Based on Fiction Book/Short Story   ...             Kids Fiction   
912                 Original Screenplay   ...     Contemporary Fiction   
922                              Remake   ...     Contemporary Fiction   
957                 Original Screenplay   ...     Contemporary Fiction   
999                       Based on Play   ...     Contemporary Fi

In [39]:
domestic_distributor_list = list(master_list_df_reconstituted_again['domestic_distributor'].unique())
domestic_distributor_list = [x for x in domestic_distributor_list if str(x) != 'nan']


final_list = []
for domestic_distributor in domestic_distributor_list:
    list_to_add = [x.strip() for x in domestic_distributor.split(",")]
    final_list.extend(list_to_add)
    
final_list = list(set(final_list))
final_list = [x for x in final_list if x != 'LLC']
final_list = [x for x in final_list if x != 'Inc.']

with open('data/domestic_distributor_list.txt', 'w') as f:
    for item in final_list:
        f.write("%s\n" % item)

#went into the domestics distributor list text file and made some changes by hand

In [40]:
distributor_dict = {
    
    "disney": ["Walt Disney"],
    
    "time_warner": ["Warner Bros."],

    "21st_century_fox": ["Fox Searchlight","20th Century Fox"],
    
    "nbc_universal": ["Focus Features","Universal","Gramercy"],
    
    "sony": ["Sony Pictures Classics","Sony Pictures"],
    
    "viacom": ["Paramount Pictures"],
    
    "lionsgate": ["Roadside Attractions","Lionsgate","Codeblack Entertainment"]
}


In [41]:
#break-up of movies not released in India by us distributor (note that in some cases, the international or indian rights might be with another distributor)
#also that the domestic distributor may not be the one associated with the parent company , split deals are apparently commonplace too

import re

category = 'domestic_distributor'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

for key, value in distributor_dict.items():

    category_name = key

    division_list = value

    master_list_df_reconstituted_again_dupli = master_list_df_reconstituted_again

    df = df.append({"category": category_name,
                    '2013': None,
                    '2014': None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)

    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True))])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):

        year_string = str(year)

        year_percent_string = str(year) + ' %'

        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True))  &
                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again_dupli['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                                       (master_list_df_reconstituted_again_dupli['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)

            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent

df.sort_values('total not',ascending=False)

#you should have a caveat that these are all the movies that earned at least $500,000 at the US box office

category 2013 2014 2015 2016 2017 2018 total not total 2013 %  \
6         lionsgate    8    6    3    6    8   10        41   118   34.8   
4              sony    0    5    5    4    5    5        24   122      0   
3     nbc_universal    0    2    3    2    2    4        13   121      0   
2  21st_century_fox    2    1    1    0    1    1         6   109    9.5   
5            viacom    0    2    1    0    0    0         3    61      0   
1       time_warner    0    1    0    1    0    0         2   111      0   
0            disney    0    0    0    0    0    0         0    57      0   

  2014 % 2015 % 2016 % 2017 % 2018 % total not %  
6   33.3   17.6   21.4   44.4   71.4        34.7  
4   22.7   23.8     16   23.8   33.3        19.7  
3    9.5     12      8   11.1   30.8        10.7  
2    4.8      5      0    4.5   14.3         5.5  
5   18.2     10      0      0      0         4.9  
1    4.3      0      5      0      0         1.8  
0      0      0      0      0      0           0

In [42]:
division_list = distributor_dict['time_warner']

master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['domestic_distributor'].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year         title  domestic_box_office  production_budget  \
827    3020  2016         Keanu             20591853           15000000   
860     953  2014  The Good Lie              2722209                  0   

    domestic_release_date domestic_distributor mpaa_rating franchise  \
827            2016-04-29         Warner Bros.           R       NaN   
860            2014-10-03         Warner Bros.       PG-13       NaN   

                  source   ...            creative_type  \
827  Original Screenplay   ...     Contemporary Fiction   
860  Original Screenplay   ...     Contemporary Fiction   

                                  production_companies production_countries  \
827  New Line Cinema,RatPac Entertainment,Dune Ente...        United States   
860  Black Label Media,Imagine Entertainment,Relian...        United States   

    released_in_india_2nd_check production_budget_bins  \
827                          no               100k-25m   
860                          no                no info   

    domestic_box_office_bins            director    genres_imdb_final  \
827                  50k-50m       Peter Atencio  action,comedy,drama   
860                  50k-50m  Philippe Falardeau      biography,drama   

    languages_imdb  id_imdb  
827        English  4139124  
860        English  2652092  

[2 rows x 22 columns]

In [43]:
division_list = distributor_dict['viacom']

master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['domestic_distributor'].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                                  title  domestic_box_office  \
828     906  2014                               Top Five             25317379   
865    1863  2015  Scouts Guide to the Zombie Apocalypse              3703046   
946     968  2014                Men, Women and Children               705908   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
828           12000000            2014-12-12   Paramount Pictures           R   
865           15000000            2015-10-30   Paramount Pictures           R   
946           16000000            2014-10-01   Paramount Pictures           R   

    franchise               source   ...            creative_type  \
828       NaN  Original Screenplay   ...     Contemporary Fiction   
865       NaN  Original Screenplay   ...                  Fantasy   
946       NaN  Original Screenplay   ...     Contemporary Fiction   

               production_companies production_countries  \
828                            IACF        United States   
865  Paramount Pictures,Broken Road        United States   
946              Right of Way Films        United States   

    released_in_india_2nd_check production_budget_bins  \
828                          no               100k-25m   
865                          no               100k-25m   
946                          no               100k-25m   

    domestic_box_office_bins            director     genres_imdb_final  \
828                  50k-50m          Chris Rock        comedy,romance   
865                  50k-50m  Christopher Landon  action,comedy,horror   
946                  50k-50m       Jason Reitman          comedy,drama   

    languages_imdb  id_imdb  
828        English  2784678  
865        English  1727776  
946        English  3179568  

[3 rows x 22 columns]

In [44]:
division_list = distributor_dict['21st_century_fox']

master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['domestic_distributor'].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year             title  domestic_box_office  production_budget  \
684    5263  2018  Super Troopers 2             30617396                  0   
698    4059  2017       Patti Cake$               800148            1000000   
740     121  2013       Enough Said             17550872            8000000   
758    1898  2015  Mistress America              2500431                  0   
861     140  2013            Stoker              1703125           12000000   
967     921  2014       The Pyramid              2756333                  0   

    domestic_release_date domestic_distributor mpaa_rating       franchise  \
684            2018-04-20     20th Century Fox           R  Super Troopers   
698            2017-08-18      Fox Searchlight           R             NaN   
740            2013-09-18      Fox Searchlight       PG-13             NaN   
758            2015-08-14      Fox Searchlight           R             NaN   
861            2013-03-01      Fox Searchlight           R             NaN   
967            2014-12-05     20th Century Fox           R             NaN   

                  source   ...            creative_type  \
684  Original Screenplay   ...     Contemporary Fiction   
698  Original Screenplay   ...     Contemporary Fiction   
740  Original Screenplay   ...     Contemporary Fiction   
758  Original Screenplay   ...     Contemporary Fiction   
861  Original Screenplay   ...     Contemporary Fiction   
967  Original Screenplay   ...                  Fantasy   

                                  production_companies  \
684  Broken Lizard Industries,Fox Searchlight Pictu...   
698  TSG Entertainment,Fox Searchlight Pictures,RT ...   
740                     Likely Story,TSG Entertainment   
758               Fox Searchlight Pictures,RT Features   
861                 Scott Free Films,Indian Paintbrush   
967       Fox International Productions,Silvatar Media   

             production_countries released_in_india_2nd_check  \
684                 United States                          no   
698                 United States                          no   
740                 United States                          no   
758                 United States                          no   
861  United Kingdom,United States                          no   
967                 United States                          no   

    production_budget_bins domestic_box_office_bins           director  \
684                no info                  50k-50m  Jay Chandrasekhar   
698               100k-25m                  50k-50m      Geremy Jasper   
740               100k-25m                  50k-50m  Nicole Holofcener   
758                no info                  50k-50m      Noah Baumbach   
861               100k-25m                  50k-50m     Park Chan-wook   
967                no info                  50k-50m  Gregory Levasseur   

           genres_imdb_final          languages_imdb  id_imdb  
684     comedy,crime,mystery                 English   859635  
698              drama,music                 English  6288250  
740     comedy,drama,romance                 English  2390361  
758             comedy,drama                 English  2872462  
861           drama,thriller  English,French,Italian  1682180  
967  action,adventure,horror                 English  2799166  

[6 rows x 22 columns]

In [91]:
 production_company_dict = {
"20th Century Fox":["20th Century Fox Animation"],
"Bloom":["Jellyfish Bloom"],
"Film 4":["Film 44"],
# "Inc.":["3DTK Inc.","87Eleven Inc.","Dentsu Inc.","Scholastic Entertainment Inc."],
"KG":["KGB Media"],
# "LLC":["Corner Piece Capital LLC","Dreamline Pictures LLC","Greater Productions LLC","Hammond Entertainment LLC","LLC Primeredian Entertainment","Peak Distribution Partners LLC"],
"Riche":["Riche-Ludwig"],
"Sony Pictures":["Sony Pictures Animation","Sony Pictures Classics"]
}

In [89]:
pd.set_option('display.max_rows', 500)

In [92]:
#movies from which production company do we get to see the least in India?
import re

production_company_list = list(master_list_df_reconstituted_again['production_companies'].unique())
production_company_list = [x for x in production_company_list if str(x) != 'nan']
final_list = []
for production_company in production_company_list:
    list_to_add = [x.strip() for x in production_company.split(",")]
    final_list.extend(list_to_add)
    
final_list = list(set(final_list))
final_list = [x for x in final_list if x != 'LLC']
final_list = [x for x in final_list if x != 'Inc.']

category = 'production_companies'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

for category_name in final_list:

    if category_name in list(production_company_dict.keys()):
        avoid_list = production_company_dict[category_name]
        avoid_list = [re.escape(m) for m in avoid_list]
        master_list_df_reconstituted_again_dupli = master_list_df_reconstituted_again.loc[~(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(avoid_list)),na=False,regex=True))] #regex true here
    else:
        master_list_df_reconstituted_again_dupli = master_list_df_reconstituted_again
    
    df = df.append({"category": category_name,
                    '2013': None,
                    '2014': None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(category_name, na=False, regex=False)) &
                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(category_name, na=False, regex=False))])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(category_name, na=False, regex=False))  &
                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again_dupli['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(category_name, na=False, regex=False)) &
                                                                                       (master_list_df_reconstituted_again_dupli['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
df.sort_values('total not',ascending=False)

#you should have a caveat that these are all the movies that earned at least $500,000 at the US box office


category  2013  2014  2015  2016  2017  2018  \
1232                   Lionsgate     5     0     0     2     5     2   
421                    Pure Flix  None     1     3     1     2     2   
1108                   IM Global     3     0     0     3     1  None   
478         Roadside Attractions     1  None  None     2     2     1   
463       Perfect World Pictures  None  None  None     1     2     2   
36              Duplass Brothers  None     2     2     1  None  None   
281             LD Entertainment     1  None  None     0     0     4   
739           Universal Pictures     0  None     0     1     2     2   
440            Anonymous Content     1     0     1     0  None     2   
865                 Affirm Films  None     1     1     0     1     1   
248         Summit Entertainment     0     0     0     1     0     3   
81                  Bron Studios  None  None     1     1     1     1   
634              Bleecker Street  None  None     0     1     1     2   
642              Codeblack Films  None  None  None     1  None     3   
1107                 RT Features  None     1     1     1     1  None   
897              Provident Films  None     1     2  None     1  None   
1261               Stage 6 Films     0  None  None     2     1     1   
129   Star Thrower Entertainment  None  None  None  None     3  None   
1197         Snoot Entertainment     0  None  None     1  None     2   
900            Tri-Star Pictures     0     1     2     0     0  None   
1301      Sony Pictures Classics     0  None  None     1     1     1   
85                         Film4     0  None     1     0     1     1   
847              Pantelion Films  None  None     0     1     1     1   
888           Annapurna Pictures     0     0     0     1     2  None   
995              Michael De Luca     0     0     1  None     1     1   
870             Relativity Media     1     2  None     0  None  None   
986                          A24  None  None     0     1     0     2   
1248       Imagine Entertainment     0     1     1  None     1     0   
1226     Worldview Entertainment  None     2     0     0     1  None   
161                Park Pictures  None  None     1  None     1     1   
...                          ...   ...   ...   ...   ...   ...   ...   
561           RSVP Entertainment  None  None  None  None  None     0   
559                Decibel Films  None  None     0  None  None  None   
520                Nick Wechsler     0  None  None  None     0  None   
523          A Monster Calls AIE  None  None  None     0  None  None   
524           Electric Somewhere  None  None  None  None  None     0   
525      Spectacle Entertainment  None  None  None     0  None  None   
526                    MTV Films     0  None  None  None  None  None   
528           Tollin Productions  None  None  None  None     0  None   
530              Luke Greenfield  None     0  None  None  None  None   
531                Augusta Films  None  None  None     0  None  None   
532      The Mark Gordon Company     0  None     0     0     0  None   
533        Apelles Entertainment  None  None  None  None  None     0   
534        KatzSmith Productions  None  None  None  None     0  None   
537      Echo Lake Entertainment     0  None     0  None  None  None   
538              France 2 Cinema  None  None  None     0  None  None   
540                       Canana  None     0  None  None  None  None   
542                   Johnny Mac  None  None  None     0  None  None   
543                      Syncopy     0     0  None  None     0  None   
546                    Beaglepug  None  None     0     0  None  None   
547                Ehud Bleiberg     0  None  None  None  None  None   
549                    Le Grisbi  None     0     0  None     0  None   
550             Screen Australia  None  None  None  None  None     0   
551           Afterworks Limited  None  None     0  None  None  None   
552       Whitaker Entertainment  None  None  None     0  None  

In [93]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains('Lionsgate', na=False, regex=False))&
                                  (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                                   title  \
658     3045  2016                               Compadres   
675      153  2013                           Stand Up Guys   
712     4017  2017       Film Stars Don't Die in Liverpool   
749      166  2013                             Filly Brown   
764     3965  2017                        The Glass Castle   
780     5179  2018                                Acrimony   
796     5175  2018                      I Can Only Imagine   
810     3988  2017                                Stronger   
829     3925  2017                 How to Be a Latin Lover   
831     3936  2017  Tyler Perry's Boo 2! A Madea Halloween   
879      159  2013                      Thanks for Sharing   
912     3036  2016                       The Perfect Match   
999       96  2013                Tyler Perry's Temptation   
1013      97  2013         Tyler Perry's A Madea Christmas   

      domestic_box_office  production_budget domestic_release_date  \
658               3127773            3000000            2016-04-22   
675               3310031                  0            2013-02-01   
712               1024266                  0                   NaN   
749               2850357            1250000            2013-04-19   
764              17273059                  0            2017-08-11   
780              43549096           20000000            2018-03-30   
796              83482352            7000000            2018-03-16   
810               4211129                  0            2017-09-22   
829              32149404           10000000            2017-04-28   
831              47319572           20000000            2017-10-20   
879               1066256                  0            2013-12-13   
912               9669521            5000000            2016-03-11   
999              51975354                  0            2013-03-29   
1013             52543354           25000000            2013-12-13   

      domestic_distributor mpaa_rating franchise  \
658              Lionsgate           R       NaN   
675   Roadside Attractions           R       NaN   
712     Adler & Associates           R       NaN   
749              Lionsgate           R       NaN   
764              Lionsgate       PG-13       NaN   
780              Lionsgate           R       NaN   
796   Roadside Attractions          PG       NaN   
810   Roadside Attractions           R       NaN   
829              Lionsgate       PG-13       NaN   
831              Lionsgate       PG-13     Madea   
879          Mongrel Media           R       NaN   
912              Lionsgate           R       NaN   
999              Lionsgate       PG-13       NaN   
1013             Lionsgate       PG-13     Madea   

                             source   ...            creative_type  \
658             Original Screenplay   ...     Contemporary Fiction   
675             Original Screenplay   ...     Contemporary Fiction   
712       Based on Real Life Events   ...            Dramatization   
749             Original Screenplay   ...     Contemporary Fiction   
764   Based on Factual Book/Article   ...            Dramatization   
780             Original Screenplay   ...     Contemporary Fiction   
796                   Based on Song   ...            Dramatization   
810   Based on Factual Book/Article   ...            Dramatization   
829             Original Screenplay   ...     Contemporary Fiction   
831             Original Screenplay   ...     Contemporary Fiction   
879             Original Screenplay   ...     Contemporary Fiction   
912             Original Screenplay   ...     Contemporary Fiction   
999                   Based on Play   ...     Contemporary Fiction   
1013                  Based on Play   ...     Contemporary Fiction   

                                   production_companies  \
658   Pantelion Films,Lionsgate,Televisa Cine,Draco ...   
675   Lionsgate,Sidney Kimmel Entertainment,Lakeshor...   
712   Eon Produ

In [94]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains('Pure Flix', na=False, regex=False))&
                                  (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                                title  domestic_box_office  \
639     1955  2015                 Faith of Our Fathers              1004105   
644     3968  2017                  The Case for Christ             14678714   
650     5125  2018                               Samson              4719928   
701     1868  2015                      Do You Believe?             12985600   
732     5189  2018  God's Not Dead: A Light in Darkness              5728940   
840      928  2014                      Moms' Night Out             10429707   
846     4029  2017                  A Question of Faith              2587072   
899     3089  2016                      I'm Not Ashamed              2082980   
1006    1867  2015                             Woodlawn             14394097   

      production_budget domestic_release_date  \
639                   0            2015-07-01   
644                   0            2017-04-07   
650                   0            2018-02-16   
701             2300000            2015-03-20   
732                   0            2018-03-30   
840             5000000            2014-05-09   
846                   0            2017-09-29   
899             1500000            2016-10-21   
1006           13000000            2015-10-16   

                  domestic_distributor mpaa_rating       franchise  \
639   Pure Flix / Samuel Goldwyn Films       PG-13             NaN   
644            Pure Flix Entertainment          PG             NaN   
650            Pure Flix Entertainment       PG-13             NaN   
701            Pure Flix Entertainment       PG-13             NaN   
732            Pure Flix Entertainment          PG  God's Not Dead   
840                      Sony Pictures          PG             NaN   
846            Pure Flix Entertainment          PG             NaN   
899            Pure Flix Entertainment       PG-13             NaN   
1006           Pure Flix Entertainment          PG             NaN   

                         source   ...            creative_type  \
639         Original Screenplay   ...     Contemporary Fiction   
644   Based on Real Life Events   ...            Dramatization   
650     Based on Religious Text   ...            Dramatization   
701         Original Screenplay   ...     Contemporary Fiction   
732         Original Screenplay   ...     Contemporary Fiction   
840         Original Screenplay   ...     Contemporary Fiction   
846         Original Screenplay   ...     Contemporary Fiction   
899   Based on Real Life Events   ...            Dramatization   
1006  Based on Real Life Events   ...            Dramatization   

                                   production_companies  \
639   Downes Brothers Productions,Pure Flix,Oak Wate...   
644                      Pure Flix,Triple Horse Studios   
650                            Pure Flix,Boomtown Films   
701     Pure Flix,10 West Studios,Believe Entertainment   
732                           Pure Flix,GND Media Group   
840   Tri-Star Pictures,Affirm Films,Provident Films...   
846              Pure Flix,Silver Linings Entertainment   
899                          Pure Flix,Visible Pictures   
1006                          Pure Flix,Provident Films   

            production_countries released_in_india_2nd_check  \
639                United States                          no   
644                United States                          no   
650   South Africa,United States                          no   
701                United States                          no   
732                United States                          no   
840                United States                          no   
846                United States                          no   
899                United States                          no   
1006               United States                          no   

     production_budget_bins domestic_box_office_bins  \
639                 no info                  50k-50m   
644     

In [95]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains('IM Global', na=False, regex=False))&
                                  (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                              title  domestic_box_office  \
635    3062  2016                        Miles Ahead              2610896   
666    3016  2016              Fifty Shades of Black             11686940   
696     188  2013                 The Lords of Salem              1165881   
712    4017  2017  Film Stars Don't Die in Liverpool              1024266   
860      94  2013                    A Haunted House             40041683   
872     128  2013                      Dead Man Down             10895295   
967    3051  2016                 Southside with You              6304223   

     production_budget domestic_release_date      domestic_distributor  \
635                  0            2016-04-01    Sony Pictures Classics   
666            5000000            2016-01-29                 Open Road   
696            1500000            2013-04-19  Anchor Bay Entertainment   
712                  0                   NaN        Adler & Associates   
860            2500000            2013-01-11                 Open Road   
872           30000000            2013-03-08              FilmDistrict   
967                  0            2016-08-26      Roadside Attractions   

    mpaa_rating        franchise                     source   ...     \
635           R              NaN  Based on Real Life Events   ...      
666           R              NaN             Based on Movie   ...      
696           R              NaN        Original Screenplay   ...      
712           R              NaN  Based on Real Life Events   ...      
860           R  A Haunted House        Original Screenplay   ...      
872           R              NaN        Original Screenplay   ...      
967       PG-13              NaN        Original Screenplay   ...      

               creative_type  \
635            Dramatization   
666     Contemporary Fiction   
696                  Fantasy   
712            Dramatization   
860  Multiple Creative Types   
872     Contemporary Fiction   
967            Dramatization   

                                  production_companies  \
635  Bifrost Pictures,Sony Pictures Classics,Miles ...   
666                 IM Global,Open Road Films,Baby Way   
696                            Haunted Movie,IM Global   
712  Eon Productions,IM Global,Lionsgate,Synchronis...   
860  Open Road Films,IM Global,Endgame Entertainmen...   
872  FilmDistrict,IM Global,WWE Studios,Original Fi...   
967       IM Global,Miramax Films,Roadside Attractions   

                    production_countries released_in_india_2nd_check  \
635                        United States                          no   
666                        United States                          no   
696  Canada,United Kingdom,United States                          no   
712         United Kingdom,United States                          no   
860                        United States                          no   
872                        United States                          no   
967                        United States                          no   

    production_budget_bins domestic_box_office_bins           director  \
635                no info                  50k-50m        Don Cheadle   
666               100k-25m                  50k-50m     Michael Tiddes   
696               100k-25m                  50k-50m         Rob Zombie   
712                no info                  50k-50m      Paul McGuigan   
860               100k-25m                  50k-50m      Michel Tiddes   
872                25m-50m                  50k-50m  Niels Arden Oplev   
967                no info                  50k-50m      Richard Tanne   

           genres_imdb_final                             languages_imdb  \
635    biography,drama,music                                    English   
666                   comedy                                    English   
696          horror,thriller                                    English   
712  biography,drama,roman

In [91]:
# production_company_list = list(master_list_df_reconstituted_again['production_companies'].unique())
# production_company_list = [x for x in production_company_list if (str(x) != 'nan') ]
# final_list = []
# for production_company in production_company_list:
#     list_to_add = [x.strip() for x in production_company.split(",")]
#     final_list.extend(list_to_add)
    
# final_list = list(set(final_list))
# final_list = [x for x in final_list if x != 'LLC']
# final_list = [x for x in final_list if x != 'Inc.']

# #movies from which production company do we get to see the least in India?

# category = 'production_companies'

# df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

# for category_name in final_list:
    
#     df = df.append({"category": category_name,
#                     '2013': None,
#                     '2014': None,
#                     '2015':None,
#                     '2016':None,
#                     '2017':None,
#                     '2018':None,
#                     'total not':None,
#                     'total':None,
#                     '2013 %':None,
#                     '2014 %':None,
#                     '2015 %':None,
#                     '2016 %':None,
#                     '2017 %':None,
#                     '2018 %':None,
#                     'total not %':None
#                     }, ignore_index=True)
    
#     movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False)) &
#                                                                             (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

#     movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False))])

#     movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
#     movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

#     df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
#     df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
#     df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

#     for year in range(2013,2019):
        
#         year_string = str(year)
        
#         year_percent_string = str(year) + ' %'
        
#         movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False))  &
#                                                                             (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
#                                                                             (master_list_df_reconstituted_again['year'] == year)])

#         movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False)) &
#                                                                                        (master_list_df_reconstituted_again['year'] == year) ])
#         if movies_in_category_name != 0:
#             movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
#             movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
#             df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
#             df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
# df.sort_values('total not',ascending=False)

# #you should have a caveat that these are all the movies that earned at least $500,000 at the US box office

In [11]:
studio_dict = {
    
    "disney": ["Walt Disney Pictures","Walt Disney Animation Studios","Disney Nature","DisneyToon Studios","Disney-Pixar","Marvel Studios","Lucasfilm","Touchstone Pictures","A&E Indiefilms"],
    
    "time_warner": ["Warner Bros.","Warner Animation Group","New Line Cinema","DC Films","DC Comics","Castle Rock Entertainment","CNN Films","HBO Films","HBO Documentary Films","Flagship Entertainment"],

    "21st_century_fox": ["Fox Searchlight Pictures","Twentieth Century Fox","20th Century Fox Animation","Fox International Productions","20th Century Fox","Fox 2000 Pictures","Blue Sky Studios",
                        "Regency Enterprises","New Regency"],
    
    "nbc_universal": ["Focus Features","Universal Pictures","Gramercy Pictures","Working Title Films","Bullwinkle Studios","DreamWorks Animation","Illumination Entertainment","Focus World","Oriental DreamWorks"],
    
    "sony": ["Sony Pictures Classics","Columbia Pictures","Sony Pictures","Sony Pictures Animation","Screen Gems","Affirm Films","Stage 6 Films","Tri-Star Pictures"],
    
    "viacom": ["Paramount Vantage","Paramount Pictures","Nickelodeon Films","MTV Films","Awesomeness Films","BET Films"],
    
    "lionsgate": ["Roadside Attractions","Lionsgate","Codeblack Films","Good Universe","Pantelion Films","Summit Entertainment","Summit Premiere"]
}

#the ownership of some of these studios have changed hands over the years, sticking to how the situation is now for simplicity's sake
#dreamworks pictures is an independent production company
#also allowing for studios where the parent company has a minority stake

In [97]:
#break-up of movies not released in India by conglomerate

import re

category = 'production_companies'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

for key, value in studio_dict.items():

    category_name = key

    division_list = value

    master_list_df_reconstituted_again_dupli = master_list_df_reconstituted_again

    df = df.append({"category": category_name,
                    '2013': None,
                    '2014': None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)

    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True))])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)

    df.loc[df['category'] == category_name, "total" ] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):

        year_string = str(year)

        year_percent_string = str(year) + ' %'

        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True))  &
                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again_dupli['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli[category].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                                       (master_list_df_reconstituted_again_dupli['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)

            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent

df.sort_values('total not',ascending=False)

#you should have a caveat that these are all the movies that earned at least $500,000 at the US box office

category 2013 2014 2015 2016 2017 2018 total not total 2013 %  \
6         lionsgate    5    0    0    6    6    7        24    88   27.8   
4              sony    0    2    2    3    3    2        12    81      0   
3     nbc_universal    0    0    2    2    2    2         8    88      0   
1       time_warner    0    1    0    2    1    0         4    81      0   
2  21st_century_fox    0    1    1    0    1    1         4    72      0   
5            viacom    0    1    1    1    0    0         3    47      0   
0            disney    0    0    0    0    0    0         0    52      0   

  2014 % 2015 % 2016 % 2017 % 2018 % total not %  
6      0      0   22.2   46.2   58.3        27.3  
4   33.3     25   13.6   17.6   16.7        14.8  
3      0   15.4    7.7   10.5     20         9.1  
1     25      0    9.1    6.7      0         4.9  
2   12.5    5.9      0    5.3     20         5.6  
5     50   14.3    6.2      0      0         6.4  
0      0      0      0      0      0           0

In [98]:
division_list = studio_dict['lionsgate']

master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                                   title  \
658     3045  2016                               Compadres   
675      153  2013                           Stand Up Guys   
712     4017  2017       Film Stars Don't Die in Liverpool   
721     5349  2018                                   Beast   
749      166  2013                             Filly Brown   
764     3965  2017                        The Glass Castle   
780     5179  2018                                Acrimony   
794     5266  2018                                 Traffik   
796     5175  2018                      I Can Only Imagine   
810     3988  2017                                Stronger   
827     2952  2016            Neighbors 2: Sorority Rising   
829     3925  2017                 How to Be a Latin Lover   
831     3936  2017  Tyler Perry's Boo 2! A Madea Halloween   
879      159  2013                      Thanks for Sharing   
900     3050  2016                                  Genius   
912     3036  2016                       The Perfect Match   
917     3989  2017                       Beatriz at Dinner   
922     5340  2018                               Overboard   
939     3027  2016                 Hello, My Name is Doris   
957     5514  2018                           Blindspotting   
967     3051  2016                      Southside with You   
999       96  2013                Tyler Perry's Temptation   
1013      97  2013         Tyler Perry's A Madea Christmas   
1068    5585  2018                           Blindspotting   

      domestic_box_office  production_budget domestic_release_date  \
658               3127773            3000000            2016-04-22   
675               3310031                  0            2013-02-01   
712               1024266                  0                   NaN   
721                800365                  0            2018-05-11   
749               2850357            1250000            2013-04-19   
764              17273059                  0            2017-08-11   
780              43549096           20000000            2018-03-30   
794               9186156                  0            2018-04-20   
796              83482352            7000000            2018-03-16   
810               4211129                  0            2017-09-22   
827              55340730           35000000            2016-05-20   
829              32149404           10000000            2017-04-28   
831              47319572           20000000            2017-10-20   
879               1066256                  0            2013-12-13   
900               1361045           17000000            2016-06-10   
912               9669521            5000000            2016-03-11   
917               7115854                  0            2017-06-09   
922              50316123           12000000            2018-05-04   
939              14444999                  0            2016-03-11   
957               4333394                  0            2018-08-10   
967               6304223                  0            2016-08-26   
999              51975354                  0            2013-03-29   
1013             52543354           25000000            2013-12-13   
1068              4333394                  0            2018-08-10   

      domestic_distributor mpaa_rating  franchise  \
658              Lionsgate           R        NaN   
675   Roadside Attractions           R        NaN   
712     Adler & Associates           R        NaN   
721   Roadside Attractions           R        NaN   
749              Lionsgate           R        NaN   
764              Lionsgate       PG-13        NaN   
780              Lionsgate           R        NaN   
794              Lionsgate           R        NaN   
796   Roadside Attractions          PG        NaN   
810   Roadside Attractions           R        NaN   
827              Universal           R  Neighbors   
829              Lionsgate       PG-13        NaN   
831            

In [99]:
division_list = studio_dict['sony']

master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                                 title  domestic_box_office  \
635     3062  2016                           Miles Ahead              2610896   
643     3137  2016                            The Bronze               615816   
657     1805  2015                              War Room             67790117   
692     4002  2017                            All Saints              5802208   
699     4043  2017  Professor Marston & The Wonder Women              1585362   
740     5185  2018               Paul, Apostle of Christ             17547999   
789     5443  2018                            Boundaries               701828   
840      928  2014                       Moms' Night Out             10429707   
904     4091  2017                             Novitiate               580346   
920     1833  2015                   The Lady in the Van             10021175   
939     3027  2016               Hello, My Name is Doris             14444999   
1033     867  2014                  Think Like a Man Too             65028687   

      production_budget domestic_release_date    domestic_distributor  \
635                   0            2016-04-01  Sony Pictures Classics   
643             3500000            2016-03-18  Sony Pictures Classics   
657             3000000            2015-08-28           Sony Pictures   
692             2000000            2017-08-25           Sony Pictures   
699                   0            2017-10-13      Annapurna Pictures   
740             5000000            2018-03-23           Sony Pictures   
789                   0            2018-06-22  Sony Pictures Classics   
840             5000000            2014-05-09           Sony Pictures   
904                   0            2017-10-27  Sony Pictures Classics   
920                   0            2015-01-15  Sony Pictures Classics   
939                   0            2016-03-11    Roadside Attractions   
1033           24000000            2014-06-20           Sony Pictures   

     mpaa_rating         franchise                         source   ...     \
635            R               NaN      Based on Real Life Events   ...      
643            R               NaN            Original Screenplay   ...      
657           PG               NaN            Original Screenplay   ...      
692           PG               NaN      Based on Real Life Events   ...      
699            R               NaN      Based on Real Life Events   ...      
740        PG-13               NaN        Based on Religious Text   ...      
789            R               NaN            Original Screenplay   ...      
840           PG               NaN            Original Screenplay   ...      
904            R               NaN            Original Screenplay   ...      
920        PG-13               NaN                  Based on Play   ...      
939            R               NaN            Based on Short Film   ...      
1033       PG-13  Think Like a Man  Based on Factual Book/Article   ...      

             creative_type                               production_companies  \
635          Dramatization  Bifrost Pictures,Sony Pictures Classics,Miles ...   
643   Contemporary Fiction                     Duplass Brothers,Stage 6 Films   
657   Contemporary Fiction  Tri-Star Pictures,Faithstep Films,Provident Fi...   
692          Dramatization                       Affirm Films,Provident Films   
699          Dramatization  Annapurna Pictures,Stage 6 Films,Topple Entert...   
740          Dramatization  Affirm Films,Giving Films,Outside Da Box Films...   
789   Contemporary Fiction  Automatik,Oddfellows Entertainment,Stage 6 Fil...   
840   Contemporary Fiction  Tri-Star Pictures,Affirm Films,Provident Films...   
904     Historical Fiction              Sony Pictures Classics,Maven Pictures   
920          Dramatization                        Tri-Star Pictures,BBC Films   
939   Contemporary Fiction  Roadside Attractions,Stage 6 Films,Red Crown, ...   
1033  Contempor

In [100]:
division_list = studio_dict['nbc_universal']

master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')]

number  year                         title  domestic_box_office  \
474     1746  2015          Fifty Shades of Grey            166167230   
649     3906  2017                    Girls Trip            115108515   
654     5119  2018            Fifty Shades Freed            100407760   
698     3880  2017           Fifty Shades Darker            114434010   
827     2952  2016  Neighbors 2: Sorority Rising             55340730   
901     1910  2015                  5 Flights Up              1020921   
985     5341  2018                   Breaking In             46383120   
1002    3046  2016             The Young Messiah              6469813   

      production_budget domestic_release_date domestic_distributor  \
474            40000000            2015-02-13            Universal   
649            28000000            2017-07-21            Universal   
654            55000000            2018-02-09            Universal   
698            55000000            2017-02-10            Universal   
827            35000000            2016-05-20            Universal   
901                   0            2015-05-08       Focus Features   
985             6000000            2018-05-11            Universal   
1002           16800000            2016-03-11       Focus Features   

     mpaa_rating             franchise                             source  \
474            R  Fifty Shades of Grey  Based on Fiction Book/Short Story   
649            R                   NaN                Original Screenplay   
654            R  Fifty Shades of Grey  Based on Fiction Book/Short Story   
698            R  Fifty Shades of Grey  Based on Fiction Book/Short Story   
827            R             Neighbors                Original Screenplay   
901        PG-13                   NaN                Original Screenplay   
985        PG-13                   NaN                Original Screenplay   
1002       PG-13                   NaN       Based on Comic/Graphic Novel   

       ...            creative_type  \
474    ...     Contemporary Fiction   
649    ...     Contemporary Fiction   
654    ...     Contemporary Fiction   
698    ...     Contemporary Fiction   
827    ...     Contemporary Fiction   
901    ...     Contemporary Fiction   
985    ...     Contemporary Fiction   
1002   ...            Dramatization   

                                   production_companies production_countries  \
474   Focus Features,Michael De Luca,Trigger Street ...        United States   
649   Will Packer Productions,Universal Pictures,Per...        United States   
654   Michael De Luca,Universal Pictures,Perfect Wor...        United States   
698   Universal Pictures,Perfect World Pictures,Mich...        United States   
827   Point Grey,Good Universe,Universal Pictures,Pe...        United States   
901   Revelations Entertainment,Latitude Entertainme...        United States   
985   Will Packer Productions,Practical Pictures,Uni...        United States   
1002  Focus Features,Ocean Blue Entertainment,1492 P...        United States   

     released_in_india_2nd_check production_budget_bins  \
474                           no                25m-50m   
649                           no                25m-50m   
654                           no                50m-75m   
698                           no                50m-75m   
827                           no                25m-50m   
901                           no                no info   
985                           no               100k-25m   
1002                          no               100k-25m   

     domestic_box_office_bins            director       genres_imdb_final  \
474                 150m-200m  Sam Taylor-Johnson  drama,romance,thriller   
649                 100m-150m      Malcolm D. Lee            comedy,drama   
654                 100m-150m         James Foley  drama,romance,thriller   
698                 100m-150m         James Foley           drama,romance   
827                  50m-100m    

In [15]:
all_big_studio_divisions = []

for key, value in studio_dict.items():
    all_big_studio_divisions.extend(value)

In [16]:
len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(all_big_studio_divisions)), na=False, regex=True)) &
                                        (master_list_df_reconstituted_again['released_in_india_2nd_check'] == 'yes')])

436

In [17]:
len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(all_big_studio_divisions)), na=False, regex=True)) &
                                        (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

53

In [18]:
len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(all_big_studio_divisions)), na=False, regex=True))])

489

In [19]:
len(master_list_df_reconstituted_again.loc[~(master_list_df_reconstituted_again['production_companies'].str.contains(('|'.join(all_big_studio_divisions)), na=False, regex=True))])

516

In [20]:
len(master_list_df_reconstituted_again)

1005

In [101]:
def not_released_number(categoryx, binx):

    for key, value in studio_dict.items():

        category_name = key

        division_list = value 

        master_list_df_reconstituted_again_dupli = master_list_df_reconstituted_again

        movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli['production_companies']\
                                                                                                            .str.contains(('|'.join(division_list)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again_dupli[categoryx] == binx) ])

        print('For the "{}" studio cluster, the number of movies in the {} range of {} which were not released in India is {}'.format(key,binx,categoryx,movies_in_category_name_total_released_india_no))
        

not_released_number('domestic_box_office_bins','50m-100m')

For the "disney" studio cluster, the number of movies in the 50m-100m range of domestic_box_office_bins which were not released in India is 0
For the "time_warner" studio cluster, the number of movies in the 50m-100m range of domestic_box_office_bins which were not released in India is 0
For the "21st_century_fox" studio cluster, the number of movies in the 50m-100m range of domestic_box_office_bins which were not released in India is 0
For the "nbc_universal" studio cluster, the number of movies in the 50m-100m range of domestic_box_office_bins which were not released in India is 1
For the "sony" studio cluster, the number of movies in the 50m-100m range of domestic_box_office_bins which were not released in India is 2
For the "viacom" studio cluster, the number of movies in the 50m-100m range of domestic_box_office_bins which were not released in India is 0
For the "lionsgate" studio cluster, the number of movies in the 50m-100m range of domestic_box_office_bins which were not releas

In [102]:
division_listx = studio_dict["lionsgate"]

master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli['production_companies']\
                                                                                                            .str.contains(('|'.join(division_listx)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again_dupli['domestic_box_office_bins'] == '50m-100m') ]

number  year                            title  domestic_box_office  \
796     5175  2018               I Can Only Imagine             83482352   
827     2952  2016     Neighbors 2: Sorority Rising             55340730   
922     5340  2018                        Overboard             50316123   
999       96  2013         Tyler Perry's Temptation             51975354   
1013      97  2013  Tyler Perry's A Madea Christmas             52543354   

      production_budget domestic_release_date  domestic_distributor  \
796             7000000            2018-03-16  Roadside Attractions   
827            35000000            2016-05-20             Universal   
922            12000000            2018-05-04             Lionsgate   
999                   0            2013-03-29             Lionsgate   
1013           25000000            2013-12-13             Lionsgate   

     mpaa_rating  franchise               source   ...     \
796           PG        NaN        Based on Song   ...      
827            R  Neighbors  Original Screenplay   ...      
922        PG-13        NaN               Remake   ...      
999        PG-13        NaN        Based on Play   ...      
1013       PG-13      Madea        Based on Play   ...      

             creative_type                               production_companies  \
796          Dramatization  Lionsgate,Erwin Brothers Entertainment,South W...   
827   Contemporary Fiction  Point Grey,Good Universe,Universal Pictures,Pe...   
922   Contemporary Fiction  Pantelion Films,Metro-Goldwyn-Mayer Pictures,3...   
999   Contemporary Fiction                              Lionsgate,TPS Company   
1013  Contemporary Fiction                      Lionsgate,Tyler Perry Studios   

     production_countries released_in_india_2nd_check production_budget_bins  \
796         United States                          no               100k-25m   
827         United States                          no                25m-50m   
922         United States                          no               100k-25m   
999         United States                          no                no info   
1013        United States                          no                25m-50m   

     domestic_box_office_bins                director       genres_imdb_final  \
796                  50m-100m  Andrew Erwin,Jon Erwin  biography,drama,family   
827                  50m-100m        Nicholas Stoller                  comedy   
922                  50m-100m           Rob Greenberg          comedy,romance   
999                  50m-100m             Tyler Perry          drama,thriller   
1013                 50m-100m             Tyler Perry            comedy,drama   

                        languages_imdb  id_imdb  
796                            English  6450186  
827                            English  4438848  
922   English,Norwegian,Spanish,French  1563742  
999                            English  2070862  
1013                           English  2609758  

[5 rows x 22 columns]

In [103]:
division_listx = studio_dict["sony"]

master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli['production_companies']\
                                                                                                            .str.contains(('|'.join(division_listx)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again_dupli['domestic_box_office_bins'] == '50m-100m') ]

number  year                 title  domestic_box_office  \
657     1805  2015              War Room             67790117   
1033     867  2014  Think Like a Man Too             65028687   

      production_budget domestic_release_date domestic_distributor  \
657             3000000            2015-08-28        Sony Pictures   
1033           24000000            2014-06-20        Sony Pictures   

     mpaa_rating         franchise                         source   ...     \
657           PG               NaN            Original Screenplay   ...      
1033       PG-13  Think Like a Man  Based on Factual Book/Article   ...      

             creative_type                               production_companies  \
657   Contemporary Fiction  Tri-Star Pictures,Faithstep Films,Provident Fi...   
1033  Contemporary Fiction  Screen Gems,LStar Capital,Will Packer Productions   

     production_countries released_in_india_2nd_check production_budget_bins  \
657         United States                          no               100k-25m   
1033        United States                          no               100k-25m   

     domestic_box_office_bins                  director genres_imdb_final  \
657                  50m-100m             Alex Kendrick             drama   
1033                 50m-100m  Tim Story,Keith Merryman    comedy,romance   

     languages_imdb  id_imdb  
657         English  3832914  
1033        English  2239832  

[2 rows x 22 columns]

In [13]:
division_listx = studio_dict["nbc_universal"]

master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_companies']\
                                                                                                            .str.contains(('|'.join(division_listx)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again['domestic_box_office_bins'] == '50m-100m') ]

number  year                         title  domestic_box_office  \
782    2952  2016  Neighbors 2: Sorority Rising             55340730   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
782           35000000            2016-05-20            Universal           R   

     franchise               source   ...            creative_type  \
782  Neighbors  Original Screenplay   ...     Contemporary Fiction   

                                  production_companies production_countries  \
782  Point Grey,Good Universe,Universal Pictures,Pe...        United States   

    released_in_india_2nd_check production_budget_bins  \
782                          no                25m-50m   

    domestic_box_office_bins          director genres_imdb_final  \
782                 50m-100m  Nicholas Stoller            comedy   

    languages_imdb  id_imdb  
782        English  4438848  

[1 rows x 22 columns]

In [104]:
not_released_number('domestic_box_office_bins','100m-150m')

For the "disney" studio cluster, the number of movies in the 100m-150m range of domestic_box_office_bins which were not released in India is 0
For the "time_warner" studio cluster, the number of movies in the 100m-150m range of domestic_box_office_bins which were not released in India is 0
For the "21st_century_fox" studio cluster, the number of movies in the 100m-150m range of domestic_box_office_bins which were not released in India is 0
For the "nbc_universal" studio cluster, the number of movies in the 100m-150m range of domestic_box_office_bins which were not released in India is 3
For the "sony" studio cluster, the number of movies in the 100m-150m range of domestic_box_office_bins which were not released in India is 0
For the "viacom" studio cluster, the number of movies in the 100m-150m range of domestic_box_office_bins which were not released in India is 0
For the "lionsgate" studio cluster, the number of movies in the 100m-150m range of domestic_box_office_bins which were not

In [105]:
division_listx = studio_dict["nbc_universal"]

master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli['production_companies']\
                                                                                                            .str.contains(('|'.join(division_listx)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again_dupli['domestic_box_office_bins'] == '100m-150m') ]

number  year                title  domestic_box_office  \
649    3906  2017           Girls Trip            115108515   
654    5119  2018   Fifty Shades Freed            100407760   
698    3880  2017  Fifty Shades Darker            114434010   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
649           28000000            2017-07-21            Universal           R   
654           55000000            2018-02-09            Universal           R   
698           55000000            2017-02-10            Universal           R   

                franchise                             source   ...     \
649                   NaN                Original Screenplay   ...      
654  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      
698  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      

            creative_type                               production_companies  \
649  Contemporary Fiction  Will Packer Productions,Universal Pictures,Per...   
654  Contemporary Fiction  Michael De Luca,Universal Pictures,Perfect Wor...   
698  Contemporary Fiction  Universal Pictures,Perfect World Pictures,Mich...   

    production_countries released_in_india_2nd_check production_budget_bins  \
649        United States                          no                25m-50m   
654        United States                          no                50m-75m   
698        United States                          no                50m-75m   

    domestic_box_office_bins        director       genres_imdb_final  \
649                100m-150m  Malcolm D. Lee            comedy,drama   
654                100m-150m     James Foley  drama,romance,thriller   
698                100m-150m     James Foley           drama,romance   

    languages_imdb  id_imdb  
649        English  3564472  
654        English  4477536  
698        English  4465564  

[3 rows x 22 columns]

In [106]:
not_released_number('production_budget_bins','50m-75m')

For the "disney" studio cluster, the number of movies in the 50m-75m range of production_budget_bins which were not released in India is 0
For the "time_warner" studio cluster, the number of movies in the 50m-75m range of production_budget_bins which were not released in India is 0
For the "21st_century_fox" studio cluster, the number of movies in the 50m-75m range of production_budget_bins which were not released in India is 0
For the "nbc_universal" studio cluster, the number of movies in the 50m-75m range of production_budget_bins which were not released in India is 2
For the "sony" studio cluster, the number of movies in the 50m-75m range of production_budget_bins which were not released in India is 0
For the "viacom" studio cluster, the number of movies in the 50m-75m range of production_budget_bins which were not released in India is 0
For the "lionsgate" studio cluster, the number of movies in the 50m-75m range of production_budget_bins which were not released in India is 0


In [107]:
division_listx = studio_dict["nbc_universal"]

master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli['production_companies']\
                                                                                                            .str.contains(('|'.join(division_listx)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again_dupli['production_budget_bins'] == '50m-75m') ]

number  year                title  domestic_box_office  \
654    5119  2018   Fifty Shades Freed            100407760   
698    3880  2017  Fifty Shades Darker            114434010   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
654           55000000            2018-02-09            Universal           R   
698           55000000            2017-02-10            Universal           R   

                franchise                             source   ...     \
654  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      
698  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      

            creative_type                               production_companies  \
654  Contemporary Fiction  Michael De Luca,Universal Pictures,Perfect Wor...   
698  Contemporary Fiction  Universal Pictures,Perfect World Pictures,Mich...   

    production_countries released_in_india_2nd_check production_budget_bins  \
654        United States                          no                50m-75m   
698        United States                          no                50m-75m   

    domestic_box_office_bins     director       genres_imdb_final  \
654                100m-150m  James Foley  drama,romance,thriller   
698                100m-150m  James Foley           drama,romance   

    languages_imdb  id_imdb  
654        English  4477536  
698        English  4465564  

[2 rows x 22 columns]

In [108]:
not_released_number('production_budget_bins','25m-50m')

For the "disney" studio cluster, the number of movies in the 25m-50m range of production_budget_bins which were not released in India is 0
For the "time_warner" studio cluster, the number of movies in the 25m-50m range of production_budget_bins which were not released in India is 0
For the "21st_century_fox" studio cluster, the number of movies in the 25m-50m range of production_budget_bins which were not released in India is 0
For the "nbc_universal" studio cluster, the number of movies in the 25m-50m range of production_budget_bins which were not released in India is 3
For the "sony" studio cluster, the number of movies in the 25m-50m range of production_budget_bins which were not released in India is 0
For the "viacom" studio cluster, the number of movies in the 25m-50m range of production_budget_bins which were not released in India is 0
For the "lionsgate" studio cluster, the number of movies in the 25m-50m range of production_budget_bins which were not released in India is 2


In [109]:
division_listx = studio_dict["nbc_universal"]

master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli['production_companies']\
                                                                                                            .str.contains(('|'.join(division_listx)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again_dupli['production_budget_bins'] == '25m-50m') ]

number  year                         title  domestic_box_office  \
474    1746  2015          Fifty Shades of Grey            166167230   
649    3906  2017                    Girls Trip            115108515   
827    2952  2016  Neighbors 2: Sorority Rising             55340730   

     production_budget domestic_release_date domestic_distributor mpaa_rating  \
474           40000000            2015-02-13            Universal           R   
649           28000000            2017-07-21            Universal           R   
827           35000000            2016-05-20            Universal           R   

                franchise                             source   ...     \
474  Fifty Shades of Grey  Based on Fiction Book/Short Story   ...      
649                   NaN                Original Screenplay   ...      
827             Neighbors                Original Screenplay   ...      

            creative_type                               production_companies  \
474  Contemporary Fiction  Focus Features,Michael De Luca,Trigger Street ...   
649  Contemporary Fiction  Will Packer Productions,Universal Pictures,Per...   
827  Contemporary Fiction  Point Grey,Good Universe,Universal Pictures,Pe...   

    production_countries released_in_india_2nd_check production_budget_bins  \
474        United States                          no                25m-50m   
649        United States                          no                25m-50m   
827        United States                          no                25m-50m   

    domestic_box_office_bins            director       genres_imdb_final  \
474                150m-200m  Sam Taylor-Johnson  drama,romance,thriller   
649                100m-150m      Malcolm D. Lee            comedy,drama   
827                 50m-100m    Nicholas Stoller                  comedy   

    languages_imdb  id_imdb  
474        English  2322441  
649        English  3564472  
827        English  4438848  

[3 rows x 22 columns]

In [110]:
division_listx = studio_dict["lionsgate"]

master_list_df_reconstituted_again_dupli.loc[(master_list_df_reconstituted_again_dupli['production_companies']\
                                                                                                            .str.contains(('|'.join(division_listx)), na=False, regex=True)) &
                                                                                                            (master_list_df_reconstituted_again_dupli['released_in_india_2nd_check'] != 'yes') &
                                                                                                            (master_list_df_reconstituted_again_dupli['production_budget_bins'] == '25m-50m') ]

number  year                            title  domestic_box_office  \
827     2952  2016     Neighbors 2: Sorority Rising             55340730   
1013      97  2013  Tyler Perry's A Madea Christmas             52543354   

      production_budget domestic_release_date domestic_distributor  \
827            35000000            2016-05-20            Universal   
1013           25000000            2013-12-13            Lionsgate   

     mpaa_rating  franchise               source   ...     \
827            R  Neighbors  Original Screenplay   ...      
1013       PG-13      Madea        Based on Play   ...      

             creative_type                               production_companies  \
827   Contemporary Fiction  Point Grey,Good Universe,Universal Pictures,Pe...   
1013  Contemporary Fiction                      Lionsgate,Tyler Perry Studios   

     production_countries released_in_india_2nd_check production_budget_bins  \
827         United States                          no                25m-50m   
1013        United States                          no                25m-50m   

     domestic_box_office_bins          director genres_imdb_final  \
827                  50m-100m  Nicholas Stoller            comedy   
1013                 50m-100m       Tyler Perry      comedy,drama   

     languages_imdb  id_imdb  
827         English  4438848  
1013        English  2609758  

[2 rows x 22 columns]

In [6]:
#-- do a list for critically appreciated movies, either movies that have done well at film festivals, or that have won oscars or indepedent spirit awards
#since there's just 48 movies, just checked the csv manually instead of through code

#looking at the independent spirit awards, 48 movies with best feature, director or screenplay nominations from 2014 to 2018. 18 of those 48 were never released in India. That's around 38 percent 
#Put another way, 2 out of 5 critically acclaimed independent American movies (from our selection of 48 movies) never found their way to an Indian screen
#note that "call me by your name" had censorship concerns

#history of winners from https://s3.amazonaws.com/SA_SubForm_etc/2018_SA_NomsWinners_040218.pdf 

#find out how many of them had major studio backing in some form
    #find out which production companies these were

import pandas as pd

indy_award_nominees_df = pd.read_csv('data/independent_spirit_awards_nominees_2014_2018.csv')
indy_award_nominees_df.head()

year             title                      nominee released_in_india
0  2014  12 Years A Slave                 best_feature               yes
1  2014       All Is Lost                 best_feature               yes
2  2014   Before Midnight  best_director_or_screenplay               yes
3  2014      Blue Jasmine  best_director_or_screenplay               yes
4  2014       Enough Said  best_director_or_screenplay                no

In [8]:
studio_dict = {
    
    "disney": ["Walt Disney Pictures","Walt Disney Animation Studios","Disney Nature","DisneyToon Studios","Disney-Pixar","Marvel Studios","Lucasfilm","Touchstone Pictures","A&E Indiefilms"],
    
    "time_warner": ["Warner Bros.","Warner Animation Group","New Line Cinema","DC Films","DC Comics","Castle Rock Entertainment","CNN Films","HBO Films","HBO Documentary Films","Flagship Entertainment"],

    "21st_century_fox": ["Fox Searchlight Pictures","Twentieth Century Fox","20th Century Fox Animation","Fox International Productions","20th Century Fox","Fox 2000 Pictures","Blue Sky Studios",
                        "Regency Enterprises","New Regency"],
    
    "nbc_universal": ["Focus Features","Universal Pictures","Gramercy Pictures","Working Title Films","Bullwinkle Studios","DreamWorks Animation","Illumination Entertainment","Focus World","Oriental DreamWorks"],
    
    "sony": ["Sony Pictures Classics","Columbia Pictures","Sony Pictures","Sony Pictures Animation","Screen Gems","Affirm Films","Stage 6 Films","Tri-Star Pictures"],
    
    "viacom": ["Paramount Vantage","Paramount Pictures","Nickelodeon Films","MTV Films","Awesomeness Films","BET Films"],
    
    "lionsgate": ["Roadside Attractions","Lionsgate","Codeblack Films","Good Universe","Pantelion Films","Summit Entertainment","Summit Premiere"]
}


distributor_dict = {
    
    "disney": ["Walt Disney"],
    
    "time_warner": ["Warner Bros."],

    "21st_century_fox": ["Fox Searchlight","20th Century Fox"],
    
    "nbc_universal": ["Focus Features","Universal","Gramercy"],
    
    "sony": ["Sony Pictures Classics","Sony Pictures"],
    
    "viacom": ["Paramount Pictures"],
    
    "lionsgate": ["Roadside Attractions","Lionsgate","Codeblack Entertainment"]
}

In [9]:
from fuzzywuzzy import fuzz

import pprint

pp = pprint.PrettyPrinter(indent=4)

division_count = {
    
    "disney": {'total': 0, 'released':0,'not_released':0},
    
    "time_warner": {'total': 0, 'released':0,'not_released':0},

    "21st_century_fox": {'total': 0, 'released':0,'not_released':0},
    
    "nbc_universal": {'total': 0, 'released':0,'not_released':0},
    
    "sony": {'total': 0, 'released':0,'not_released':0},
    
    "viacom": {'total': 0, 'released':0,'not_released':0},
    
    "lionsgate": {'total': 0, 'released':0,'not_released':0}
}

scraped_data_df = pd.read_csv('data/scraped_data.csv', converters={'number': str})

for index,row in indy_award_nominees_df.iterrows():
    
    title = row['title']
    print('\n')
    print(title)
    year = row['year']
    year = int(year)
    year_list = [year-2, year-1, year]
    released_in_india = row['released_in_india']
    
    for indexx, rowx in master_list_df_reconstituted_again.iterrows():
        titlex = rowx['title']
        yearx = rowx['year']
        yearx = int(yearx)
        
        production_companies = rowx['production_companies']
        
        if ((fuzz.token_sort_ratio(title, titlex) >= 85) and (yearx in year_list)):
            
            print("possible match for title '{}' from indy nominee list is '{}' from master list".format(title,titlex))
            
            for key, value in studio_dict.items():
                
                group_name = key
                
                division_list = value  
    
                if str(production_companies) != 'nan':
                
                    if any(x in production_companies for x in division_list):
                        
                        print('division of {} movie studio involved in title {}'.format(group_name,title))
                        
                        division_count[group_name]['total'] += 1

                        if released_in_india == 'yes':

                            division_count[group_name]['released'] += 1

                        else:

                            division_count[group_name]['not_released'] += 1
#                     else:
#                         print('no divisions of {} movie studio involved in title "{}"'.format(group_name,title))
                else:
                    
                    print('no production companies for title "{}" from indy nominee list'.format(title))
                    
            break
        
        else:
            
            continue
    
print('\n')
pp.pprint(division_count)
print('\n')
print('done and done')



12 Years A Slave
possible match for title '12 Years A Slave' from indy nominee list is '12 Years a Slave' from master list
division of 21st_century_fox movie studio involved in title 12 Years A Slave


All Is Lost
possible match for title 'All Is Lost' from indy nominee list is 'All is Lost' from master list
division of lionsgate movie studio involved in title All Is Lost


Before Midnight
possible match for title 'Before Midnight' from indy nominee list is 'Before Midnight' from master list
division of time_warner movie studio involved in title Before Midnight


Blue Jasmine
possible match for title 'Blue Jasmine' from indy nominee list is 'Blue Jasmine' from master list
division of sony movie studio involved in title Blue Jasmine


Enough Said
possible match for title 'Enough Said' from indy nominee list is 'Enough Said' from master list


Frances Ha
possible match for title 'Frances Ha' from indy nominee list is 'Frances Ha' from master list


Inside Llewyn Davis
possible match fo

In [10]:
from fuzzywuzzy import fuzz

import pprint

pp = pprint.PrettyPrinter(indent=4)

division_count = {
    
    "disney": {'total': 0, 'released':0,'not_released':0},
    
    "time_warner": {'total': 0, 'released':0,'not_released':0},

    "21st_century_fox": {'total': 0, 'released':0,'not_released':0},
    
    "nbc_universal": {'total': 0, 'released':0,'not_released':0},
    
    "sony": {'total': 0, 'released':0,'not_released':0},
    
    "viacom": {'total': 0, 'released':0,'not_released':0},
    
    "lionsgate": {'total': 0, 'released':0,'not_released':0}
}

scraped_data_df = pd.read_csv('data/scraped_data.csv', converters={'number': str})

for index,row in indy_award_nominees_df.iterrows():
    
    title = row['title']
    print('\n')
    print(title)
    year = row['year']
    year = int(year)
    year_list = [year-2, year-1, year]
    released_in_india = row['released_in_india']
    
    for indexx, rowx in scraped_data_df.iterrows():
        titlex = rowx['title']
        yearx = rowx['year']
        yearx = int(yearx)
        
        production_companies = rowx['production_companies']
        
        if ((fuzz.token_sort_ratio(title, titlex) >= 85) and (yearx in year_list)):
            
            print("possible match for title '{}' from indy nominee list is '{}' from master list".format(title,titlex))
            
            for key, value in studio_dict.items():
                
                group_name = key
                
                division_list = value  
    
                if str(production_companies) != 'nan':
                
                    if any(x in production_companies for x in division_list):
                        
                        print('division of {} movie studio involved in title {}'.format(group_name,title))
                        
                        division_count[group_name]['total'] += 1

                        if released_in_india == 'yes':

                            division_count[group_name]['released'] += 1

                        else:

                            division_count[group_name]['not_released'] += 1
#                     else:
#                         print('no divisions of {} movie studio involved in title "{}"'.format(group_name,title))
                else:
                    
                    print('no production companies for title "{}" from indy nominee list'.format(title))
                    
            break
        
        else:
            
            continue
    
print('\n')
pp.pprint(division_count)
print('\n')
print('done and done')



12 Years A Slave
possible match for title '12 Years A Slave' from indy nominee list is '12 Years a Slave' from master list
division of 21st_century_fox movie studio involved in title 12 Years A Slave


All Is Lost
possible match for title 'All Is Lost' from indy nominee list is 'All is Lost' from master list
division of lionsgate movie studio involved in title All Is Lost


Before Midnight
possible match for title 'Before Midnight' from indy nominee list is 'Before Midnight' from master list
division of time_warner movie studio involved in title Before Midnight


Blue Jasmine
possible match for title 'Blue Jasmine' from indy nominee list is 'Blue Jasmine' from master list
division of sony movie studio involved in title Blue Jasmine


Enough Said
possible match for title 'Enough Said' from indy nominee list is 'Enough Said' from master list


Frances Ha
possible match for title 'Frances Ha' from indy nominee list is 'Frances Ha' from master list


Inside Llewyn Davis
possible match fo

In [11]:
from fuzzywuzzy import fuzz

import pprint

pp = pprint.PrettyPrinter(indent=4)

division_count = {

    "disney": {'total': 0, 'released':0,'not_released':0},

    "time_warner": {'total': 0, 'released':0,'not_released':0},

    "21st_century_fox": {'total': 0, 'released':0,'not_released':0},

    "nbc_universal": {'total': 0, 'released':0,'not_released':0},

    "sony": {'total': 0, 'released':0,'not_released':0},

    "viacom": {'total': 0, 'released':0,'not_released':0},

    "lionsgate": {'total': 0, 'released':0,'not_released':0}
}

scraped_data_df = pd.read_csv('data/scraped_data.csv', converters={'number': str})

for index,row in indy_award_nominees_df.iterrows():

    title = row['title']
    print('\n')
    print(title)
    year = row['year']
    year = int(year)
    year_list = [year-2, year-1, year]
    released_in_india = row['released_in_india']

    for indexx, rowx in scraped_data_df.iterrows():
        titlex = rowx['title']
        yearx = rowx['year']
        yearx = int(yearx)

        domestic_distributor = rowx['domestic_distributor']

        if ((fuzz.token_sort_ratio(title, titlex) >= 85) and (yearx in year_list)):

            print("possible match for title '{}' from indy nominee list is '{}' from master list".format(title,titlex))
            
            indy_award_nominees_df.loc[index,'domestic_distributor'] = domestic_distributor

            for key, value in distributor_dict.items():

                group_name = key

                division_list = value

                if str(domestic_distributor) != 'nan':

                    if any(x in domestic_distributor for x in division_list):

                        print('division of {} movie studio involved in distribution of title "{}"'.format(group_name,title))
                        
                        indy_award_nominees_df.loc[index,'domestic_distributor'] = group_name

                        division_count[group_name]['total'] += 1

                        if released_in_india == 'yes':

                            division_count[group_name]['released'] += 1

                        else:

                            division_count[group_name]['not_released'] += 1

                        break
                        
                    else:
                        
                        continue
                        
                else:

                    print('no us distributors for title "{}" from indy nominee list'.format(title))

            break

        else:

            continue

print('\n')
pp.pprint(division_count)
print('\n')

indy_award_nominees_df.to_csv('data/independent_spirit_awards_nominees_with_distributor.csv', index=False)

print('done and done')



12 Years A Slave
possible match for title '12 Years A Slave' from indy nominee list is '12 Years a Slave' from master list
division of 21st_century_fox movie studio involved in distribution of title "12 Years A Slave"


All Is Lost
possible match for title 'All Is Lost' from indy nominee list is 'All is Lost' from master list
division of lionsgate movie studio involved in distribution of title "All Is Lost"


Before Midnight
possible match for title 'Before Midnight' from indy nominee list is 'Before Midnight' from master list
division of sony movie studio involved in distribution of title "Before Midnight"


Blue Jasmine
possible match for title 'Blue Jasmine' from indy nominee list is 'Blue Jasmine' from master list
division of sony movie studio involved in distribution of title "Blue Jasmine"


Enough Said
possible match for title 'Enough Said' from indy nominee list is 'Enough Said' from master list
division of 21st_century_fox movie studio involved in distribution of title "Enou

In [12]:
len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_2nd_check'] == 'yes'])

784

In [13]:
len(master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes'])

221

In [27]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_2nd_check'] == 'yes'].groupby('genre').size()

genre
Action               128
Adventure            118
Black Comedy          14
Comedy               112
Drama                208
Horror                59
Multiple Genres        1
Musical               11
Romantic Comedy       23
Thriller/Suspense    102
Western                8
dtype: int64

In [14]:
master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes'].groupby('genre').size()

genre
Action                 4
Adventure              5
Black Comedy           4
Comedy                49
Drama                120
Horror                 6
Multiple Genres        1
Musical                1
Romantic Comedy       11
Thriller/Suspense     19
Western                1
dtype: int64

In [15]:
master_list_df_reconstituted_again.dtypes

number                          int64
year                            int64
title                          object
domestic_box_office             int64
production_budget               int64
domestic_release_date          object
domestic_distributor           object
mpaa_rating                    object
franchise                      object
source                         object
genre                          object
production_method              object
creative_type                  object
production_companies           object
production_countries           object
released_in_india_2nd_check    object
production_budget_bins         object
domestic_box_office_bins       object
director                       object
genres_imdb_final              object
languages_imdb                 object
id_imdb                         int64
dtype: object

In [ ]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_final'] == 'music')&
                                      (master_list_df_reconstituted_again['domestic_box_office_bins'])]

In [17]:
master_list_df_reconstituted_again['domestic_box_office_bins'].unique()

array(['150m-200m', '50k-50m', '200m-250m', '300m-350m', '50m-100m',
       '100m-150m', '500m-550m', '650m-700m', '250m-300m', '400m-450m',
       '350m-400m', '450m-500m', '600m-650m', '700m-750m', '900m-950m'], dtype=object)

In [23]:
for binx in master_list_df_reconstituted_again['domestic_box_office_bins'].unique():
    lengthx = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_final'].str.contains('music', na=False, regex=False))&
                                      (master_list_df_reconstituted_again['domestic_box_office_bins']==binx) &
                                        (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])
    
    print('for binx {}, number of movies not released in music genre is {}'.format(binx,lengthx))    

for binx 150m-200m, number of movies not released in music genre is 0
for binx 50k-50m, number of movies not released in music genre is 16
for binx 200m-250m, number of movies not released in music genre is 0
for binx 300m-350m, number of movies not released in music genre is 0
for binx 50m-100m, number of movies not released in music genre is 0
for binx 100m-150m, number of movies not released in music genre is 0
for binx 500m-550m, number of movies not released in music genre is 0
for binx 650m-700m, number of movies not released in music genre is 0
for binx 250m-300m, number of movies not released in music genre is 0
for binx 400m-450m, number of movies not released in music genre is 0
for binx 350m-400m, number of movies not released in music genre is 0
for binx 450m-500m, number of movies not released in music genre is 0
for binx 600m-650m, number of movies not released in music genre is 0
for binx 700m-750m, number of movies not released in music genre is 0
for binx 900m-950m, nu

In [24]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_final'].str.contains('music', na=False, regex=False))&
                                        (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')].sort_values('domestic_box_office',ascending=False)

number  year               title  domestic_box_office  production_budget  \
895    5068  2018     Forever My Girl             16376066            3500000   
765     923  2014   Beyond the Lights             14618727            7000000   
635    1866  2015        Love & Mercy             12551031                  0   
986    5586  2018       Juliet, Naked              3423155                  0   
716     166  2013         Filly Brown              2850357            1250000   
694     951  2014       The Identical              2827666                  0   
625    3062  2016         Miles Ahead              2610896                  0   
691    5441  2018    Hearts Beat Loud              2386254            2000000   
623    4025  2017       Brad's Status              2133158                  0   
797     143  2013     Unfinished Song              1698952                  0   
874    3096  2016     I Saw the Light              1646788                  0   
800    5192  2018   Finding Your Feet              1418682                  0   
802     985  2014            The Song              1005691                  0   
698    4059  2017         Patti Cake$               800148            1000000   
881    3087  2016     Born to Be Blue               755153                  0   
648    3127  2016  Saturday's Warrior               744046                  0   

    domestic_release_date    domestic_distributor mpaa_rating franchise  \
895            2018-01-19    Roadside Attractions          PG       NaN   
765            2014-11-14              Relativity       PG-13       NaN   
635            2015-06-05    Roadside Attractions       PG-13       NaN   
986            2018-08-17    Roadside Attractions           R       NaN   
716            2013-04-19               Lionsgate           R       NaN   
694            2014-09-05     Freestyle Releasing          PG       NaN   
625            2016-04-01  Sony Pictures Classics           R       NaN   
691            2018-06-08         Gunpowder & Sky       PG-13       NaN   
623            2017-09-15      Annapurna Pictures           R       NaN   
797            2013-06-21           Weinstein Co.       PG-13       NaN   
874            2016-03-25  Sony Pictures Classics           R       NaN   
800            2018-03-30    Roadside Attractions       PG-13       NaN   
802            2014-09-26    Samuel Goldwyn Films       PG-13       NaN   
698            2017-08-18         Fox Searchlight           R       NaN   
881            2016-03-04               IFC Films           R       NaN   
648            2016-04-01     Purdie Distribution          PG       NaN   

                                source   ...            creative_type  \
895  Based on Fiction Book/Short Story   ...     Contemporary Fiction   
765                Original Screenplay   ...     Contemporary Fiction   
635          Based on Real Life Events   ...            Dramatization   
986  Based on Fiction Book/Short Story   ...     Contemporary Fiction   
716                Original Screenplay   ...     Contemporary Fiction   
694                Original Screenplay   ...       Historical Fiction   
625          Based on Real Life Events   ...            Dramatization   
691                Original Screenplay   ...     Contemporary Fiction   
623                Original Screenplay   ...     Contemporary Fiction   
797                Original Screenplay   ...     Contemporary Fiction   
874      Based on Factual Book/Article   ...            Dramatization   
800                Original Screenplay   ...     Contemporary Fiction   
802                Original Screenplay   ...     Contemporary Fiction   
698                Original Screenplay   ...     Contemporary Fiction   
881          Based on Real Life Events   ...            Dramatization   
648          Based on Musical or Opera   ...     Contemporary Fiction   

                                  production_companies  \
895             LD Entertainment,Liddell Entertainm

In [26]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_final'].str.contains('sport', na=False, regex=False))&
                                        (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')].sort_values('domestic_box_office', ascending=False)

number  year               title  domestic_box_office  production_budget  \
945    1867  2015            Woodlawn             14394097           13000000   
879    5265  2018  The Miracle Season             10230620                  0   
937     168  2013            Home Run              2859955            1200000   
791    1924  2015     My All-American              2246000           20000000   
838    3091  2016             Greater              2000093            9000000   
889    4049  2017        Slamma Jamma              1687000                  0   
630    3137  2016          The Bronze               615816            3500000   
715    1005  2014            23 Blast               549185            1000000   

    domestic_release_date     domestic_distributor mpaa_rating franchise  \
945            2015-10-16  Pure Flix Entertainment          PG       NaN   
879            2018-04-06         LD Entertainment          PG       NaN   
937            2013-04-19     Samuel Goldwyn Films       PG-13       NaN   
791            2015-11-13    Clarius Entertainment          PG       NaN   
838            2016-08-26    Hammond Entertainment          PG       NaN   
889            2017-03-24                Riverrain          PG       NaN   
630            2016-03-18   Sony Pictures Classics           R       NaN   
715            2014-10-24         Abramorama Films       PG-13       NaN   

                            source   ...            creative_type  \
945      Based on Real Life Events   ...            Dramatization   
879      Based on Real Life Events   ...            Dramatization   
937            Original Screenplay   ...     Contemporary Fiction   
791  Based on Factual Book/Article   ...            Dramatization   
838      Based on Real Life Events   ...            Dramatization   
889            Original Screenplay   ...     Contemporary Fiction   
630            Original Screenplay   ...     Contemporary Fiction   
715            Original Screenplay   ...     Contemporary Fiction   

                                  production_companies production_countries  \
945                          Pure Flix,Provident Films        United States   
879                                   LD Entertainment        United States   
937                Impact Productions,Hero Productions        United States   
791  Clarius Entertainment,Anthem Ventures,Anthem P...        United States   
838  Hammond Entertainment LLC,Greater Productions LLC        United States   
889                                                NaN        United States   
630                     Duplass Brothers,Stage 6 Films        United States   
715                                                NaN        United States   

    released_in_india_2nd_check production_budget_bins  \
945                          no               100k-25m   
879                          no                no info   
937                          no               100k-25m   
791                          no               100k-25m   
838                          no               100k-25m   
889                          no                no info   
630                          no               100k-25m   
715                          no               100k-25m   

    domestic_box_office_bins                               director  \
945                  50k-50m  The Erwin Brothers,The Erwin Brothers   
879                  50k-50m                          Sean McNamara   
937                  50k-50m                             David Boyd   
791                  50k-50m                           Angelo Pizzo   
838                  50k-50m                             David Hunt   
889                  50k-50m                        Timothy A. Chey   
630                  50k-50m                          Bryan Buckley   
715                  50k-50m                            Dylan Baker   

          genres_imdb_final languages_imdb  id_imdb  
945             drama,sport        Engl

In [28]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_final'].str.contains('romance', na=False, regex=False))&
                                        (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')].sort_values('domestic_box_office', ascending=False)

number  year                               title  domestic_box_office  \
466    1746  2015                Fifty Shades of Grey            166167230   
677    3880  2017                 Fifty Shades Darker            114434010   
641    5119  2018                  Fifty Shades Freed            100407760   
966     867  2014                Think Like a Man Too             65028687   
868    5340  2018                           Overboard             50316123   
779    1829  2015                    Love the Coopers             26302731   
828     906  2014                            Top Five             25317379   
740     121  2013                         Enough Said             17550872   
895    5068  2018                     Forever My Girl             16376066   
898     917  2014                      And So It Goes             15160801   
765     923  2014                   Beyond the Lights             14618727   
885    3027  2016             Hello, My Name is Doris             14444999   
834     898  2014              Magic in the Moonlight             10534510   
859    3036  2016                   The Perfect Match              9669521   
673     149  2013                 The Spectacular Now              6852971   
745    5124  2018                           Every Day              6112914   
639     940  2014                  The Skeleton Twins              5284309   
683     943  2014                   Dear White People              4404154   
785     157  2013              Much Ado About Nothing              4328850   
845    4014  2017                            The Hero              4077333   
720     142  2013                          Frances Ha              4067398   
812     936  2014                         My Old Lady              4011530   
950    1886  2015                   Learning to Drive              3447633   
872    3049  2016                       Maggie's Plan              3351735   
666     948  2014                       Obvious Child              3122616   
649    3996  2017                         Tulip Fever              2455635   
672     958  2014                     Love is Strange              2262555   
741     947  2014                  Words and Pictures              2171257   
871     935  2014                       The Immigrant              2013456   
964    1937  2015                       Old Fashioned              1914090   
697    4041  2017                       A Ghost Story              1594798   
762    1929  2015               Infinitely Polar Bear              1430655   
829     159  2013                  Thanks for Sharing              1066256   
688    4017  2017   Film Stars Don't Die in Liverpool              1024266   
772    1954  2015                       Big Stone Gap              1009984   
802     985  2014                            The Song              1005691   
985    5590  2018    The Miseducation of Cameron Post               905111   
901     987  2014  The Disappearance of Eleanor Rigby               587152   
927     186  2013                       To the Wonder               584563   
804    4075  2017                      Tommy's Honour               569306   
711    1939  2015                            Freeheld               546201   
850    1003  2014                      The One I Love               511635   

     production_budget domestic_release_date            domestic_distributor  \
466           40000000            2015-02-13                       Universal   
677           55000000            2017-02-10                       Universal   
641           55000000            2018-02-09                       Universal   
966           24000000            2014-06-20                   Sony Pictures   
868           12000000            2018-05-04                       Lionsgate   
779           18000000            2015-11-13                       CBS Films   
828           12000000            2014-12-12              Paramount Pictures   
740       

In [31]:
master_list_df_reconstituted_again.sort_values('domestic_box_office', ascending=False)

number  year                                              title  \
972    1736  2015               Star Wars Ep. VII: The Force Awakens   
457    5117  2018                                      Black Panther   
184    5257  2018                             Avengers: Infinity War   
67     1737  2015                                     Jurassic World   
864    3857  2017                  Star Wars Ep. VIII: The Last Jedi   
359    5427  2018                                      Incredibles 2   
593    2887  2016                       Rogue One: A Star Wars Story   
60     3858  2017                               Beauty and the Beast   
529    2888  2016                                       Finding Dory   
298    1739  2015                            Avengers: Age of Ultron   
323       5  2013                    The Hunger Games: Catching Fire   
539    5428  2018                     Jurassic World: Fallen Kingdom   
281    3865  2017                                       Wonder Woman   
521       2  2013                                         Iron Man 3   
141    2886  2016                         Captain America: Civil War   
410    3861  2017                     Jumanji: Welcome to the Jungle   
171       1  2013                                             Frozen   
292    3863  2017                      Guardians of the Galaxy Vol 2   
453    2891  2016                            The Secret Life of Pets   
437       3  2013                                    Despicable Me 2   
391    2890  2016                                    The Jungle Book   
355    2894  2016                                           Deadpool   
241    1742  2015                                         Inside Out   
618    1738  2015                                          Furious 7   
806     799  2014                                    American Sniper   
431    2889  2016                                           Zootopia   
111     790  2014              The Hunger Games: Mockingjay - Part 1   
137    1740  2015                                            Minions   
463    3862  2017                             Spider-Man: Homecoming   
597     789  2014                            Guardians of the Galaxy   
414    2892  2016                 Batman v Superman: Dawn of Justice   
321    3868  2017                                                 It   
6      2895  2016                                      Suicide Squad   
511    5336  2018                                         Deadpool 2   
556    3864  2017                                     Thor: Ragnarok   
185       9  2013                                       Man of Steel   
562    1745  2015              The Hunger Games: Mockingjay - Part 2   
203       8  2013                                            Gravity   
455    2898  2016                                               Sing   
84        7  2013                                Monsters University   
473    3860  2017                                    Despicable Me 3   
126     793  2014                Captain America: The Winter Soldier   
260       4  2013                The Hobbit: The Desolation of Smaug   
518     803  2014                                     The Lego Movie   
320     788  2014          The Hobbit: The Battle of the Five Armies   
239    2897  2016                                              Moana   
587     787  2014                    Transformers: Age of Extinction   
155     791  2014                                         Maleficent   
616       6  2013                                 Fast and Furious 6   
368      13  2013                          Oz the Great and Powerful   
590    2893  2016            Fantastic Beasts and Where to Find Them   
165     792  2014                         X-Men: Days of Future Past   
24     2896  2016                                     Doctor Strange   
229    3869  2017                                     Justice League   
300      14  2013                            

In [32]:
master_list_df_reconstituted_again['production_budget_bins'].unique()

array(['225m-250m', '100k-25m', '175m-200m', '100m-125m', 'no info',
       '50m-75m', '125m-150m', '25m-50m', '150m-175m', '75m-100m',
       '200m-225m', '250m-275m', '275m-300m', '300m-325m', '325m-350m'], dtype=object)

In [34]:
len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['production_budget_bins'] != 'no info')
                                           #&
#                                         (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')
                                      ])

753

In [111]:
master_list_df_reconstituted_again_yes = master_list_df_reconstituted_again[master_list_df_reconstituted_again['released_in_india_2nd_check'] == 'yes']

In [112]:
master_list_df_reconstituted_again_yes.to_csv('data/india_releases_yes_manual_check.csv', index=False)

In [6]:
from imdb import IMDb

with open('passwords_ignore.txt') as f:
    password = f.readline()

login_string = 'postgresql://postgres:' + password + '@localhost/imdb2'

ia = IMDb('s3', login_string, adultSearch=False)

In [16]:
resultsx  = ia.search_movie("Inconvenient Sequel",results = 30)

resultsx

[<Movie id:179239[s3] title:_L'inconveniente (None)_>,
 <Movie id:7529858[s3] title:_An Inconvenient Special (None)_>,
 <Movie id:4990898[s3] title:_El Inconveniente (None)_>,
 <Movie id:1664121[s3] title:_Inconvenient Truths (None)_>,
 <Movie id:1655563[s3] title:_An Inconvenient Egg (None)_>,
 <Movie id:1013982[s3] title:_An Inconvenient Lie (None)_>,
 <Movie id:497512[s3] title:_Inconvenience Store (None)_>,
 <Movie id:8355272[s3] title:_An Inconvenient Answer (None)_>,
 <Movie id:1428564[s3] title:_In Convenience (None)_>,
 <Movie id:805551[s3] title:_In Convenience (None)_>,
 <Movie id:165831[s3] title:_Inconvenienced (None)_>,
 <Movie id:8466576[s3] title:_An Inconvenient Ruth (None)_>,
 <Movie id:5031442[s3] title:_An Inconvenient Stay (None)_>,
 <Movie id:3141888[s3] title:_An Inconvenient Fish (None)_>,
 <Movie id:1391471[s3] title:_An Inconvenient Game (None)_>,
 <Movie id:1248130[s3] title:_An Inconvenient Head (None)_>,
 <Movie id:1283287[s3] title:_An Inconvenient Penguin 

In [7]:
moviez = ia.get_movie('4700756')
moviez['kind']

'movie'

In [10]:
moviez['genres']

['drama']

In [1]:
import pandas as pd

scraped_data_df = pd.read_csv('data/scraped_data.csv', converters={'number': str})

In [2]:
scraped_data_df.dtypes

number                      object
year                         int64
title                       object
domestic_box_office          int64
international_box_office     int64
production_budget            int64
domestic_release_date       object
domestic_distributor        object
mpaa_rating                 object
franchise                   object
source                      object
genre                       object
production_method           object
creative_type               object
production_companies        object
production_countries        object
dtype: object

In [5]:
len(scraped_data_df[scraped_data_df['domestic_box_office']>500000])

1077

In [1]:
from imdb import IMDb
from random import randint
import time

ib = IMDb(accessSystem = 'http', adultSearch = False)



In [4]:
movie_http = ib.get_movie('5013056')

In [5]:
movie_http['genres']

['Action', 'Drama', 'History', 'Thriller', 'War']

In [7]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v16.csv')

In [8]:
from imdb import IMDb
from random import randint
import time

ib = IMDb(accessSystem = 'http', adultSearch = False)

for index, row in master_list_df_reconstituted_again.iterrows():
    
    number = row['number']
    id_imdb = row['id_imdb']
    id_imdb = str(id_imdb)
    print(number)

    try:
        movie_http = ib.get_movie(id_imdb)

        delay = randint(6,9)
        time.sleep(delay)

        genres_raw = movie_http['genres']
        genres_imdb = ','.join(genres_raw)

        master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb_extended'] = genres_imdb
    
    except:
        print('error for page number {}'.format(number))

master_list_df_reconstituted_again.to_csv('data/india_release_check_v17.csv', index=False)

print('done and done')

3867
164
12
1834
851
3023
2895
3986
3074
217
3899
2927
837
3918
1786
2994
2903
1798
3104
2991
800
173
868
908
2896
5344
874
4015
5177
72
2987
1777
5503
5118
902
39
52
1753
69
2905
830
1877
40
2906
22
833
18
3874
3014
103
130
160
2936
2956
129


2018-11-01 16:09:25,347 CRITICAL [imdbpy] /home/shijith/anaconda3/lib/python3.6/site-packages/imdb/_exceptions.py:34: IMDbDataAccessError exception raised; args: ({'errcode': None, 'errmsg': 'None', 'url': 'http://www.imdb.com/title/tt1814621/plotsummary', 'proxy': '', 'exception type': 'IOError', 'original exception': URLError(gaierror(-2, 'Name or service not known'),)},); kwds: {}
Traceback (most recent call last):
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py", line 1318, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1239, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1285, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1234, in endheaders
    self._send_output(message_body, encode_chu

3007
3100
797
176
3992
3858
3037
2977
3024


2018-11-01 16:12:18,796 CRITICAL [imdbpy] /home/shijith/anaconda3/lib/python3.6/site-packages/imdb/_exceptions.py:34: IMDbDataAccessError exception raised; args: ({'errcode': None, 'errmsg': 'None', 'url': 'http://www.imdb.com/title/tt1374989/plotsummary', 'proxy': '', 'exception type': 'IOError', 'original exception': URLError(gaierror(-2, 'Name or service not known'),)},); kwds: {}
Traceback (most recent call last):
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py", line 1318, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1239, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1285, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1234, in endheaders
    self._send_output(message_body, encode_chu

102
3907
1781
1737
2911
2935
2899
98
191
2909
1856
3953
68
3003


...

error for page number 1878
3894


2018-11-01 20:23:07,562 CRITICAL [imdbpy] /home/shijith/anaconda3/lib/python3.6/site-packages/imdb/_exceptions.py:34: IMDbDataAccessError exception raised; args: ({'errcode': None, 'errmsg': 'None', 'url': 'http://www.imdb.com/title/tt1753383/reference', 'proxy': '', 'exception type': 'IOError', 'original exception': URLError(timeout('timed out',),)},); kwds: {}
Traceback (most recent call last):
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py", line 1318, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1239, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1285, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1234, in endheaders
    self._send_output(message_body, encode_chunked=encode_chunked)
 

error for page number 3894
5264
121
947
123
5179
832
5124
4009
42
170
2962
5443
1827
982
1871
5266
818
5175
2934
1898
1852
169
894
1929
3929
3092
923
1970
3988
3998
3914
5346
1944
1954
3917
5516
1820
1780
920
100
1829
4032
911
2952
3931
3925
157
3936
3963
5512
3021
5505
1924
3013
928
66
3025
48
143
4029
162
5192
1759
985
3957
4075
919
799
2913
187
3017
79
94
936
978
938
43
1808
2914
931
846
4056
4046
2999
128
3001
2912
4020
3020
906
159
1779
3920
4031
2946
898
974
3000
1791
3091
3011
51
3068
5191
997
2910
4014
3040
3089
3050
1910
1003
1960
4091
3896
3009
1981
839
5513
4051
3036
953
140
1969
3989
3857
1863
1833
99
5340
3990
86
935
3049
1841
3096
3898
1870
1948
5267
5265
58
3087
1887
5269
32
3027
877
1894
1782
4049
3897
215
995
76
971
5068
5440


2018-11-01 21:09:57,823 CRITICAL [imdbpy] /home/shijith/anaconda3/lib/python3.6/site-packages/imdb/_exceptions.py:34: IMDbDataAccessError exception raised; args: ({'errcode': None, 'errmsg': 'None', 'url': 'http://www.imdb.com/title/tt6212478/reference', 'proxy': '', 'exception type': 'IOError', 'original exception': URLError(gaierror(-2, 'Name or service not known'),)},); kwds: {}
Traceback (most recent call last):
  File "/home/shijith/anaconda3/lib/python3.6/urllib/request.py", line 1318, in do_open
    encode_chunked=req.has_header('Transfer-encoding'))
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1239, in request
    self._send_request(method, url, body, headers, encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1285, in _send_request
    self.endheaders(body, encode_chunked=encode_chunked)
  File "/home/shijith/anaconda3/lib/python3.6/http/client.py", line 1234, in endheaders
    self._send_output(message_body, encode_chunk

error for page number 5440
2918
917
5514
980
987
5511
1764
3070
3979
189
1838
3051
3078
4021
1952
3902
993
3044
3901
950
932
1904
1799
1909
179
3048
925
175
5341
3005
186
2969
3975
2925
35
1748
54
1918
3955
3937
168
96
1874
80
3046
91
1975
163
1867
968
1762
5345
5348
1886
5437
97
2995
1821
5342
1985
3933
1941
836
135
17
3120
3072
1937
5429
867
921
104
850
3019
903
1736
2982
3943
4035
1835
2949
4008
3923
880
197
4050
5583
5574
5590
5586
5567
5569
5580
5568
5591
5579
5570
5582
5571
5593
5581
5578
5585
5575
5573
5576
5572
5577
done and done


In [6]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v18.csv')

master_list_df_reconstituted_again.head()

number  year                                             title  \
0    3867  2017  Pirates of the Caribbean: Dead Men Tell No Tales   
1     164  2013                                          The East   
2      12  2013                                       World War Z   
3    1834  2015                               Ricki and the Flash   
4     851  2014                                     Transcendence   

   domestic_box_office  production_budget domestic_release_date  \
0            172558876          230000000            2017-05-26   
1              2274649            6500000            2013-05-31   
2            202359711          190000000            2013-06-21   
3             26839498           18000000            2015-08-07   
4             23022309          100000000            2014-04-18   

  domestic_distributor mpaa_rating                 franchise  \
0          Walt Disney       PG-13  Pirates of the Caribbean   
1      Fox Searchlight       PG-13                       NaN   
2   Paramount Pictures       PG-13               World War Z   
3        Sony Pictures       PG-13                       NaN   
4         Warner Bros.       PG-13                       NaN   

                              source                   ...                     \
0           Based on Theme Park Ride                   ...                      
1                Original Screenplay                   ...                      
2  Based on Fiction Book/Short Story                   ...                      
3                Original Screenplay                   ...                      
4                Original Screenplay                   ...                      

                                production_companies production_countries  \
0             Walt Disney Pictures,Jerry Bruckheimer        United States   
1                                   Scott Free Films        United States   
2  Skydance Productions,Hemisphere Media Capital,...        United States   
3  Marc Platt Productions,Badwill Entertainment ,...        United States   
4                Straight Up Films,DMG Entertainment        United States   

  released_in_india_2nd_check production_budget_bins domestic_box_office_bins  \
0                         yes              225m-250m                150m-200m   
1                         yes               100k-25m                  50k-50m   
2                         yes              175m-200m                200m-250m   
3                         yes               100k-25m                  50k-50m   
4                         yes              100m-125m                  50k-50m   

                        director         genres_imdb_final  \
0  Joachim Ronnin,Espen Sandberg  action,adventure,fantasy   
1                 Zal Batmanglij  adventure,drama,thriller   
2                   Marc Forster   action,adventure,horror   
3                 Jonathan Demme        comedy,drama,music   
4                  Wally Pfister     drama,mystery,romance   

                   languages_imdb  id_imdb  \
0                 English,Spanish  1790809   
1  English,American Sign Language  1869716   
2   English,Spanish,Hebrew,Arabic   816711   
3                         English  3623726   
4                         English  2209764   

                      genres_imdb_extended  
0                 Action,Adventure,Fantasy  
1                 Adventure,Drama,Thriller  
2  Action,Adventure,Horror,Sci-Fi,Thriller  
3                       Comedy,Drama,Music  
4    Drama,Mystery,Romance,Sci-Fi,Thriller  

[5 rows x 23 columns]

In [7]:
#note that the languages from the http website are capitalised

master_list_df_reconstituted_again['genres_imdb_extended'].isnull().sum().sum()

1

In [8]:
from imdb import IMDb
from random import randint
import time

ib = IMDb(accessSystem = 'http', adultSearch = False)

for index, row in master_list_df_reconstituted_again.iterrows():
    
    genres_ext_value = row['genres_imdb_extended']
    
    if str(genres_ext_value) == 'nan':

        number = row['number']
        id_imdb = row['id_imdb']
        id_imdb = str(id_imdb)
        print(number)

        try:
            movie_http = ib.get_movie(id_imdb)

            delay = randint(6,9)
            time.sleep(delay)

            genres_raw = movie_http['genres']
            genres_imdb = ','.join(genres_raw)

            master_list_df_reconstituted_again.loc[master_list_df_reconstituted_again['number'] == number,'genres_imdb_extended'] = genres_imdb

        except:
            print('error for page number {}'.format(number))
    
    else:
        continue

master_list_df_reconstituted_again.to_csv('data/india_release_check_v19.csv', index=False)

print('done and done')

2937
done and done


In [ ]:
import pandas as pd

master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v19.csv')

master_list_df_reconstituted_again.head()

In [9]:
genres_imdb_list = list(master_list_df_reconstituted_again['genres_imdb_extended'].unique())
print(len(genres_imdb_list))
genres_imdb_list = [x for x in genres_imdb_list if str(x) != 'nan']
final_list = []
for genres_imdb in genres_imdb_list:
    list_to_add = [x.strip() for x in genres_imdb.split(",")]
    final_list.extend(list_to_add)
    
final_list = list(set(final_list))
print(len(final_list))

329
20


In [10]:
#movies from which genre do we get to see the least in India?

category = 'genres_imdb_extended'

df = pd.DataFrame(columns=["category", '2013','2014','2015','2016','2017','2018','total not','total','2013 %','2014 %','2015 %','2016 %','2017 %','2018 %','total not %'])

for category_name in final_list:
    
    df = df.append({"category": category_name,
                    '2013': None,
                    '2014': None,
                    '2015':None,
                    '2016':None,
                    '2017':None,
                    '2018':None,
                    'total not':None,
                    'total':None,
                    '2013 %':None,
                    '2014 %':None,
                    '2015 %':None,
                    '2016 %':None,
                    '2017 %':None,
                    '2018 %':None,
                    'total not %':None
                    }, ignore_index=True)
    
    movies_in_category_name_total_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False)) &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')])

    movies_in_category_name_total = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False))])

    movies_in_category_name_total_released_india_no_percent = (movies_in_category_name_total_released_india_no/movies_in_category_name_total)*100
    movies_in_category_name_total_released_india_no_percent = round(movies_in_category_name_total_released_india_no_percent,1)
    
    df.loc[df['category'] == category_name, "total"] = int(movies_in_category_name_total)
    df.loc[df['category'] == category_name, "total not" ] = int(movies_in_category_name_total_released_india_no)
    df.loc[df['category'] == category_name, 'total not %' ] = movies_in_category_name_total_released_india_no_percent

    for year in range(2013,2019):
        
        year_string = str(year)
        
        year_percent_string = str(year) + ' %'
        
        movies_in_category_name_released_india_no = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False))  &
                                                                            (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes') &
                                                                            (master_list_df_reconstituted_again['year'] == year)])

        movies_in_category_name = len(master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again[category].str.contains(category_name, na=False, regex=False)) &
                                                                                       (master_list_df_reconstituted_again['year'] == year) ])
        if movies_in_category_name != 0:
            movies_in_category_name_released_india_no_percent = (movies_in_category_name_released_india_no/movies_in_category_name)*100
            movies_in_category_name_released_india_no_percent = round(movies_in_category_name_released_india_no_percent,1)
            
            df.loc[df['category'] == category_name, year_string ] = movies_in_category_name_released_india_no
            df.loc[df['category'] == category_name, year_percent_string ] = movies_in_category_name_released_india_no_percent
            
df.sort_values('total not %',ascending=False)

#you should have a caveat that these are all the movies that earned at least $500,000 at the US box office

category 2013 2014 2015 2016 2017 2018 total not total 2013 % 2014 %  \
18    Romance    7   16    8    8    7    8        54   169   26.9     40   
6       Drama   24   29   32   18   40   34       177   570   26.4   29.9   
9       Sport    1    1    2    2    2    1         9    32     20   16.7   
7       Music    2    3    1    4    2    5        17    63     25     20   
5     History    2    1    3    1    3    4        14    53     50   16.7   
3   Biography    1    2    6    8    8    5        30   117    6.2   11.8   
0      Comedy   12   14   14   15   14   18        87   362   20.3   24.1   
15        War    3    1    1    0    1    2         8    35     60   11.1   
11    Western    0    1    0    0    0    1         2    11      0     50   
4       Crime    4    1    1    4    4   11        25   160   11.8    4.2   
2    Thriller   10    5    4    3    7   11        40   305   16.4   10.9   
10     Family    1    1    3    2    2    4        13   114    5.6    4.5   
8     Mystery    1    3    2    0    4    3        13   116    9.1   13.6   
13     Horror    1    3    1    3    4    0        12   109    6.7   18.8   
12     Action    3    4    2    6    1    4        20   286    6.4    8.5   
19    Fantasy    2    1    1    1    1    2         8   137      8    4.3   
17  Animation    0    0    0    3    0    1         4    71      0      0   
14     Sci-Fi    1    3    0    2    0    2         8   157    3.8   10.7   
16    Musical    0    0    0    1    0    0         1    21      0      0   
1   Adventure    1    1    2    0    1    3         8   242    2.5    2.4   

   2015 % 2016 % 2017 % 2018 % total not %  
18   25.8   23.5   31.8     50          32  
6    28.1     18   36.4   58.6        31.1  
9      25   33.3     40     50        28.1  
7     8.3   33.3     25   62.5          27  
5    21.4    7.1     30     80        26.4  
3      24   33.3     32     50        25.6  
0    20.9   19.7     23   43.9          24  
15     25      0   14.3   66.7        22.9  
11      0      0      0    100        18.2  
4     3.8   15.4   15.4   45.8        15.6  
2     7.8    5.6     13   28.2        13.1  
10   15.8    8.3   10.5   33.3        11.4  
8       8      0   17.4   18.8        11.2  
13    5.6   11.1     19      0          11  
12    4.5    9.1    2.3   10.5           7  
19      5    3.2    3.8   16.7         5.8  
17      0   15.8      0   12.5         5.6  
14      0    6.9      0    9.1         5.1  
16      0     20      0      0         4.8  
1     4.9      0    2.6   11.5         3.3

In [ ]:
#are there some tags that appear more often for movies? Have a feeling certain tages like 'drama' get overused and get penalised because so much gets put under it

In [16]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_extended'].str.contains('Sport', na=False, regex=False)) &
                                      (master_list_df_reconstituted_again['released_in_india_2nd_check'] != 'yes')].sort_values('domestic_box_office',ascending=False)

number  year               title  domestic_box_office  production_budget  \
945    1867  2015            Woodlawn             14394097           13000000   
879    5265  2018  The Miracle Season             10230620                  0   
937     168  2013            Home Run              2859955            1200000   
791    1924  2015     My All-American              2246000           20000000   
838    3091  2016             Greater              2000093            9000000   
889    4049  2017        Slamma Jamma              1687000                  0   
630    3137  2016          The Bronze               615816            3500000   
804    4075  2017      Tommy's Honour               569306                  0   
715    1005  2014            23 Blast               549185            1000000   

    domestic_release_date     domestic_distributor mpaa_rating franchise  \
945            2015-10-16  Pure Flix Entertainment          PG       NaN   
879            2018-04-06         LD Entertainment          PG       NaN   
937            2013-04-19     Samuel Goldwyn Films       PG-13       NaN   
791            2015-11-13    Clarius Entertainment          PG       NaN   
838            2016-08-26    Hammond Entertainment          PG       NaN   
889            2017-03-24                Riverrain          PG       NaN   
630            2016-03-18   Sony Pictures Classics           R       NaN   
804            2017-04-14     Roadside Attractions          PG       NaN   
715            2014-10-24         Abramorama Films       PG-13       NaN   

                            source              ...                \
945      Based on Real Life Events              ...                 
879      Based on Real Life Events              ...                 
937            Original Screenplay              ...                 
791  Based on Factual Book/Article              ...                 
838      Based on Real Life Events              ...                 
889            Original Screenplay              ...                 
630            Original Screenplay              ...                 
804  Based on Factual Book/Article              ...                 
715            Original Screenplay              ...                 

                                  production_companies production_countries  \
945                          Pure Flix,Provident Films        United States   
879                                   LD Entertainment        United States   
937                Impact Productions,Hero Productions        United States   
791  Clarius Entertainment,Anthem Ventures,Anthem P...        United States   
838  Hammond Entertainment LLC,Greater Productions LLC        United States   
889                                                NaN        United States   
630                     Duplass Brothers,Stage 6 Films        United States   
804  Gutta Percha Productions,Creative Scotland,Tim...        United States   
715                                                NaN        United States   

    released_in_india_2nd_check production_budget_bins  \
945                          no               100k-25m   
879                          no                no info   
937                          no               100k-25m   
791                          no               100k-25m   
838                          no               100k-25m   
889                          no                no info   
630                          no               100k-25m   
804                          no                no info   
715                          no               100k-25m   

    domestic_box_office_bins                               director  \
945                  50k-50m  The Erwin Brothers,The Erwin Brothers   
879                  50k-50m                          Sean McNamara   
937                  50k-50m                             David Boyd   
791                  50k-50m                           Angelo Pizzo   
838            

In [12]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_extended'].str.contains('Drama', na=False, regex=False))].sort_values('domestic_box_office',ascending=False)

number  year                               title  domestic_box_office  \
391    2890  2016                     The Jungle Book            364001123   
241    1742  2015                          Inside Out            356461711   
806     799  2014                     American Sniper            350126372   
321    3868  2017                                  It            327481748   
203       8  2013                             Gravity            274092705   
345    1744  2015                         The Martian            228433663   
428    3870  2017                               Logan            226277068   
57      797  2014                          Big Hero 6            222527828   
250     794  2014      Dawn of the Planet of the Apes            208545589   
394    1747  2015                          Cinderella            201151353   
47     3874  2017                             Dunkirk            190068280   
537    5258  2018                       A Quiet Place            188024361   
216     796  2014                        Interstellar            188017894   
932    1748  2015                        The Revenant            183637894   
570    3878  2017                The Greatest Showman            174340174   
661    2920  2016                      Hidden Figures            169607287   
337     806  2014                           Gone Girl            167767189   
466    1746  2015                Fifty Shades of Grey            166167230   
445    1769  2015              Straight Outta Compton            161197785   
299    1751  2015                         San Andreas            155190832   
420    2902  2016                          La La Land            151101803   
884      32  2013                     American Hustle            150117807   
121    3875  2017      War for the Planet of the Apes            146880162   
389      20  2013                    The Great Gatsby            144840419   
525      45  2013                      Identity Thief            134506920   
343    3885  2017                              Wonder            132422809   
288     825  2014                      Into the Woods            128002372   
446    2907  2016                The Legend of Tarzan            126643061   
840      51  2013                       Lone Survivor            125095601   
191    2919  2016                               Sully            125070033   
..      ...   ...                                 ...                  ...   
624    5442  2018               The Catcher Was A Spy               714205   
946     968  2014             Men, Women and Children               705908   
764    3092  2016                          Little Men               702537   
851    1960  2015                           Tangerine               702354   
750    5443  2018                          Boundaries               701828   
108    3131  2016                          Mr. Church               685780   
843     997  2014                   A Matter of Faith               680113   
996    5593  2018                               Blaze               674373   
862    1969  2015                         The D Train               669688   
458    3082  2016                      American Honey               663247   
542    4080  2017                              Wilson               653951   
855    1981  2015      The Stanford Prison Experiment               649690   
397     185  2013                            Parkland               641439   
956    1985  2015                       Welcome to Me               625727   
821    4046  2017     The Only Living Boy in New York               624332   
766    1970  2015         Kumiko, The Treasure Hunter               623383   
630    3137  2016                          The Bronze               615816   
901     987  2014  The Disappearance of Eleanor Rigby               587152   
927     186  2013                       To the Wonder               584563   
852    4091  2017          

In [11]:
master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['genres_imdb_extended'].str.contains('Drama', na=False, regex=False))].sort_values('domestic_box_office',ascending=False)

number  year                               title  domestic_box_office  \
391    2890  2016                     The Jungle Book            364001123   
241    1742  2015                          Inside Out            356461711   
806     799  2014                     American Sniper            350126372   
321    3868  2017                                  It            327481748   
203       8  2013                             Gravity            274092705   
345    1744  2015                         The Martian            228433663   
428    3870  2017                               Logan            226277068   
57      797  2014                          Big Hero 6            222527828   
250     794  2014      Dawn of the Planet of the Apes            208545589   
394    1747  2015                          Cinderella            201151353   
47     3874  2017                             Dunkirk            190068280   
537    5258  2018                       A Quiet Place            188024361   
216     796  2014                        Interstellar            188017894   
932    1748  2015                        The Revenant            183637894   
570    3878  2017                The Greatest Showman            174340174   
661    2920  2016                      Hidden Figures            169607287   
337     806  2014                           Gone Girl            167767189   
466    1746  2015                Fifty Shades of Grey            166167230   
445    1769  2015              Straight Outta Compton            161197785   
299    1751  2015                         San Andreas            155190832   
420    2902  2016                          La La Land            151101803   
884      32  2013                     American Hustle            150117807   
121    3875  2017      War for the Planet of the Apes            146880162   
389      20  2013                    The Great Gatsby            144840419   
525      45  2013                      Identity Thief            134506920   
343    3885  2017                              Wonder            132422809   
288     825  2014                      Into the Woods            128002372   
446    2907  2016                The Legend of Tarzan            126643061   
840      51  2013                       Lone Survivor            125095601   
191    2919  2016                               Sully            125070033   
..      ...   ...                                 ...                  ...   
624    5442  2018               The Catcher Was A Spy               714205   
946     968  2014             Men, Women and Children               705908   
764    3092  2016                          Little Men               702537   
851    1960  2015                           Tangerine               702354   
750    5443  2018                          Boundaries               701828   
108    3131  2016                          Mr. Church               685780   
843     997  2014                   A Matter of Faith               680113   
996    5593  2018                               Blaze               674373   
862    1969  2015                         The D Train               669688   
458    3082  2016                      American Honey               663247   
542    4080  2017                              Wilson               653951   
855    1981  2015      The Stanford Prison Experiment               649690   
397     185  2013                            Parkland               641439   
956    1985  2015                       Welcome to Me               625727   
821    4046  2017     The Only Living Boy in New York               624332   
766    1970  2015         Kumiko, The Treasure Hunter               623383   
630    3137  2016                          The Bronze               615816   
901     987  2014  The Disappearance of Eleanor Rigby               587152   
927     186  2013                       To the Wonder               584563   
852    4091  2017          

In [17]:
master_list_df_reconstituted_again.dtypes

number                          int64
year                            int64
title                          object
domestic_box_office             int64
production_budget               int64
domestic_release_date          object
domestic_distributor           object
mpaa_rating                    object
franchise                      object
source                         object
genre                          object
production_method              object
creative_type                  object
production_companies           object
production_countries           object
released_in_india_2nd_check    object
production_budget_bins         object
domestic_box_office_bins       object
director                       object
genres_imdb_final              object
languages_imdb                 object
id_imdb                         int64
genres_imdb_extended           object
dtype: object

In [30]:
big_studio_list = ["Disney","Warner","Fox","Universal","Columbia","Sony","Paramount","Lionsgate"]

year_list = list(range(2013,2019))

df_list = []

for studiox in big_studio_list:
    
#     print(studiox)
    
    for year in year_list:
        
#         print(year)
        
        df_filtered = master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['year'] == year) &
                                        (master_list_df_reconstituted_again['production_companies'].str.contains(studiox, na=False, regex=False))]

        try:
            df_to_append = df_filtered.ix[df_filtered['domestic_box_office'].argmax()]

            df_list.append(df_to_append)
        except:
            continue

df_appended_complete = pd.concat(df_list, axis = 1)

# df_appended_complete.reset_index(drop=True,inplace=True)

df_appended_complete.T

/home/shijith/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:19: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated


number  year                                  title domestic_box_office  \
171      1  2013                                 Frozen           400738009   
57     797  2014                             Big Hero 6           222527828   
241   1742  2015                             Inside Out           356461711   
529   2888  2016                           Finding Dory           486295561   
864   3857  2017      Star Wars Ep. VIII: The Last Jedi           620181382   
359   5427  2018                          Incredibles 2           606354358   
185      9  2013                           Man of Steel           291045518   
518    803  2014                         The Lego Movie           257784718   
94    1772  2015                                  Creed           109767581   
414   2892  2016     Batman v Superman: Dawn of Justice           330360194   
281   3865  2017                           Wonder Woman           412563408   
990   5568  2018                      Crazy Rich Asians           171326596   
522     36  2013                               The Heat           159581587   
266    801  2014                                  Rio 2           131538435   
619   1761  2015                      The Peanuts Movie           130178411   
661   2920  2016                         Hidden Figures           169607287   
570   3878  2017                   The Greatest Showman           174340174   
511   5336  2018                             Deadpool 2           318482400   
437      3  2013                        Despicable Me 2           368065385   
67    1737  2015                         Jurassic World           652270625   
453   2891  2016                The Secret Life of Pets           368384330   
473   3860  2017                        Despicable Me 3           264624300   
539   5428  2018         Jurassic World: Fallen Kingdom           416573615   
884     32  2013                        American Hustle           150117807   
500    811  2014                         22 Jump Street           191719337   
408   1750  2015                   Hotel Transylvania 2           169700110   
496   2921  2016                           Ghostbusters           128350574   
410   3861  2017         Jumanji: Welcome to the Jungle           404508916   
790   5505  2018  Hotel Transylvania 3: Summer Vacation           166076985   
88      28  2013    Cloudy with a Chance of Meatballs 2           119793567   
331    926  2014                          The Interview             6105175   
408   1750  2015                   Hotel Transylvania 2           169700110   
625   3062  2016                            Miles Ahead             2610896   
418   3893  2017                        The Emoji Movie            86089513   
790   5505  2018  Hotel Transylvania 3: Summer Vacation           166076985   
521      2  2013                             Iron Man 3           408992272   
90     809  2014                                   Noah           101200044   
552   1743  2015       Mission: Impossible—Rogue Nation           195042377   
73    2909  2016                       Star Trek Beyond           158848340   
361   3871  2017          Transformers: The Last Knight           130168683   
32    5503  2018            Mission: Impossible—Fallout           218139667   
323      5  2013        The Hunger Games: Catching Fire           424668047   
111    790  2014  The Hunger Games: Mockingjay - Part 1           337135885   
562   1745  2015  The Hunger Games: Mockingjay - Part 2           281723902   
928   2969  2016   Tyler Perry's Boo! A Madea Halloween            73206343   
343   3885  2017                                 Wonder           132422809   
756   5175  2018                     I Can Only Imagine            83482352   

    production_budget domestic_release_date    domestic_distributor  \
171         150000000            2013-11-27             Walt Disney   
57          165000000            2014-11-07             Walt Disney  

In [31]:
big_distributor_list = ["Disney","Warner","Fox","Universal","Sony","Paramount","Lionsgate"]

year_list = list(range(2013,2019))

df_list = []

for distributorx in big_distributor_list:
    
#     print(studiox)
    
    for year in year_list:
        
#         print(year)
        
        df_filtered = master_list_df_reconstituted_again.loc[(master_list_df_reconstituted_again['year'] == year) &
                                        (master_list_df_reconstituted_again['domestic_distributor'].str.contains(distributorx, na=False, regex=False))]

        try:
            df_to_append = df_filtered.ix[df_filtered['domestic_box_office'].argmax()]

            df_list.append(df_to_append)
        except:
            continue

df_appended_complete = pd.concat(df_list, axis = 1)

# df_appended_complete.reset_index(drop=True,inplace=True)

df_appended_complete.T

/home/shijith/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:19: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated


number  year                                  title domestic_box_office  \
521      2  2013                             Iron Man 3           408992272   
597    789  2014                Guardians of the Galaxy           333172112   
972   1736  2015   Star Wars Ep. VII: The Force Awakens           936662225   
593   2887  2016           Rogue One: A Star Wars Story           532177324   
864   3857  2017      Star Wars Ep. VIII: The Last Jedi           620181382   
457   5117  2018                          Black Panther           700059566   
185      9  2013                           Man of Steel           291045518   
806    799  2014                        American Sniper           350126372   
299   1751  2015                            San Andreas           155190832   
414   2892  2016     Batman v Superman: Dawn of Justice           330360194   
281   3865  2017                           Wonder Woman           412563408   
990   5568  2018                      Crazy Rich Asians           171326596   
382     11  2013                             The Croods           187168425   
165    792  2014             X-Men: Days of Future Past           233921534   
345   1744  2015                            The Martian           228433663   
355   2894  2016                               Deadpool           363070709   
428   3870  2017                                  Logan           226277068   
511   5336  2018                             Deadpool 2           318482400   
437      3  2013                        Despicable Me 2           368065385   
319    815  2014                              Neighbors           150086800   
67    1737  2015                         Jurassic World           652270625   
453   2891  2016                The Secret Life of Pets           368384330   
473   3860  2017                        Despicable Me 3           264624300   
539   5428  2018         Jurassic World: Fallen Kingdom           416573615   
884     32  2013                        American Hustle           150117807   
498    795  2014               The Amazing Spider-Man 2           202853933   
186   1741  2015                                Spectre           200074175   
496   2921  2016                           Ghostbusters           128350574   
410   3861  2017         Jumanji: Welcome to the Jungle           404508916   
790   5505  2018  Hotel Transylvania 3: Summer Vacation           166076985   
300     14  2013                Star Trek Into Darkness           228778661   
587    787  2014        Transformers: Age of Extinction           245439076   
552   1743  2015       Mission: Impossible—Rogue Nation           195042377   
73    2909  2016                       Star Trek Beyond           158848340   
361   3871  2017          Transformers: The Last Knight           130168683   
32    5503  2018            Mission: Impossible—Fallout           218139667   
323      5  2013        The Hunger Games: Catching Fire           424668047   
111    790  2014  The Hunger Games: Mockingjay - Part 1           337135885   
562   1745  2015  The Hunger Games: Mockingjay - Part 2           281723902   
420   2902  2016                             La La Land           151101803   
343   3885  2017                                 Wonder           132422809   
868   5340  2018                              Overboard            50316123   

    production_budget domestic_release_date domestic_distributor mpaa_rating  \
521         200000000            2013-05-03          Walt Disney       PG-13   
597         170000000            2014-08-01          Walt Disney       PG-13   
972         306000000            2015-12-18          Walt Disney       PG-13   
593         200000000            2016-12-16          Walt Disney       PG-13   
864         317000000            2017-12-15          Walt Disney       PG-13   
457         200000000            2018-02-16          Walt Disney       PG-13   
185         225000000            2013-06-14   

In [30]:
import pandas as pd

distributor_dict = {
    
    "disney": ["Walt Disney"],
    
    "time_warner": ["Warner Bros."],

    "21st_century_fox": ["Fox Searchlight","20th Century Fox"],
    
    "nbc_universal": ["Focus Features","Universal","Gramercy"],
    
    "sony": ["Sony Pictures Classics","Sony Pictures"],
    
    "viacom": ["Paramount Pictures"],
    
    "lionsgate": ["Roadside Attractions","Lionsgate","Codeblack Entertainment"]
}


master_list_df_reconstituted_again = pd.read_csv('data/india_release_check_v19.csv')

master_list_df_reconstituted_again.head()

number  year                                             title  \
0    3867  2017  Pirates of the Caribbean: Dead Men Tell No Tales   
1     164  2013                                          The East   
2      12  2013                                       World War Z   
3    1834  2015                               Ricki and the Flash   
4     851  2014                                     Transcendence   

   domestic_box_office  production_budget domestic_release_date  \
0            172558876          230000000            2017-05-26   
1              2274649            6500000            2013-05-31   
2            202359711          190000000            2013-06-21   
3             26839498           18000000            2015-08-07   
4             23022309          100000000            2014-04-18   

  domestic_distributor mpaa_rating                 franchise  \
0          Walt Disney       PG-13  Pirates of the Caribbean   
1      Fox Searchlight       PG-13                       NaN   
2   Paramount Pictures       PG-13               World War Z   
3        Sony Pictures       PG-13                       NaN   
4         Warner Bros.       PG-13                       NaN   

                              source                   ...                     \
0           Based on Theme Park Ride                   ...                      
1                Original Screenplay                   ...                      
2  Based on Fiction Book/Short Story                   ...                      
3                Original Screenplay                   ...                      
4                Original Screenplay                   ...                      

                                production_companies production_countries  \
0             Walt Disney Pictures,Jerry Bruckheimer        United States   
1                                   Scott Free Films        United States   
2  Skydance Productions,Hemisphere Media Capital,...        United States   
3  Marc Platt Productions,Badwill Entertainment ,...        United States   
4                Straight Up Films,DMG Entertainment        United States   

  released_in_india_2nd_check production_budget_bins domestic_box_office_bins  \
0                         yes              225m-250m                150m-200m   
1                         yes               100k-25m                  50k-50m   
2                         yes              175m-200m                200m-250m   
3                         yes               100k-25m                  50k-50m   
4                         yes              100m-125m                  50k-50m   

                        director         genres_imdb_final  \
0  Joachim Ronnin,Espen Sandberg  action,adventure,fantasy   
1                 Zal Batmanglij  adventure,drama,thriller   
2                   Marc Forster   action,adventure,horror   
3                 Jonathan Demme        comedy,drama,music   
4                  Wally Pfister     drama,mystery,romance   

                   languages_imdb  id_imdb  \
0                 English,Spanish  1790809   
1  English,American Sign Language  1869716   
2   English,Spanish,Hebrew,Arabic   816711   
3                         English  3623726   
4                         English  2209764   

                      genres_imdb_extended  
0                 Action,Adventure,Fantasy  
1                 Adventure,Drama,Thriller  
2  Action,Adventure,Horror,Sci-Fi,Thriller  
3                       Comedy,Drama,Music  
4    Drama,Mystery,Romance,Sci-Fi,Thriller  

[5 rows x 23 columns]

In [31]:
import re

for index,row in master_list_df_reconstituted_again.iterrows():
    #numberx = row['number']
    #print(numberx)

    domestic_distributor_string = row['domestic_distributor']
    #print(domestic_distributor_string)

    if str(domestic_distributor_string) != 'nan':
        
        for key, value in distributor_dict.items():

            category_name = key

            division_list = value

            
            if any(i in domestic_distributor_string for i in division_list):
                

                distributor_us = category_name
                

                master_list_df_reconstituted_again.loc[index,'distributor_us'] = distributor_us
                
                break

            else:
                master_list_df_reconstituted_again.loc[index,'distributor_us'] = 'others'
                continue
        
        continue
        
    else:
        master_list_df_reconstituted_again.loc[index,'distributor_us'] = 'no_info'
        continue
        

master_list_df_reconstituted_again.to_csv('data/india_release_check_v20.csv', index=False)

print('DONE AND DONE')

DONE AND DONE


In [ ]:
#QUESTIONS, TO-DOs

#how do you deal with the problem of multiple genres

#of the movies that haven't been released, find if they've applied for CBFC certificates
    #if no certificate, does that mean we don't get to see it on netflix, amazon either?
    #make sure that the movies that werent released couldnt get released because of the censor board

#jave a section at the top of the jupyter notebook, with a summary/overview of what all steps were taken in collecting data and cleaning the dataset

In [ ]:
#NOTES FOR GITHUB METHODOLOGY SECTION

#when i am talking about domestic box office and domestic release date, the data is for the US and not India, just stuck to that labelling because that's the label used in the pages i scraped the data from
    #avoid any possible confusion while writing the code

#dont forget to mention bookmyshow list has all the english movies released in india, including those made in india. Just mention this in methodology notes


In [ ]:
#TAKEN CARE OF, DONE, NOT BOTHERING WITH

#should I change the minimum box office gross to $1 million? even the promotional release of the TV show inhumans got $500,000 in one day. My bar is too low.

#have a feeling my focus should shift from production companies to distributors, the official oscars pdf has the nominations categorised by us distributor not production company

#also fifty shades movies, were they released in India or not
#https://www.hindustantimes.com/hollywood/despite-cuts-censor-blocks-fifty-shades-of-grey-in-india/story-W88JEi3GStWxMAiJvjGpyH.html
#http://www.rediff.com/movies/report/fifty-shades-darker-banned-in-india/20170310.htm


#have a feeling a few non-English movies may have slipped through, but think I've cleaned the dataset the best I can
#if a froeign title has an english language title for the american market, cant do anything about it

#shouldn't you talk about how much money these movies could possibly make in India? No, that makes it a business story

#do a manual check of the bookmyshow list UPDATE: nah forget about it, the bookmyshow list even has indian english movies, no way I can keep out titles based on a glance

#do one with just the boutique divisions of major studios

#whatever happeneded to that inhumans theatrical realease? has that gotten into the list?

#get a csv of films marked with yes for released in India

#split the datasheet into two parts, one with just the documentaries and one without documentaries
#so one will be feature-length films and the other will be documentaries

#seems i got the str(director) as != 'nan' instead of == 'nan'

#see if you have taken care of the atlas shrugged and religous titles
#until i have definite proof that they haven't been released (proof in the form of news articles etc.) I've pretty much used the list of titles from bookmyshow as is

#leaving them in , have a feeling they may have never been released in India, dont remember any buzz about them 
#who knows there may have been parts of the country where they were released
#will give the bookmyshow list the benefit of the doubt
#i thought I would exclude movies that have 0 critic/user ratings/reviews on the bookmyshow website, but anchorman 2, a movie which i'm sure would have been released in India, has 0 critic/user ratings/reviews

#weed out movies that aren't movies

#should i have documentaries in my movie list 
#what do i do about documentaries?

#i think I will have to go row by row and remove things like the game of thrones Imax experience, mayweather vs. macgregor etc. it's only a 1000 rows you can do it
#exclude stand up specials like Kevin Hart as well

#also there's a batman: killing joke in there, how do we exclude them programatically? Answer is there isn't, at least not with the attributes and metadata available